# Project Five 
# Game of Thrones - Season Five

## Importing and Cleaning

In [1]:
import numpy as np
import pandas as pd
import nltk
from nltk.tag import pos_tag
from nltk.tokenize import word_tokenize
from nltk.tokenize import sent_tokenize
from textblob import TextBlob
from nltk.corpus import stopwords
from sklearn.feature_extraction.text import TfidfVectorizer, CountVectorizer
from sklearn.decomposition import NMF, LatentDirichletAllocation
import gensim
from nltk.tag import pos_tag
import re

Using Theano backend.


In [2]:
pd.set_option('display.max_columns', 125)
pd.set_option('display.max_rows', 125)

In [3]:
df_s5 = pd.read_json('/Users/zoemarkovits/Metis/project_five_got/scrape/season_five.json')

In [4]:
df_s5[['title','script_text']]

title  \
0           [The Wars to Come Script]   
1      [The House of Black and White]   
2               [High Sparrow Script]   
3          [Sons of the Harpy Script]   
4               [Kill the Boy Script]   
5  [Unbowed, Unbent, Unbroken Script]   
6                   [The Gift Script]   
7                   [Hardhome Script]   
8     [The Dance of Dragons (Script)]   
9             [Mother's Mercy Script]   

                                         script_text  
0  [\n, \n, EXT. WOODS, \n, \n, \n, \nMELARA: We ...  
1  [\n, \nBRAAVOSI MAN: In the old times, wheneve...  
2  [TITLE SEQUENCE, \n, \n, CUT TO: BRAAVOS, \n, ...  
3  [TITLE SEQUENCE, \n, \n, EXT. BEACH, \n, \n, \...  
4  [TITLE SEQUENCE, \n, \n, INT. ROOM, \n, \n, \n...  
5  [INT. HOUSE OF BLACK AND WHITE - CHAMBER, \n, ...  
6  [EXT. CASTLE BLACK, \n, \n, \n, \nJON: First R...  
7  [INT. MEEREEN - PYRAMID, \n, \nJORAH: Your Gra...  
8  [EXT. STANNIS’ CAMP - NIGHT, \n, \n, \n, \n, I...  
9  [INT. STANNIS’S CAMP - MELISANDRE’S TENT, \n, ...

In [5]:
df_s5['title'] = df_s5['title'].map(lambda x: str(x)[3:-2])

In [6]:
df_s5.title

0             The Wars to Come Script
1        The House of Black and White
2                 High Sparrow Script
3            Sons of the Harpy Script
4                 Kill the Boy Script
5    Unbowed, Unbent, Unbroken Script
6                     The Gift Script
7                     Hardhome Script
8       The Dance of Dragons (Script)
9               Mother's Mercy Script
Name: title, dtype: object

In [7]:
names5_01 = ['MELARA','CERSEI','MAGGY','PRIEST','JAIME','VARYS','TYRION','PROSTITUTE','WHITE RAT','DAENERYS',
             'BARRISTAN','MOSSADOR','GREY WORM','MISSANDEI','JON','OLLY','GILLY','SAM','ALLISER','MELISANDRE',
             'STANNIS','DAVOS','MASTER OF ARMS','YOHN ROYCE','BAELISH','ROYCE','SQUIRE','SANSA','PODRICK','BRIENNE',
             'LORAS','GRAND MAESTER PYRCELLE','LANCEL LANNISTER','LANCEL','KEVAN LANNISTER','KEVAN','OLYVAR',
             'MARGAERY','DAARIO NAHARIS','HIZDAHR ZO LORAQ','HIZDAHR','DAARIO','MANCE']

names5_02 = ['BRAAVOSI MAN','ARYA','MAN','OLD MAN','PODRICK','WAITRESS','SANSA','BAELISH','BRIENNE','GUARD','KNIGHT 1',
             'KNIGHT','JAIME','CERSEI','LOLLYS STOKEWORTH','BRONN','LOLLYS','TRYSTANE (O.S.)','AREO','ELLARIA',
             'DORAN','DAARIO (O.S.)','DAARIO','GREY WORM','MOSSADOR','DAENERYS','BARRISTAN','HIZDAHR','MOSSADOR',
             'TYRION','VARYS','MERYN','HUNTERS','QYBURN','KEVAN','MACE TYRELL','PYCELLE','MACE','SHIREEN','GILLY',
             'SAM','SELYSE (to Sam and Gilly):','SAM','SELYSE','STANNIS','JON','DAVOS','ALLISER','AEMON','JANOS',
             'MEN','SHADOW TOWER BROTHER','BROTHER','BROTHERS','JAQEN','HARPY (Valyrian)']

names5_03 = ['MAN','JAQEN','ARYA','MARGAERY & TOMMEN','TOMMEN','MARGAERY','CERSEI','ROOSE','RAMSAY','SANSA','BAELISH',
             'PODRICK','BRIENNE','STANNIS','JON','DAVOS','OLLY','WAIF','ROOSE','RAMSAY','WOMAN','SAM','JANOS',
             'OLYVAR','HIGH SEPTON','LANCEL','CROWD','MAN 1','MAN 2','QYBURN','MACE','PYCELLE','MERYN','MAN 3',
             'WOMAN','WOMAN 2','TYRION','VARYS','PRIESTESS','JORAH']

names5_04 = ['JAIME','CAPTAIN','BRONN','CERSEI','MACE','PYCELLE','HIGH SPARROW','MERCHANT','OLYVAR','MILITANT',
             'LORAS','LANCEL','TOMMEN','MARGAERY','KINGSGUARD','MAN 1','MAN 2','MAN 3','WOMAN','MAN 4','SELYSE','JON',
             'STANNIS','MELISANDRE','SAM','SHIREEN','SANSA','BAELISH','RIDER','TYENE','ELARIA','OBARA','NYMERIA',
             'TYRION','JORAH','DAENERYS','BARRISTAN','DARIO','HIZDAHR','MISSANDEI','WOMAN']

names5_05 = ['HIZDAHR','DAENERYS','DAARIO','MAN','SAM','AEMON','JON','TORMUND','STANNIS','DAVOS','ALLISTER','EDD',
             'OLLY','PODRICK','BRIENNE','RAMSAY','MYRANDA','WOMAN','SANSA','THEON','ROOSE','WALDA','GILLY','SHIREEN',
             'MISSANDEI','GREY WORM','TYRION','JORAH']

names5_06 = ['ARYA','WAIF','JAQEN','TYRION','JORAH','MAN','GIRL','MALKO','SLAVER','LANCEL','BAELISH','CERSEI',
             'TRYSTANE','MYRCELLA','DORAN,','AREO','JAIME','BRONN','ELLARIA','SAND SNAKES','OBARA','RIDER','OLENNA',
             'MARGAERY','HIGH SPARROW','LORAS','SPARROW','OLYVAR','MYRANDA','SANSA','THEON','ROOSE','RAMSAY']

names5_07 = ['JON','ALLISER','SAM','AEMON','SANSA','THEON','RAMSAY','AEMON','GILLY','BROTHERS','DAVOS','STANNIS',
             'MELISANDRE','DERRYK','BRAND','MALKO','SLAVE BUYER','TYRION','BUYER','DAARIO','DAENERYS','OLENNA',
             'HIGH SPARROW','SPARROW','SQUIRE','CERSEI','TOMMEN','AREO','MYRCELLA','JAIME','BRONN','TYENE','OBARA',
             'BAELISH','OLENNA','SLAVE OWNER','OWNER','MEN','HIZDAHR','JORAH','MARGAERY','HIGH SPARROW','SPARROW']

names5_08 = ['JORAH','DAENERYS','TYRION','SEPTA','CERSEI','ARYA','JAQEN','THIN MAN','MAN','WAIF','QYBURN','SANSA',
             'THEON','BOLTON BANNERMAN','ROOSE','RAMSAY','MASTER','GILLY','SAM','OLLY','TORMUND','JON',
             'LORD OF BONES','KARSI','LOBODA','WILDLING ELDER','GIANT','DAUGHTER','WUN WUN','NIGHT’S WATCH BROTHER',
             'BROTHER','EDD']

names5_09 = ['DAVOS','STANNIS','ALLISER','SAM','JON','SHIREEN','JAIME','DORAN','MYRCELLA','TRYSTANE','ELLARIA',
             'TYENE','NYMERIA','BRONN','AREO','ARYA','MAN','THIN MAN','BANKER','MACE','MERYN','BROTHEL KEEPER',
             'PROSTITUTE','JOHN','HEAD PROSTITUTE','HEAD','JAQEN','MELISANDRE','SELYSE','DAENERYS','HIZDAHR',
             'ANNOUNCER','QUICK','STRONG','DAARIO','TYRION','JORAH']

names5_10 = ['MELISANDRE','STANNIS','SOLDIER','SOLDIER 2','JON','SAM','PODRICK','BRIENNE','RAMSAY','SURVIVOR',
             'MYRANDA','THEON','SANSA','MAN','MERYN','ARYA','JAQEN','WAIF','DORAN','JAIME','ELLARIA','BRONN','TYENE',
             'MYRCELLA','TYRION','JORAH','DAARIO','GREY WORM','MISSANDEI','VARYS','DAENERYS','SEPTA','CERSEI',
             'HIGH SPARROW','SPARROW','CROWD','WOMAN','MAN','QYBURN','DAVOS','OLLY','ALLISER','BROTHER']

### Episode One

In [8]:
df_s5.script_text[0]

[u'\n',
 u'\n',
 u'EXT. WOODS',
 u'\n',
 u'\n',
 u'\n',
 u'\nMELARA: We shouldn\u2019t be out here alone.',
 u'\n',
 u'\nCERSEI: Why not?',
 u'\n',
 u'\nMELARA: If your father hears\u2026',
 u'\n',
 u'\nCERSEI: He\u2019ll never know we\u2019ve been gone.',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'\nCERSEI: You don\u2019t need to be afraid of my father.',
 u'\n',
 u'\n',
 u'\n',
 u'\nMELARA: Are you sure?',
 u'\n',
 u'\nCERSEI: Yes.',
 u'\n',
 u'\nMELARA: We shouldn\u2019t go in.',
 u'\n',
 u'\nCERSEI: Of course we should.',
 u'\n',
 u'\n',
 u'INT. MAGGY\u2019S HUT',
 u'\n',
 u'\n',
 u'\n',
 u'\nMAGGY: Get out. Get out!',
 u'\n',
 u'\nMELARA: Let\u2019s go\u2026',
 u'\n',
 u'\nCERSEI: No.',
 u'\n',
 u'\nMAGGY: Listen to your friend.',
 u'\n',
 u'\nCERSEI: They said that you were terrifying. With cat\u2019s teeth and three eyes. You\u2019re not terrifying. You\u2019re boring.',
 u'\n',
 u'\nMAGGY: You don\u2019t know what I am.',
 u'\n',
 u'\nCERSEI: I know you\u2019re a witch and you 

In [9]:
script_text5_01 = df_s5.script_text[0]
print type(script_text5_01)

script_text5_01

<type 'list'>


[u'\n',
 u'\n',
 u'EXT. WOODS',
 u'\n',
 u'\n',
 u'\n',
 u'\nMELARA: We shouldn\u2019t be out here alone.',
 u'\n',
 u'\nCERSEI: Why not?',
 u'\n',
 u'\nMELARA: If your father hears\u2026',
 u'\n',
 u'\nCERSEI: He\u2019ll never know we\u2019ve been gone.',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'\nCERSEI: You don\u2019t need to be afraid of my father.',
 u'\n',
 u'\n',
 u'\n',
 u'\nMELARA: Are you sure?',
 u'\n',
 u'\nCERSEI: Yes.',
 u'\n',
 u'\nMELARA: We shouldn\u2019t go in.',
 u'\n',
 u'\nCERSEI: Of course we should.',
 u'\n',
 u'\n',
 u'INT. MAGGY\u2019S HUT',
 u'\n',
 u'\n',
 u'\n',
 u'\nMAGGY: Get out. Get out!',
 u'\n',
 u'\nMELARA: Let\u2019s go\u2026',
 u'\n',
 u'\nCERSEI: No.',
 u'\n',
 u'\nMAGGY: Listen to your friend.',
 u'\n',
 u'\nCERSEI: They said that you were terrifying. With cat\u2019s teeth and three eyes. You\u2019re not terrifying. You\u2019re boring.',
 u'\n',
 u'\nMAGGY: You don\u2019t know what I am.',
 u'\n',
 u'\nCERSEI: I know you\u2019re a witch and you 

In [10]:
script_split = [i.split('\n') for i in script_text5_01]
script_split

[[u'', u''],
 [u'', u''],
 [u'EXT. WOODS'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u'MELARA: We shouldn\u2019t be out here alone.'],
 [u'', u''],
 [u'', u'CERSEI: Why not?'],
 [u'', u''],
 [u'', u'MELARA: If your father hears\u2026'],
 [u'', u''],
 [u'', u'CERSEI: He\u2019ll never know we\u2019ve been gone.'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u'CERSEI: You don\u2019t need to be afraid of my father.'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u'MELARA: Are you sure?'],
 [u'', u''],
 [u'', u'CERSEI: Yes.'],
 [u'', u''],
 [u'', u'MELARA: We shouldn\u2019t go in.'],
 [u'', u''],
 [u'', u'CERSEI: Of course we should.'],
 [u'', u''],
 [u'', u''],
 [u'INT. MAGGY\u2019S HUT'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u'MAGGY: Get out. Get out!'],
 [u'', u''],
 [u'', u'MELARA: Let\u2019s go\u2026'],
 [u'', u''],
 [u'', u'CERSEI: No.'],
 [u'', u''],
 [u'', u'MAGGY: Listen to your friend.'],
 [u'', u''],
 [u'',
  u'CERSEI: They said that you

In [11]:
string_script_text = ' '

for i in script_split:
    for e in i:
        string_script_text = string_script_text + ' ' + e

In [12]:
string_script_text

u'      EXT. WOODS        MELARA: We shouldn\u2019t be out here alone.    CERSEI: Why not?    MELARA: If your father hears\u2026    CERSEI: He\u2019ll never know we\u2019ve been gone.            CERSEI: You don\u2019t need to be afraid of my father.        MELARA: Are you sure?    CERSEI: Yes.    MELARA: We shouldn\u2019t go in.    CERSEI: Of course we should.     INT. MAGGY\u2019S HUT        MAGGY: Get out. Get out!    MELARA: Let\u2019s go\u2026    CERSEI: No.    MAGGY: Listen to your friend.    CERSEI: They said that you were terrifying. With cat\u2019s teeth and three eyes. You\u2019re not terrifying. You\u2019re boring.    MAGGY: You don\u2019t know what I am.    CERSEI: I know you\u2019re a witch and you can see the future. Tell me mine.    MAGGY: Everybody wants to know their future. Until they know their future.    CERSEI:   Tell me my future or I\u2019ll have your two boring eyes gouged out of your head.        MAGGY: Your blood. Give me a taste.            CERSEI: But I will 

In [13]:
words = word_tokenize(string_script_text)
words

[u'EXT',
 u'.',
 u'WOODS',
 u'MELARA',
 u':',
 u'We',
 u'shouldn\u2019t',
 u'be',
 u'out',
 u'here',
 u'alone',
 u'.',
 u'CERSEI',
 u':',
 u'Why',
 u'not',
 u'?',
 u'MELARA',
 u':',
 u'If',
 u'your',
 u'father',
 u'hears\u2026',
 u'CERSEI',
 u':',
 u'He\u2019ll',
 u'never',
 u'know',
 u'we\u2019ve',
 u'been',
 u'gone',
 u'.',
 u'CERSEI',
 u':',
 u'You',
 u'don\u2019t',
 u'need',
 u'to',
 u'be',
 u'afraid',
 u'of',
 u'my',
 u'father',
 u'.',
 u'MELARA',
 u':',
 u'Are',
 u'you',
 u'sure',
 u'?',
 u'CERSEI',
 u':',
 u'Yes',
 u'.',
 u'MELARA',
 u':',
 u'We',
 u'shouldn\u2019t',
 u'go',
 u'in',
 u'.',
 u'CERSEI',
 u':',
 u'Of',
 u'course',
 u'we',
 u'should',
 u'.',
 u'INT',
 u'.',
 u'MAGGY\u2019S',
 u'HUT',
 u'MAGGY',
 u':',
 u'Get',
 u'out',
 u'.',
 u'Get',
 u'out',
 u'!',
 u'MELARA',
 u':',
 u'Let\u2019s',
 u'go\u2026',
 u'CERSEI',
 u':',
 u'No',
 u'.',
 u'MAGGY',
 u':',
 u'Listen',
 u'to',
 u'your',
 u'friend',
 u'.',
 u'CERSEI',
 u':',
 u'They',
 u'said',
 u'that',
 u'you',
 u'were',
 

In [14]:
sentences = sent_tokenize(string_script_text)
sentences

[u'      EXT.',
 u'WOODS        MELARA: We shouldn\u2019t be out here alone.',
 u'CERSEI: Why not?',
 u'MELARA: If your father hears\u2026    CERSEI: He\u2019ll never know we\u2019ve been gone.',
 u'CERSEI: You don\u2019t need to be afraid of my father.',
 u'MELARA: Are you sure?',
 u'CERSEI: Yes.',
 u'MELARA: We shouldn\u2019t go in.',
 u'CERSEI: Of course we should.',
 u'INT.',
 u'MAGGY\u2019S HUT        MAGGY: Get out.',
 u'Get out!',
 u'MELARA: Let\u2019s go\u2026    CERSEI: No.',
 u'MAGGY: Listen to your friend.',
 u'CERSEI: They said that you were terrifying.',
 u'With cat\u2019s teeth and three eyes.',
 u'You\u2019re not terrifying.',
 u'You\u2019re boring.',
 u'MAGGY: You don\u2019t know what I am.',
 u'CERSEI: I know you\u2019re a witch and you can see the future.',
 u'Tell me mine.',
 u'MAGGY: Everybody wants to know their future.',
 u'Until they know their future.',
 u'CERSEI:   Tell me my future or I\u2019ll have your two boring eyes gouged out of your head.',
 u'MAGGY: You

In [15]:
dialogue = []

for sentence in sentences:
    if sentence.split(':')[0] in (names5_01):
        dialogue.append(sentence)

In [16]:
dialogue

[u'CERSEI: Why not?',
 u'MELARA: If your father hears\u2026    CERSEI: He\u2019ll never know we\u2019ve been gone.',
 u'CERSEI: You don\u2019t need to be afraid of my father.',
 u'MELARA: Are you sure?',
 u'CERSEI: Yes.',
 u'MELARA: We shouldn\u2019t go in.',
 u'CERSEI: Of course we should.',
 u'MELARA: Let\u2019s go\u2026    CERSEI: No.',
 u'MAGGY: Listen to your friend.',
 u'CERSEI: They said that you were terrifying.',
 u'MAGGY: You don\u2019t know what I am.',
 u'CERSEI: I know you\u2019re a witch and you can see the future.',
 u'MAGGY: Everybody wants to know their future.',
 u'CERSEI:   Tell me my future or I\u2019ll have your two boring eyes gouged out of your head.',
 u'MAGGY: Your blood.',
 u'CERSEI: But I will be queen?',
 u'MAGGY:                 MELARA: Come on, we have to go.',
 u'CERSEI: They will keep waiting.',
 u'PRIEST: But your grace, many of these lords and ladies have travelled day and night to be here\u2026        PRIEST: From all seven kingdoms\u2026    CERSEI: T

In [17]:
import pickle
with open('/Users/zoemarkovits/Metis/project_five_got/Dialogue_PKLs/s501.pkl', 'wb') as f:
    pickle.dump(dialogue, f)

In [18]:
from collections import defaultdict

speakers = defaultdict(list)
for sentence in dialogue:
    speakers[sentence.split(':')[0]].append(sentence.split(':')[1])

speakers

defaultdict(list,
            {u'ALLISER': [u' These men need a firm hand.', u' Not soldiers.'],
             u'BAELISH': [u' Some boys develop more slowly.',
              u' He has other gifts.',
              u'         SANSA',
              u' I have no doubt that upon my return, Robin\u2019s skills will have improved  .',
              u' I did.',
              u' We are.',
              u' Lord Royce may be as honorable as he thinks he is, but he\u2019s not alone in that castle.',
              u' No.',
              u' So a land so far from here, even Cersei Lannister can\u2019t get her hands on you.'],
             u'BARRISTAN': [u' Yes, your grace.',
              u' It was only a matter of time, your grace.',
              u' The Sons of the Harpy will hear that message.'],
             u'BRIENNE': [u' Do you even know what a squire is?',
              u' I\u2019m not a knight.',
              u' I don\u2019t care, I\u2019m not your mother.',
              u' I found Arya.',


In [19]:
speakers['CERSEI']

[u' Why not?',
 u' You don\u2019t need to be afraid of my father.',
 u' Yes.',
 u' Of course we should.',
 u' They said that you were terrifying.',
 u' I know you\u2019re a witch and you can see the future.',
 u'   Tell me my future or I\u2019ll have your two boring eyes gouged out of your head.',
 u' But I will be queen?',
 u' They will keep waiting.',
 u' They?',
 u' They had nothing to do with it.',
 u' ...and now our father is dead.',
 u' Tyrion may be a monster but at least he killed our father on purpose.',
 u' Cousin Lancel.',
 u' Uncle, it\u2019s quite alright.',
 u' I\u2019m sure he\u2019ll grow out of it.',
 u' Your wounds from the Blackwater seem to have healed.',
 u' What can I do for you?',
 u' What could you possibly have done to warrant my forgiveness?',
 u' I doubt you\u2019ve ever led anyone anywhere.',
 u' I don\u2019t know what you\u2019re talking about.',
 u' The day Tywin Lannister\u2019s soul needs your help\u2026         CUT TO']

In [20]:
episode_one = pd.DataFrame.from_dict(speakers, orient="index")
print episode_one.shape

(39, 22)


In [21]:
#from numpy import nan
#episode_one.fillna(value=str(0), inplace=True)

In [22]:
episode_one.info()

<class 'pandas.core.frame.DataFrame'>
Index: 39 entries, STANNIS to ROYCE
Data columns (total 22 columns):
0     39 non-null object
1     29 non-null object
2     25 non-null object
3     23 non-null object
4     19 non-null object
5     12 non-null object
6     11 non-null object
7     11 non-null object
8     10 non-null object
9     6 non-null object
10    6 non-null object
11    5 non-null object
12    5 non-null object
13    5 non-null object
14    5 non-null object
15    5 non-null object
16    5 non-null object
17    5 non-null object
18    4 non-null object
19    4 non-null object
20    3 non-null object
21    2 non-null object
dtypes: object(22)
memory usage: 7.0+ KB


In [23]:
episode_one.head()

0   \
STANNIS          You know who rules at Winterfell now?   
DAVOS        I’ve been talking to your sworn brothers.   
KEVAN                   They call themselves sparrows.   
MELISANDRE                      The king wants a word.   
OLLY                                   It’s too heavy.   

                                                           1   \
STANNIS      The traitor who plunged a dagger into Robb St...   
DAVOS                                             Many don’t.   
KEVAN                                              Of course.   
MELISANDRE                                             Never.   
OLLY                                                     None   

                                                           2   \
STANNIS                                            No matter.   
DAVOS        Some of the Night’s Watch feel you have too m...   
KEVAN                                                    None   
MELISANDRE                                              Feel.   
OLLY                                                     None   

                                                           3   \
STANNIS         If they swear to follow me, I’ll pardon them.   
DAVOS                                      It’s a fair offer.   
KEVAN                                                    None   
MELISANDRE   Man or woman, young or old, lord or peasant, ...   
OLLY                                                     None   

                                                           4   \
STANNIS      I’ll offer them their lives and their freedom...   
DAVOS                                                    None   
KEVAN                                                    None   
MELISANDRE   Free folk, there is only one true king, and h...   
OLLY                                                     None   

                                     5               6            7   \
STANNIS      You admire him, don’t you?   He likes you.   Nightfall.   
DAVOS                              None            None         None   
KEVAN                              None            None         None   
MELISANDRE                         None            None         None   
OLLY                               None            None         None   

                          8     9     10    11    12    13    14    15    16  \
STANNIS      Kneel and live.  None  None  None  None  None  None  None  None   
DAVOS                   None  None  None  None  None  None  None  None  None   
KEVAN                   None  None  None  None  None  None  None  None  None   
MELISANDRE              None  None  None  None  None  None  None  None  None   
OLLY                    None  None  None  None  None  None  None  None  None   

              17    18    19    20    21  
STANNIS     None  None  None  None  None  
DAVOS       None  None  None  None  None  
KEVAN       None  None  None  None  None  
MELISANDRE  None  None  None  None  None  
OLLY        None  None  None  None  None

In [24]:
def remove_stops(sentence):
    characters = ['?','!','.',',',':',';']
    stoplist = stopwords.words('english') + characters
    try: 
        new_sentence = re.sub(r'[^a-zA-Z ]','', sentence)
        new_sentence = new_sentence.lower()
        new_sentence = new_sentence.split()
        new_sentence = [word for word in new_sentence if word not in stoplist]
        new_sentence = ' '.join(new_sentence)
        return new_sentence
    except:
        return sentence   

In [25]:
test = episode_one[0].apply(remove_stops)
test

STANNIS                                               know rules winterfell
DAVOS                                            ive talking sworn brothers
KEVAN                                                         call sparrows
MELISANDRE                                                  king wants word
OLLY                                                                  heavy
JAIME                     theyre waiting night make sure hes really dead...
TYRION                           still dont see stay fucking crate set sail
MISSANDEI                      white rat unsullied heard found body brothel
MOSSADOR                                                see us people grace
PROSTITUTE                                                            habit
BAELISH                                                 boys develop slowly
MANCE                                                    first met prisoner
SAM                                              well im hardly new recruit
GRAND MAESTE

In [26]:
for column in episode_one.columns:
    for x in range(len(episode_one[column])):
        episode_one[column][x] = remove_stops(episode_one[column][x])

In [27]:
episode_one.info()

<class 'pandas.core.frame.DataFrame'>
Index: 39 entries, STANNIS to ROYCE
Data columns (total 22 columns):
0     39 non-null object
1     29 non-null object
2     25 non-null object
3     23 non-null object
4     19 non-null object
5     12 non-null object
6     11 non-null object
7     11 non-null object
8     10 non-null object
9     6 non-null object
10    6 non-null object
11    5 non-null object
12    5 non-null object
13    5 non-null object
14    5 non-null object
15    5 non-null object
16    5 non-null object
17    5 non-null object
18    4 non-null object
19    4 non-null object
20    3 non-null object
21    2 non-null object
dtypes: object(22)
memory usage: 7.0+ KB


In [28]:
episode_one.index = episode_one.index.str.title()

episode_one.shape

(39, 22)

In [29]:
episode_one.head()

0   \
Stannis          know rules winterfell   
Davos       ive talking sworn brothers   
Kevan                    call sparrows   
Melisandre             king wants word   
Olly                             heavy   

                                                  1   \
Stannis     traitor plunged dagger robb starks heart   
Davos                                      many dont   
Kevan                                         course   
Melisandre                                     never   
Olly                                            None   

                                                    2   \
Stannis                                         matter   
Davos       nights watch feel much affection wildlings   
Kevan                                             None   
Melisandre                                        feel   
Olly                                              None   

                                                  3   \
Stannis                      swear follow ill pardon   
Davos                                     fair offer   
Kevan                                           None   
Melisandre  man woman young old lord peasant choices   
Olly                                            None   

                                                           4            5   \
Stannis     ill offer lives freedom mance kneels swears lo...  admire dont   
Davos                                                    None         None   
Kevan                                                    None         None   
Melisandre               free folk one true king name stannis         None   
Olly                                                     None         None   

               6          7           8     9     10    11    12    13    14  \
Stannis     likes  nightfall  kneel live  None  None  None  None  None  None   
Davos        None       None        None  None  None  None  None  None  None   
Kevan        None       None        None  None  None  None  None  None  None   
Melisandre   None       None        None  None  None  None  None  None  None   
Olly         None       None        None  None  None  None  None  None  None   

              15    16    17    18    19    20    21  
Stannis     None  None  None  None  None  None  None  
Davos       None  None  None  None  None  None  None  
Kevan       None  None  None  None  None  None  None  
Melisandre  None  None  None  None  None  None  None  
Olly        None  None  None  None  None  None  None

### Episode Two

In [30]:
df_s5.script_text[1]

[u'\n',
 u"\nBRAAVOSI MAN: In the old times, whenever Braavos stood in danger, the titan would step with fire in his eyes. He'd wade into the sea and smash the enemies.",
 u'\n',
 u"\nARYA: He's just a statue.",
 u'\n',
 u'\n',
 u'\n',
 u"\nMAN: Don't be afraid. He\u2019s announcing our arrival.",
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'EXT. BRAAVOS - RAGMAN HARBOR',
 u'\n',
 u'\n',
 u'\n',
 u"\nMAN: The House of Black and White: this is where you'll find the man you seek.",
 u'\n',
 u'\n',
 u'EXT. BRAAVOS - THE HOUSE OF BLACK AND WHITE',
 u'\n',
 u'\n',
 u'\n',
 u'\nMAN: Here, I leave you.',
 u'\n',
 u'\n',
 u'\n',
 u'\nARYA: Thank you for bringing me.',
 u'\n',
 u'\nMAN: Any man of Braavos would have done the same. Valar morghulis.',
 u'\n',
 u'\nARYA: Valar dohaeris.',
 u'\n',
 u'\n',
 u'\n',
 u'\nARYA: Hello. Valar Morghulis.',
 u'\n',
 u'\n',
 u'\n',
 u'\nARYA: Jaqen H\u2019ghar gave me this.',
 u'\n',
 u'\nOLD MAN: No one here by that name.',
 u'\n',
 u'\n',
 u'\n',
 u

In [31]:
script_text5_02 = df_s5.script_text[1]
print type(script_text5_02)

script_text5_02

<type 'list'>


[u'\n',
 u"\nBRAAVOSI MAN: In the old times, whenever Braavos stood in danger, the titan would step with fire in his eyes. He'd wade into the sea and smash the enemies.",
 u'\n',
 u"\nARYA: He's just a statue.",
 u'\n',
 u'\n',
 u'\n',
 u"\nMAN: Don't be afraid. He\u2019s announcing our arrival.",
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'EXT. BRAAVOS - RAGMAN HARBOR',
 u'\n',
 u'\n',
 u'\n',
 u"\nMAN: The House of Black and White: this is where you'll find the man you seek.",
 u'\n',
 u'\n',
 u'EXT. BRAAVOS - THE HOUSE OF BLACK AND WHITE',
 u'\n',
 u'\n',
 u'\n',
 u'\nMAN: Here, I leave you.',
 u'\n',
 u'\n',
 u'\n',
 u'\nARYA: Thank you for bringing me.',
 u'\n',
 u'\nMAN: Any man of Braavos would have done the same. Valar morghulis.',
 u'\n',
 u'\nARYA: Valar dohaeris.',
 u'\n',
 u'\n',
 u'\n',
 u'\nARYA: Hello. Valar Morghulis.',
 u'\n',
 u'\n',
 u'\n',
 u'\nARYA: Jaqen H\u2019ghar gave me this.',
 u'\n',
 u'\nOLD MAN: No one here by that name.',
 u'\n',
 u'\n',
 u'\n',
 u

In [32]:
script_split2 = [i.split('\n') for i in script_text5_02]
script_split2

[[u'', u''],
 [u'',
  u"BRAAVOSI MAN: In the old times, whenever Braavos stood in danger, the titan would step with fire in his eyes. He'd wade into the sea and smash the enemies."],
 [u'', u''],
 [u'', u"ARYA: He's just a statue."],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u"MAN: Don't be afraid. He\u2019s announcing our arrival."],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'EXT. BRAAVOS - RAGMAN HARBOR'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'',
  u"MAN: The House of Black and White: this is where you'll find the man you seek."],
 [u'', u''],
 [u'', u''],
 [u'EXT. BRAAVOS - THE HOUSE OF BLACK AND WHITE'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u'MAN: Here, I leave you.'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u'ARYA: Thank you for bringing me.'],
 [u'', u''],
 [u'', u'MAN: Any man of Braavos would have done the same. Valar morghulis.'],
 [u'', u''],
 [u'', u'ARYA: Valar dohaeris.'],
 [u'', u''],
 [u'', u''],
 [u'', u''],

In [33]:
string_script_text2 = ' '

for i in script_split2:
    for e in i:
        string_script_text2 = string_script_text2 + ' ' + e

In [34]:
string_script_text2

u'     BRAAVOSI MAN: In the old times, whenever Braavos stood in danger, the titan would step with fire in his eyes. He\'d wade into the sea and smash the enemies.    ARYA: He\'s just a statue.        MAN: Don\'t be afraid. He\u2019s announcing our arrival.             EXT. BRAAVOS - RAGMAN HARBOR        MAN: The House of Black and White: this is where you\'ll find the man you seek.     EXT. BRAAVOS - THE HOUSE OF BLACK AND WHITE        MAN: Here, I leave you.        ARYA: Thank you for bringing me.    MAN: Any man of Braavos would have done the same. Valar morghulis.    ARYA: Valar dohaeris.        ARYA: Hello. Valar Morghulis.        ARYA: Jaqen H\u2019ghar gave me this.    OLD MAN: No one here by that name.        ARYA: Please. I crossed the Narrow Sea. I have nowhere else to go.    OLD MAN: You have everywhere else to go.    ARYA: But wait!         EXT. HOUSE OF BLACK AND WHITE - NIGHT    ARYA:   Cersei, Walder Frey, The Mountain, Meryn Trant.         EXT. HOUSE OF BLACK AND WHITE 

In [35]:
words2 = word_tokenize(string_script_text2)
words2

[u'BRAAVOSI',
 u'MAN',
 u':',
 u'In',
 u'the',
 u'old',
 u'times',
 u',',
 u'whenever',
 u'Braavos',
 u'stood',
 u'in',
 u'danger',
 u',',
 u'the',
 u'titan',
 u'would',
 u'step',
 u'with',
 u'fire',
 u'in',
 u'his',
 u'eyes',
 u'.',
 u'He',
 u"'d",
 u'wade',
 u'into',
 u'the',
 u'sea',
 u'and',
 u'smash',
 u'the',
 u'enemies',
 u'.',
 u'ARYA',
 u':',
 u'He',
 u"'s",
 u'just',
 u'a',
 u'statue',
 u'.',
 u'MAN',
 u':',
 u'Do',
 u"n't",
 u'be',
 u'afraid',
 u'.',
 u'He\u2019s',
 u'announcing',
 u'our',
 u'arrival',
 u'.',
 u'EXT',
 u'.',
 u'BRAAVOS',
 u'-',
 u'RAGMAN',
 u'HARBOR',
 u'MAN',
 u':',
 u'The',
 u'House',
 u'of',
 u'Black',
 u'and',
 u'White',
 u':',
 u'this',
 u'is',
 u'where',
 u'you',
 u"'ll",
 u'find',
 u'the',
 u'man',
 u'you',
 u'seek',
 u'.',
 u'EXT',
 u'.',
 u'BRAAVOS',
 u'-',
 u'THE',
 u'HOUSE',
 u'OF',
 u'BLACK',
 u'AND',
 u'WHITE',
 u'MAN',
 u':',
 u'Here',
 u',',
 u'I',
 u'leave',
 u'you',
 u'.',
 u'ARYA',
 u':',
 u'Thank',
 u'you',
 u'for',
 u'bringing',
 u'me',
 

In [36]:
sentences2 = sent_tokenize(string_script_text2)
sentences2

[u'     BRAAVOSI MAN: In the old times, whenever Braavos stood in danger, the titan would step with fire in his eyes.',
 u"He'd wade into the sea and smash the enemies.",
 u"ARYA: He's just a statue.",
 u"MAN: Don't be afraid.",
 u'He\u2019s announcing our arrival.',
 u'EXT.',
 u"BRAAVOS - RAGMAN HARBOR        MAN: The House of Black and White: this is where you'll find the man you seek.",
 u'EXT.',
 u'BRAAVOS - THE HOUSE OF BLACK AND WHITE        MAN: Here, I leave you.',
 u'ARYA: Thank you for bringing me.',
 u'MAN: Any man of Braavos would have done the same.',
 u'Valar morghulis.',
 u'ARYA: Valar dohaeris.',
 u'ARYA: Hello.',
 u'Valar Morghulis.',
 u'ARYA: Jaqen H\u2019ghar gave me this.',
 u'OLD MAN: No one here by that name.',
 u'ARYA: Please.',
 u'I crossed the Narrow Sea.',
 u'I have nowhere else to go.',
 u'OLD MAN: You have everywhere else to go.',
 u'ARYA: But wait!',
 u'EXT.',
 u'HOUSE OF BLACK AND WHITE - NIGHT    ARYA:   Cersei, Walder Frey, The Mountain, Meryn Trant.',
 

In [37]:
dialogue2 = []

for sentence in sentences2:
    words=sentence.split(':')[0]
    if len(words.split())<=2:
        if words in (names5_02):
            dialogue2.append(sentence)

In [38]:
dialogue2

[u"ARYA: He's just a statue.",
 u"MAN: Don't be afraid.",
 u'ARYA: Thank you for bringing me.',
 u'MAN: Any man of Braavos would have done the same.',
 u'ARYA: Valar dohaeris.',
 u'ARYA: Hello.',
 u'ARYA: Jaqen H\u2019ghar gave me this.',
 u'OLD MAN: No one here by that name.',
 u'ARYA: Please.',
 u'OLD MAN: You have everywhere else to go.',
 u'ARYA: But wait!',
 u'SANSA: Before we left, a maester gave you a raven scroll.',
 u'BAELISH: You are becoming an observant young lady.',
 u'SANSA: My mother used to say, "dark wings, dark words".',
 u'BAELISH: An old saying.',
 u'SANSA: So it was good news.?',
 u'BAELISH: My marriage proposal has been accepted.',
 u'SANSA: I thought you still mourn the death of my beloved Aunt Lysa.',
 u'WAITRESS: Ale?',
 u"SANSA: I'll have some.",
 u'PODRICK: My lady!',
 u'BRIENNE: What is it?',
 u'PODRICK: Sansa Stark.',
 u'BRIENNE: You sure?',
 u"PODRICK: She's dyed her hair, but it's her.",
 u'BRIENNE: Littlefinger?',
 u'PODRICK: A bunch of knights with him.

In [39]:
import pickle
with open('/Users/zoemarkovits/Metis/project_five_got/Dialogue_PKLs/s502.pkl', 'wb') as f:
    pickle.dump(dialogue2, f)

In [40]:
from collections import defaultdict

speakers2 = defaultdict(list)
for sentence in dialogue2:
    speakers2[sentence.split(':')[0]].append(sentence.split(':')[1])

speakers2

defaultdict(list,
            {u'AEMON': [u" Does anyone wish to speak for candidates before we cast our tokens for the 998th Lord Commander of the Night's Watch?",
              u' Is there anyone else?',
              u" If there's no one else, we will begin the voting.",
              u' Samwell Tarly.',
              u' It is time.'],
             u'ALLISER': [u" I can't argue with any of that."],
             u'AREO': [u' The prince does not wish to be disturbed.'],
             u'ARYA': [u" He's just a statue.",
              u' Thank you for bringing me.',
              u' Valar dohaeris.',
              u' Hello.',
              u' Jaqen H\u2019ghar gave me this.',
              u' Please.',
              u' But wait!',
              u" You said there was no Jaqen H'ghar here.",
              u' Well who are you then?'],
             u'BAELISH': [u' You are becoming an observant young lady.',
              u' An old saying.',
              u' My marriage proposal has been accep

In [41]:
speakers2['ARYA']

[u" He's just a statue.",
 u' Thank you for bringing me.',
 u' Valar dohaeris.',
 u' Hello.',
 u' Jaqen H\u2019ghar gave me this.',
 u' Please.',
 u' But wait!',
 u" You said there was no Jaqen H'ghar here.",
 u' Well who are you then?']

In [42]:
episode_two = pd.DataFrame.from_dict(speakers2, orient="index")
print episode_two.shape

(47, 23)


In [43]:
#from numpy import nan
#episode_two.fillna(value=str(0), inplace=True)

In [44]:
episode_two.info()

<class 'pandas.core.frame.DataFrame'>
Index: 47 entries, STANNIS to MAN
Data columns (total 23 columns):
0     47 non-null object
1     37 non-null object
2     30 non-null object
3     28 non-null object
4     24 non-null object
5     22 non-null object
6     20 non-null object
7     16 non-null object
8     13 non-null object
9     11 non-null object
10    10 non-null object
11    7 non-null object
12    6 non-null object
13    5 non-null object
14    4 non-null object
15    4 non-null object
16    3 non-null object
17    3 non-null object
18    3 non-null object
19    3 non-null object
20    3 non-null object
21    1 non-null object
22    1 non-null object
dtypes: object(23)
memory usage: 8.8+ KB


In [45]:
episode_two.head()

0   \
STANNIS                                          Who then?   
DAVOS     Tonight, the Night's Watch elect a new Lord C...   
SHIREEN                                  Right, very good!   
MERYN                Are you trying to deceive your Queen?   
PYCELLE   Your Grace, in the past on several occasions,...   

                                1   \
STANNIS                        JON   
DAVOS              Unpleasant man.   
SHIREEN   You'll learn, I promise.   
MERYN                         None   
PYCELLE           Your Grace, him?   

                                                        2   \
STANNIS            Lady of Bear Island, and a child of 10.   
DAVOS                                                 None   
SHIREEN                                             Three.   
MERYN                                                 None   
PYCELLE   I must say I cannot see--    CERSEI (cutting ...   

                                          3   \
STANNIS                              I know.   
DAVOS                                   None   
SHIREEN     I had a lot of time to practice.   
MERYN                                   None   
PYCELLE                                 None   

                                        4                            5   \
STANNIS   Your bravery made him look weak.   You can give me the North.   
DAVOS                                 None                         None   
SHIREEN                         Greyscale.            I don't remember.   
MERYN                                 None                         None   
PYCELLE                               None                         None   

                        6      7                   8   \
STANNIS   Kneel before me.   None                None   
DAVOS                 None   None                None   
SHIREEN            Mother.   Why?   Her name's Gilly.   
MERYN                 None   None                None   
PYCELLE               None   None                None   

                               9     10    11    12    13    14    15    16  \
STANNIS                      None  None  None  None  None  None  None  None   
DAVOS                        None  None  None  None  None  None  None  None   
SHIREEN   Gilly wouldn't do that.  None  None  None  None  None  None  None   
MERYN                        None  None  None  None  None  None  None  None   
PYCELLE                      None  None  None  None  None  None  None  None   

           17    18    19    20    21    22  
STANNIS  None  None  None  None  None  None  
DAVOS    None  None  None  None  None  None  
SHIREEN  None  None  None  None  None  None  
MERYN    None  None  None  None  None  None  
PYCELLE  None  None  None  None  None  None

In [46]:
test2 = episode_two[0].apply(remove_stops)
test2

STANNIS                                                         
DAVOS              tonight nights watch elect new lord commander
SHIREEN                                               right good
MERYN                                       trying deceive queen
PYCELLE        grace past several occasions grand maester ser...
KEVAN                                            youre hand king
OLD MAN                                                 one name
BROTHER                                      appears tie maester
BRONN                                                       dont
GILLY                                                      snake
JAIME                                                     threat
TYRION                       agreed come misrepresent intentions
LOLLYS                                                      dont
MOSSADOR                                               born free
BAELISH                            becoming observant young lady
ELLARIA                re

In [47]:
for column in episode_two.columns:
    for x in range(len(episode_two[column])):
        episode_two[column][x] = remove_stops(episode_two[column][x])

In [48]:
episode_two.info()

<class 'pandas.core.frame.DataFrame'>
Index: 47 entries, STANNIS to MAN
Data columns (total 23 columns):
0     47 non-null object
1     37 non-null object
2     30 non-null object
3     28 non-null object
4     24 non-null object
5     22 non-null object
6     20 non-null object
7     16 non-null object
8     13 non-null object
9     11 non-null object
10    10 non-null object
11    7 non-null object
12    6 non-null object
13    5 non-null object
14    4 non-null object
15    4 non-null object
16    3 non-null object
17    3 non-null object
18    3 non-null object
19    3 non-null object
20    3 non-null object
21    1 non-null object
22    1 non-null object
dtypes: object(23)
memory usage: 8.8+ KB


In [49]:
episode_two.index = episode_two.index.str.title()

episode_two.shape

(47, 23)

In [50]:
episode_two.head()

0   \
Stannis                                                      
Davos        tonight nights watch elect new lord commander   
Shireen                                         right good   
Meryn                                 trying deceive queen   
Pycelle  grace past several occasions grand maester ser...   

                          1                                   2   \
Stannis                  jon              lady bear island child   
Davos         unpleasant man                                None   
Shireen  youll learn promise                               three   
Meryn                   None                                None   
Pycelle                grace  must say cannot see cersei cutting   

                        3                       4              5       6   \
Stannis               know  bravery made look weak     give north   kneel   
Davos                 None                    None           None    None   
Shireen  lot time practice               greyscale  dont remember  mother   
Meryn                 None                    None           None    None   
Pycelle               None                    None           None    None   

           7            8              9     10    11    12    13    14    15  \
Stannis  None         None           None  None  None  None  None  None  None   
Davos    None         None           None  None  None  None  None  None  None   
Shireen        names gilly  gilly wouldnt  None  None  None  None  None  None   
Meryn    None         None           None  None  None  None  None  None  None   
Pycelle  None         None           None  None  None  None  None  None  None   

           16    17    18    19    20    21    22  
Stannis  None  None  None  None  None  None  None  
Davos    None  None  None  None  None  None  None  
Shireen  None  None  None  None  None  None  None  
Meryn    None  None  None  None  None  None  None  
Pycelle  None  None  None  None  None  None  None

### Episode Three

In [51]:
df_s5.script_text[2]

[u'TITLE SEQUENCE',
 u'\n',
 u'\n',
 u'CUT TO: BRAAVOS',
 u'\n',
 u'\n',
 u'INT. THE HOUSE OF BLACK AND WHITE',
 u'\n',
 u'\n',
 u'\n',
 u'\nMAN: Valar morghulis.',
 u'\n',
 u'\nJAQEN: Valar dohaeris.',
 u'\n',
 u'\n',
 u'\n',
 u"\nARYA: I've been sweeping this floor for days.",
 u'\n',
 u'\nJAQEN: Good.',
 u'\n',
 u"\nARYA: I didn't come here to sweep floors.",
 u'\n',
 u'\nJAQEN: No? Why come, then?',
 u'\n',
 u"\nARYA: You said that I could be your apprentice. You said you'd teach me how to a Faceless Man.",
 u'\n',
 u'\nJAQEN: A man teaches a girl. (Stands up). Valar dohaeris. All men must serve. Faceless men, most of all. (Walks away).',
 u'\n',
 u'\nARYA: I want to serve. (Jaqen stops).',
 u'\n',
 u'\nJAQEN: A girl wants to serve herself. Here we serve the Many-Faced God, to serve well. A girl must become no-one.',
 u'\n',
 u'\nARYA: Which one is the Many-Faced God? I see the Stranger. ',
 u'. ',
 u'\n',
 u'\nJAQEN: There is only one god. A girl knows his name. And all men know h

In [52]:
script_text5_03 = df_s5.script_text[2]
print type(script_text5_03)

script_text5_03

<type 'list'>


[u'TITLE SEQUENCE',
 u'\n',
 u'\n',
 u'CUT TO: BRAAVOS',
 u'\n',
 u'\n',
 u'INT. THE HOUSE OF BLACK AND WHITE',
 u'\n',
 u'\n',
 u'\n',
 u'\nMAN: Valar morghulis.',
 u'\n',
 u'\nJAQEN: Valar dohaeris.',
 u'\n',
 u'\n',
 u'\n',
 u"\nARYA: I've been sweeping this floor for days.",
 u'\n',
 u'\nJAQEN: Good.',
 u'\n',
 u"\nARYA: I didn't come here to sweep floors.",
 u'\n',
 u'\nJAQEN: No? Why come, then?',
 u'\n',
 u"\nARYA: You said that I could be your apprentice. You said you'd teach me how to a Faceless Man.",
 u'\n',
 u'\nJAQEN: A man teaches a girl. (Stands up). Valar dohaeris. All men must serve. Faceless men, most of all. (Walks away).',
 u'\n',
 u'\nARYA: I want to serve. (Jaqen stops).',
 u'\n',
 u'\nJAQEN: A girl wants to serve herself. Here we serve the Many-Faced God, to serve well. A girl must become no-one.',
 u'\n',
 u'\nARYA: Which one is the Many-Faced God? I see the Stranger. ',
 u'. ',
 u'\n',
 u'\nJAQEN: There is only one god. A girl knows his name. And all men know h

In [53]:
script_split3 = [i.split('\n') for i in script_text5_03]
script_split3

[[u'TITLE SEQUENCE'],
 [u'', u''],
 [u'', u''],
 [u'CUT TO: BRAAVOS'],
 [u'', u''],
 [u'', u''],
 [u'INT. THE HOUSE OF BLACK AND WHITE'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u'MAN: Valar morghulis.'],
 [u'', u''],
 [u'', u'JAQEN: Valar dohaeris.'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u"ARYA: I've been sweeping this floor for days."],
 [u'', u''],
 [u'', u'JAQEN: Good.'],
 [u'', u''],
 [u'', u"ARYA: I didn't come here to sweep floors."],
 [u'', u''],
 [u'', u'JAQEN: No? Why come, then?'],
 [u'', u''],
 [u'',
  u"ARYA: You said that I could be your apprentice. You said you'd teach me how to a Faceless Man."],
 [u'', u''],
 [u'',
  u'JAQEN: A man teaches a girl. (Stands up). Valar dohaeris. All men must serve. Faceless men, most of all. (Walks away).'],
 [u'', u''],
 [u'', u'ARYA: I want to serve. (Jaqen stops).'],
 [u'', u''],
 [u'',
  u'JAQEN: A girl wants to serve herself. Here we serve the Many-Faced God, to serve well. A girl must become no-one.'],
 [u'', u''],
 [

In [54]:
string_script_text3 = ' '

for i in script_split3:
    for e in i:
        string_script_text3 = string_script_text3 + ' ' + e

In [55]:
string_script_text3

u'  TITLE SEQUENCE     CUT TO: BRAAVOS     INT. THE HOUSE OF BLACK AND WHITE        MAN: Valar morghulis.    JAQEN: Valar dohaeris.        ARYA: I\'ve been sweeping this floor for days.    JAQEN: Good.    ARYA: I didn\'t come here to sweep floors.    JAQEN: No? Why come, then?    ARYA: You said that I could be your apprentice. You said you\'d teach me how to a Faceless Man.    JAQEN: A man teaches a girl. (Stands up). Valar dohaeris. All men must serve. Faceless men, most of all. (Walks away).    ARYA: I want to serve. (Jaqen stops).    JAQEN: A girl wants to serve herself. Here we serve the Many-Faced God, to serve well. A girl must become no-one.    ARYA: Which one is the Many-Faced God? I see the Stranger.  .     JAQEN: There is only one god. A girl knows his name. And all men know his gift.        ARYA: Where are they taking him?         CUT TO: KING\u2019S LANDING     EXT. STREET        BYSTANDERS: Queen Margaery! Queen Margaery! Queen Margaery!         INT. GREAT SEPT    MARGAERY

In [56]:
words3 = word_tokenize(string_script_text3)
words3

[u'TITLE',
 u'SEQUENCE',
 u'CUT',
 u'TO',
 u':',
 u'BRAAVOS',
 u'INT',
 u'.',
 u'THE',
 u'HOUSE',
 u'OF',
 u'BLACK',
 u'AND',
 u'WHITE',
 u'MAN',
 u':',
 u'Valar',
 u'morghulis',
 u'.',
 u'JAQEN',
 u':',
 u'Valar',
 u'dohaeris',
 u'.',
 u'ARYA',
 u':',
 u'I',
 u"'ve",
 u'been',
 u'sweeping',
 u'this',
 u'floor',
 u'for',
 u'days',
 u'.',
 u'JAQEN',
 u':',
 u'Good',
 u'.',
 u'ARYA',
 u':',
 u'I',
 u'did',
 u"n't",
 u'come',
 u'here',
 u'to',
 u'sweep',
 u'floors',
 u'.',
 u'JAQEN',
 u':',
 u'No',
 u'?',
 u'Why',
 u'come',
 u',',
 u'then',
 u'?',
 u'ARYA',
 u':',
 u'You',
 u'said',
 u'that',
 u'I',
 u'could',
 u'be',
 u'your',
 u'apprentice',
 u'.',
 u'You',
 u'said',
 u'you',
 u"'d",
 u'teach',
 u'me',
 u'how',
 u'to',
 u'a',
 u'Faceless',
 u'Man',
 u'.',
 u'JAQEN',
 u':',
 u'A',
 u'man',
 u'teaches',
 u'a',
 u'girl',
 u'.',
 u'(',
 u'Stands',
 u'up',
 u')',
 u'.',
 u'Valar',
 u'dohaeris',
 u'.',
 u'All',
 u'men',
 u'must',
 u'serve',
 u'.',
 u'Faceless',
 u'men',
 u',',
 u'most',
 u'of

In [57]:
sentences3 = sent_tokenize(string_script_text3)
sentences3

[u'  TITLE SEQUENCE     CUT TO: BRAAVOS     INT.',
 u'THE HOUSE OF BLACK AND WHITE        MAN: Valar morghulis.',
 u'JAQEN: Valar dohaeris.',
 u"ARYA: I've been sweeping this floor for days.",
 u'JAQEN: Good.',
 u"ARYA: I didn't come here to sweep floors.",
 u'JAQEN: No?',
 u'Why come, then?',
 u'ARYA: You said that I could be your apprentice.',
 u"You said you'd teach me how to a Faceless Man.",
 u'JAQEN: A man teaches a girl.',
 u'(Stands up).',
 u'Valar dohaeris.',
 u'All men must serve.',
 u'Faceless men, most of all.',
 u'(Walks away).',
 u'ARYA: I want to serve.',
 u'(Jaqen stops).',
 u'JAQEN: A girl wants to serve herself.',
 u'Here we serve the Many-Faced God, to serve well.',
 u'A girl must become no-one.',
 u'ARYA: Which one is the Many-Faced God?',
 u'I see the Stranger.',
 u'.',
 u'JAQEN: There is only one god.',
 u'A girl knows his name.',
 u'And all men know his gift.',
 u'ARYA: Where are they taking him?',
 u'CUT TO: KING\u2019S LANDING     EXT.',
 u'STREET        BYSTAN

In [58]:
dialogue3 = []

for sentence in sentences3:
    words=sentence.split(':')[0]
    if len(words.split())<=2:
        if words in (names5_03):
            dialogue3.append(sentence)

In [59]:
dialogue3

[u'JAQEN: Valar dohaeris.',
 u"ARYA: I've been sweeping this floor for days.",
 u'JAQEN: Good.',
 u"ARYA: I didn't come here to sweep floors.",
 u'JAQEN: No?',
 u'ARYA: You said that I could be your apprentice.',
 u'JAQEN: A man teaches a girl.',
 u'ARYA: I want to serve.',
 u'JAQEN: A girl wants to serve herself.',
 u'ARYA: Which one is the Many-Faced God?',
 u'JAQEN: There is only one god.',
 u'ARYA: Where are they taking him?',
 u'MARGAERY: No.',
 u'TOMMEN: It all happened so fast.',
 u'MARGAERY: Yes.',
 u'TOMMEN: I was scared maybe I hurt you, it sounded    MARGAERY: No, no, no.',
 u'TOMMEN: This is what I want to do all day, every day for the rest of my life.',
 u"MARGAERY: Wouldn't that be glorious?",
 u'TOMMEN: Of course not.',
 u"MARGAERY: No, I'm fine.",
 u'TOMMEN: Do you like to sail?',
 u'MARGAERY: (Sits up).',
 u'TOMMEN: I do, too.',
 u"MARGAERY: I think we're going to be very happy, you and I.    TOMMEN: I do, too.",
 u'MARGAERY: Living in a tower so high, it touches the c

In [60]:
import pickle
with open('/Users/zoemarkovits/Metis/project_five_got/Dialogue_PKLs/s503.pkl', 'wb') as f:
    pickle.dump(dialogue3, f)

In [61]:
from collections import defaultdict

speakers3 = defaultdict(list)
for sentence in dialogue3:
    speakers3[sentence.split(':')[0]].append(sentence.split(':')[1])

speakers3

defaultdict(list,
            {u'ARYA': [u" I've been sweeping this floor for days.",
              u" I didn't come here to sweep floors.",
              u' You said that I could be your apprentice.',
              u' I want to serve.',
              u' Which one is the Many-Faced God?',
              u' Where are they taking him?',
              u' What?',
              u' (After a moment, perks up).',
              u' Ow!',
              u" I told you, I'm no - (Gets hit again).",
              u" You're about to find out.",
              u' (Stands up).'],
             u'BAELISH': [u' Yes.',
              u' Home.',
              u' (Shakes his head).',
              u' He did.',
              u' For now.',
              u' Winterfell is your home.',
              u' Always.',
              u" You're not marrying Roose Bolton.",
              u' Sansa -    SANSA',
              u' (Grabbing her).',
              u' I hope so too.',
              u'     RAMSAY',
              u' He 

In [62]:
speakers3['ARYA']

[u" I've been sweeping this floor for days.",
 u" I didn't come here to sweep floors.",
 u' You said that I could be your apprentice.',
 u' I want to serve.',
 u' Which one is the Many-Faced God?',
 u' Where are they taking him?',
 u' What?',
 u' (After a moment, perks up).',
 u' Ow!',
 u" I told you, I'm no - (Gets hit again).",
 u" You're about to find out.",
 u' (Stands up).']

In [63]:
episode_three = pd.DataFrame.from_dict(speakers3, orient="index")
print episode_three.shape

(34, 24)


In [64]:
#from numpy import nan
#episode_three.fillna(value=str(0), inplace=True)

In [65]:
episode_three.info()

<class 'pandas.core.frame.DataFrame'>
Index: 34 entries, STANNIS to MAN
Data columns (total 24 columns):
0     34 non-null object
1     26 non-null object
2     24 non-null object
3     24 non-null object
4     21 non-null object
5     17 non-null object
6     17 non-null object
7     16 non-null object
8     14 non-null object
9     13 non-null object
10    10 non-null object
11    10 non-null object
12    8 non-null object
13    7 non-null object
14    7 non-null object
15    6 non-null object
16    5 non-null object
17    5 non-null object
18    4 non-null object
19    3 non-null object
20    3 non-null object
21    2 non-null object
22    1 non-null object
23    1 non-null object
dtypes: object(24)
memory usage: 6.6+ KB


In [66]:
episode_three.head()

0   \
STANNIS                     (To Olly as he closes the door).   
DAVOS                              He sees something in you.   
MERYN         I don't think this is a good idea, Your Grace.   
PYCELLE       A man's private affairs ought to stay private!   
PRIESTESS   (Valyrian) For the night is dark and full of ...   

                                               1   \
STANNIS                                Very well.   
DAVOS              The king is a complicated man.   
MERYN                                        None   
PYCELLE                                      None   
PRIESTESS   (Valyrian) I was once as you are now.   

                                                          2   \
STANNIS                        Say the word and you will be.   
DAVOS                                He's the one true king.   
MERYN                                                   None   
PYCELLE                                                 None   
PRIESTESS   (Valyrian) Bought and sold, (Varys approaches...   

                                                        3   \
STANNIS     I'm giving you a chance to avenge your family.   
DAVOS                                        Have you now?   
MERYN                                                 None   
PYCELLE                                               None   
PRIESTESS            (Valyrian) He has sent you a saviour!   

                                                          4            5   \
STANNIS                         Are you bored of us already?   I know it.   
DAVOS       As long as the Boltons rule the North, (Stand...         None   
MERYN                                                   None         None   
PYCELLE                                                 None         None   
PRIESTESS                                               None         None   

                                                         6   \
STANNIS     They'd rather burn than fight for me, so be it.   
DAVOS                                                  None   
MERYN                                                  None   
PYCELLE                                                None   
PRIESTESS                                              None   

                                    7   \
STANNIS     You're the Lord Commander.   
DAVOS                             None   
MERYN                             None   
PYCELLE                           None   
PRIESTESS                         None   

                                                8   \
STANNIS     You have many enemies in Castle Black.   
DAVOS                                         None   
MERYN                                         None   
PYCELLE                                       None   
PRIESTESS                                     None   

                                                     9     10    11    12  \
STANNIS     Whoever said that didn't have many enemies.  None  None  None   
DAVOS                                              None  None  None  None   
MERYN                                              None  None  None  None   
PYCELLE                                            None  None  None  None   
PRIESTESS                                          None  None  None  None   

             13    14    15    16    17    18    19    20    21    22    23  
STANNIS    None  None  None  None  None  None  None  None  None  None  None  
DAVOS      None  None  None  None  None  None  None  None  None  None  None  
MERYN      None  None  None  None  None  None  None  None  None  None  None  
PYCELLE    None  None  None  None  None  None  None  None  None  None  None  
PRIESTESS  None  None  None  None  None  None  None  None  None  None  None

In [67]:
test3 = episode_three[0].apply(remove_stops)
test3

STANNIS                                  olly closes door
DAVOS                                      sees something
MERYN                          dont think good idea grace
PYCELLE           mans private affairs ought stay private
PRIESTESS                valyrian night dark full terrors
OLLY                     night gathers watch begins davos
TYRION                                     get wheelhouse
BAELISH                                               yes
CROWD                                              sinner
JANOS                               stands angrily shouts
ROOSE                           sent collect taxes bodies
JON                                                stands
WOMAN 2                                   seven blessings
MAN 1                                              repent
TOMMEN                                      happened fast
MAN 2                                               shame
CERSEI                       theres nothing casterly rock
VARYS         

In [68]:
for column in episode_three.columns:
    for x in range(len(episode_three[column])):
        episode_three[column][x] = remove_stops(episode_three[column][x])

In [69]:
episode_three.info()

<class 'pandas.core.frame.DataFrame'>
Index: 34 entries, STANNIS to MAN
Data columns (total 24 columns):
0     34 non-null object
1     26 non-null object
2     24 non-null object
3     24 non-null object
4     21 non-null object
5     17 non-null object
6     17 non-null object
7     16 non-null object
8     14 non-null object
9     13 non-null object
10    10 non-null object
11    10 non-null object
12    8 non-null object
13    7 non-null object
14    7 non-null object
15    6 non-null object
16    5 non-null object
17    5 non-null object
18    4 non-null object
19    3 non-null object
20    3 non-null object
21    2 non-null object
22    1 non-null object
23    1 non-null object
dtypes: object(24)
memory usage: 6.6+ KB


In [70]:
episode_three.index = episode_three.index.str.title()

episode_three.shape

(34, 24)

In [71]:
episode_three.head()

0                     1   \
Stannis                           olly closes door                  well   
Davos                               sees something  king complicated man   
Meryn                   dont think good idea grace                  None   
Pycelle    mans private affairs ought stay private                  None   
Priestess         valyrian night dark full terrors              valyrian   

                                                          2   \
Stannis                                             say word   
Davos                                      hes one true king   
Meryn                                                   None   
Pycelle                                                 None   
Priestess  valyrian bought sold varys approaches tyrion s...   

                                       3   \
Stannis    im giving chance avenge family   
Davos                                       
Meryn                                None   
Pycelle                              None   
Priestess           valyrian sent saviour   

                                                    4     5   \
Stannis                               bored us already  know   
Davos      long boltons rule north stands north suffer  None   
Meryn                                             None  None   
Pycelle                                           None  None   
Priestess                                         None  None   

                                6                     7   \
Stannis    theyd rather burn fight  youre lord commander   
Davos                         None                  None   
Meryn                         None                  None   
Pycelle                       None                  None   
Priestess                     None                  None   

                                  8                                9     10  \
Stannis    many enemies castle black  whoever said didnt many enemies  None   
Davos                           None                             None  None   
Meryn                           None                             None  None   
Pycelle                         None                             None  None   
Priestess                       None                             None  None   

             11    12    13    14    15    16    17    18    19    20    21  \
Stannis    None  None  None  None  None  None  None  None  None  None  None   
Davos      None  None  None  None  None  None  None  None  None  None  None   
Meryn      None  None  None  None  None  None  None  None  None  None  None   
Pycelle    None  None  None  None  None  None  None  None  None  None  None   
Priestess  None  None  None  None  None  None  None  None  None  None  None   

             22    23  
Stannis    None  None  
Davos      None  None  
Meryn      None  None  
Pycelle    None  None  
Priestess  None  None

### Episode Four

In [72]:
df_s5.script_text[3]

[u'TITLE SEQUENCE',
 u'\n',
 u'\n',
 u'EXT. BEACH',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'CUT TO: EXT. BOAT',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'INT. BELOW DECK',
 u'\n',
 u'\n',
 u'\n',
 u'\nBRONN: Why are we on a merchant ship? Why no Lannister sails?',
 u'\n',
 u"\nJAIME: This ship's sailing to Oldtown. We'll get off earlier, not far from Sunspear. Row ourselves to the Dornish shores in the night.",
 u'\n',
 u'\nBRONN: You ever been to Dorne?',
 u'\n',
 u'\nJAIME: No.',
 u'\n',
 u'\nBRONN: I have. The Dornish are crazy. All they want to do is fight and fuck. Fuck and fight.',
 u'\n',
 u'\nJAIME: You should be happy to go back. (Drinks some water).',
 u'\n',
 u'\nBRONN: (Gets up, walking to his knife). ',
 u" (Pulls out his knife from the sandbag). And there's nothing like a fuck-mad Dornish girl to clear your head for the next fight. It's how the two work together. And we're gonna do a lot of fighting, I am sure. Well, I am. But I don't imagine we'll get to stick around

In [73]:
script_text5_04 = df_s5.script_text[3]
print type(script_text5_04)

script_text5_04

<type 'list'>


[u'TITLE SEQUENCE',
 u'\n',
 u'\n',
 u'EXT. BEACH',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'CUT TO: EXT. BOAT',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'INT. BELOW DECK',
 u'\n',
 u'\n',
 u'\n',
 u'\nBRONN: Why are we on a merchant ship? Why no Lannister sails?',
 u'\n',
 u"\nJAIME: This ship's sailing to Oldtown. We'll get off earlier, not far from Sunspear. Row ourselves to the Dornish shores in the night.",
 u'\n',
 u'\nBRONN: You ever been to Dorne?',
 u'\n',
 u'\nJAIME: No.',
 u'\n',
 u'\nBRONN: I have. The Dornish are crazy. All they want to do is fight and fuck. Fuck and fight.',
 u'\n',
 u'\nJAIME: You should be happy to go back. (Drinks some water).',
 u'\n',
 u'\nBRONN: (Gets up, walking to his knife). ',
 u" (Pulls out his knife from the sandbag). And there's nothing like a fuck-mad Dornish girl to clear your head for the next fight. It's how the two work together. And we're gonna do a lot of fighting, I am sure. Well, I am. But I don't imagine we'll get to stick around

In [74]:
script_split4 = [i.split('\n') for i in script_text5_04]
script_split4

[[u'TITLE SEQUENCE'],
 [u'', u''],
 [u'', u''],
 [u'EXT. BEACH'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'CUT TO: EXT. BOAT'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'INT. BELOW DECK'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u'BRONN: Why are we on a merchant ship? Why no Lannister sails?'],
 [u'', u''],
 [u'',
  u"JAIME: This ship's sailing to Oldtown. We'll get off earlier, not far from Sunspear. Row ourselves to the Dornish shores in the night."],
 [u'', u''],
 [u'', u'BRONN: You ever been to Dorne?'],
 [u'', u''],
 [u'', u'JAIME: No.'],
 [u'', u''],
 [u'',
  u'BRONN: I have. The Dornish are crazy. All they want to do is fight and fuck. Fuck and fight.'],
 [u'', u''],
 [u'', u'JAIME: You should be happy to go back. (Drinks some water).'],
 [u'', u''],
 [u'', u'BRONN: (Gets up, walking to his knife). '],
 [u" (Pulls out his knife from the sandbag). And there's nothing like a fuck-mad Dornish girl to clear your head for t

In [75]:
string_script_text4 = ' '

for i in script_split4:
    for e in i:
        string_script_text4 = string_script_text4 + ' ' + e

In [76]:
string_script_text4

u'  TITLE SEQUENCE     EXT. BEACH         CUT TO: EXT. BOAT             INT. BELOW DECK        BRONN: Why are we on a merchant ship? Why no Lannister sails?    JAIME: This ship\'s sailing to Oldtown. We\'ll get off earlier, not far from Sunspear. Row ourselves to the Dornish shores in the night.    BRONN: You ever been to Dorne?    JAIME: No.    BRONN: I have. The Dornish are crazy. All they want to do is fight and fuck. Fuck and fight.    JAIME: You should be happy to go back. (Drinks some water).    BRONN: (Gets up, walking to his knife).   (Pulls out his knife from the sandbag). And there\'s nothing like a fuck-mad Dornish girl to clear your head for the next fight. It\'s how the two work together. And we\'re gonna do a lot of fighting, I am sure. Well, I am. But I don\'t imagine we\'ll get to stick around for the rest. Not after we\'ve kidnapped their princess.    JAIME: We are not kidnapping their princess. We are rescuing my niece, bringing her back to the family,    BRONN: (Incr

In [77]:
words4 = word_tokenize(string_script_text4)
words4

[u'TITLE',
 u'SEQUENCE',
 u'EXT',
 u'.',
 u'BEACH',
 u'CUT',
 u'TO',
 u':',
 u'EXT',
 u'.',
 u'BOAT',
 u'INT',
 u'.',
 u'BELOW',
 u'DECK',
 u'BRONN',
 u':',
 u'Why',
 u'are',
 u'we',
 u'on',
 u'a',
 u'merchant',
 u'ship',
 u'?',
 u'Why',
 u'no',
 u'Lannister',
 u'sails',
 u'?',
 u'JAIME',
 u':',
 u'This',
 u'ship',
 u"'s",
 u'sailing',
 u'to',
 u'Oldtown',
 u'.',
 u'We',
 u"'ll",
 u'get',
 u'off',
 u'earlier',
 u',',
 u'not',
 u'far',
 u'from',
 u'Sunspear',
 u'.',
 u'Row',
 u'ourselves',
 u'to',
 u'the',
 u'Dornish',
 u'shores',
 u'in',
 u'the',
 u'night',
 u'.',
 u'BRONN',
 u':',
 u'You',
 u'ever',
 u'been',
 u'to',
 u'Dorne',
 u'?',
 u'JAIME',
 u':',
 u'No',
 u'.',
 u'BRONN',
 u':',
 u'I',
 u'have',
 u'.',
 u'The',
 u'Dornish',
 u'are',
 u'crazy',
 u'.',
 u'All',
 u'they',
 u'want',
 u'to',
 u'do',
 u'is',
 u'fight',
 u'and',
 u'fuck',
 u'.',
 u'Fuck',
 u'and',
 u'fight',
 u'.',
 u'JAIME',
 u':',
 u'You',
 u'should',
 u'be',
 u'happy',
 u'to',
 u'go',
 u'back',
 u'.',
 u'(',
 u'Drin

In [78]:
sentences4 = sent_tokenize(string_script_text4)
sentences4

[u'  TITLE SEQUENCE     EXT.',
 u'BEACH         CUT TO: EXT.',
 u'BOAT             INT.',
 u'BELOW DECK        BRONN: Why are we on a merchant ship?',
 u'Why no Lannister sails?',
 u"JAIME: This ship's sailing to Oldtown.",
 u"We'll get off earlier, not far from Sunspear.",
 u'Row ourselves to the Dornish shores in the night.',
 u'BRONN: You ever been to Dorne?',
 u'JAIME: No.',
 u'BRONN: I have.',
 u'The Dornish are crazy.',
 u'All they want to do is fight and fuck.',
 u'Fuck and fight.',
 u'JAIME: You should be happy to go back.',
 u'(Drinks some water).',
 u'BRONN: (Gets up, walking to his knife).',
 u'(Pulls out his knife from the sandbag).',
 u"And there's nothing like a fuck-mad Dornish girl to clear your head for the next fight.",
 u"It's how the two work together.",
 u"And we're gonna do a lot of fighting, I am sure.",
 u'Well, I am.',
 u"But I don't imagine we'll get to stick around for the rest.",
 u"Not after we've kidnapped their princess.",
 u'JAIME: We are not kidnapping 

In [79]:
dialogue4 = []

for sentence in sentences4:
    words=sentence.split(':')[0]
    if len(words.split())<=2:
        if words in (names5_04):
            dialogue4.append(sentence)

In [80]:
dialogue4

[u"JAIME: This ship's sailing to Oldtown.",
 u'BRONN: You ever been to Dorne?',
 u'JAIME: No.',
 u'BRONN: I have.',
 u'JAIME: You should be happy to go back.',
 u'BRONN: (Gets up, walking to his knife).',
 u'JAIME: We are not kidnapping their princess.',
 u"BRONN: I've been doing this sort of thing a long time.",
 u"JAIME: That's why you're here.",
 u'BRONN: I know.',
 u"JAIME: Because I don't want to start a war.",
 u"BRONN: That still doesn't explain why you're doing it.",
 u'JAIME: It has to be me.',
 u'BRONN: (Gets up starts walking).',
 u'BRONN: (Sheaths his sword).',
 u'JAIME: (Quietly) Varys set him free.',
 u'BRONN: Well, if you ever see the little fucker, (Lays down), give him my regards.',
 u'JAIME: He murdered my father.',
 u'MACE: With  , half what they ask.',
 u"CERSEI: You're the Master of Coin.",
 u"MACE: Well, House Tyrell could front the gold, and the the Crown will pay us back in time, or I'll have words with my daughter.",
 u"CERSEI: You've already given us too much.

In [81]:
import pickle
with open('/Users/zoemarkovits/Metis/project_five_got/Dialogue_PKLs/s504.pkl', 'wb') as f:
    pickle.dump(dialogue4, f)

In [82]:
from collections import defaultdict

speakers4 = defaultdict(list)
for sentence in dialogue4:
    speakers4[sentence.split(':')[0]].append(sentence.split(':')[1])

speakers4

defaultdict(list,
            {u'BAELISH': [u' I saw her once.',
              u' Come.',
              u' I am.',
              u" King's Landing.",
              u' Cersei sent for me.',
              u' I know how hard it is to live with   believe me.',
              u' (They begin walking again).',
              u' I do.',
              u' He has a larger army.',
              u' Stannis takes Winterfell, he rescues you from the most despised family in the North.',
              u' Then you will take this Bolton boy, Ramsay, and make him yours.',
              u' Of course you do.',
              u" He should, he's a dangerous man."],
             u'BARRISTAN': [u' He liked to walk among the people, he liked to sing to them.',
              u' Yes.',
              u' I made sure no one killed him.',
              u' He was very good.',
              u' Rhaegar never liked killing.',
              u' Well, one time, he gave it to the next minstrel down the street.',
              u'

In [83]:
speakers4['JON']

[u' (To some of the men sparring).',
 u' Never even heard of these people.',
 u' And how many men does this Lord Maison have to send us?',
 u' Not him.',
 u' He murdered my brother.',
 u' How can I help you?',
 u' Castle Black is my home now.',
 u" You're gonna show me some vision in the fire.",
 u" I don't think Stannis would like that very much.",
 u" I can't."]

In [84]:
episode_four = pd.DataFrame.from_dict(speakers4, orient="index")
print episode_four.shape

(36, 29)


In [85]:
#from numpy import nan
#episode_four.fillna(value=str(0), inplace=True)

In [86]:
episode_four.info()

<class 'pandas.core.frame.DataFrame'>
Index: 36 entries, STANNIS to LORAS
Data columns (total 29 columns):
0     36 non-null object
1     29 non-null object
2     25 non-null object
3     21 non-null object
4     19 non-null object
5     17 non-null object
6     15 non-null object
7     12 non-null object
8     12 non-null object
9     10 non-null object
10    8 non-null object
11    7 non-null object
12    6 non-null object
13    5 non-null object
14    5 non-null object
15    3 non-null object
16    3 non-null object
17    2 non-null object
18    2 non-null object
19    2 non-null object
20    2 non-null object
21    2 non-null object
22    2 non-null object
23    2 non-null object
24    1 non-null object
25    1 non-null object
26    1 non-null object
27    1 non-null object
28    1 non-null object
dtypes: object(29)
memory usage: 8.4+ KB


In [87]:
episode_four.head()

0   \
STANNIS           Lord Commander of the Night's Watch.   
ELARIA                                     Nym, Obara.   
SELYSE                  I should have given you a son.   
PYCELLE   The Small Council grows smaller and smaller.   
DARIO                                      (Entering).   

                                                        1   \
STANNIS                                    Not your fault.   
ELARIA    Prince Doran will weep for your father, but n...   
SELYSE                                         Whose then?   
PYCELLE                                               None   
DARIO                                     Fifty a hundred.   

                                                        2          3   \
STANNIS                                           We must.   I won't.   
ELARIA                             He's come for Myrcella.       Nym?   
SELYSE                                            My Lady.       None   
PYCELLE                                               None       None   
DARIO     I think I can protect you from Hizdahr Zo Loraq.       None   

                       4                                                  5   \
STANNIS   (Walking away).   My father used to tell me that boredom indica...   
ELARIA               None                                               None   
SELYSE               None                                               None   
PYCELLE              None                                               None   
DARIO                None                                               None   

                                                        6   \
STANNIS   I know Castle Black is no place for a child, ...   
ELARIA                                                None   
SELYSE                                                None   
PYCELLE                                               None   
DARIO                                                 None   

                            7   \
STANNIS   Why do you say that?   
ELARIA                    None   
SELYSE                    None   
PYCELLE                   None   
DARIO                     None   

                                                        8     9     10    11  \
STANNIS   When you were an infant, (Stands up and walks...  None  None  None   
ELARIA                                                None  None  None  None   
SELYSE                                                None  None  None  None   
PYCELLE                                               None  None  None  None   
DARIO                                                 None  None  None  None   

           12    13    14    15    16    17    18    19    20    21    22  \
STANNIS  None  None  None  None  None  None  None  None  None  None  None   
ELARIA   None  None  None  None  None  None  None  None  None  None  None   
SELYSE   None  None  None  None  None  None  None  None  None  None  None   
PYCELLE  None  None  None  None  None  None  None  None  None  None  None   
DARIO    None  None  None  None  None  None  None  None  None  None  None   

           23    24    25    26    27    28  
STANNIS  None  None  None  None  None  None  
ELARIA   None  None  None  None  None  None  
SELYSE   None  None  None  None  None  None  
PYCELLE  None  None  None  None  None  None  
DARIO    None  None  None  None  None  None

In [88]:
test4 = episode_four[0].apply(remove_stops)
test4

STANNIS                         lord commander nights watch
ELARIA                                            nym obara
SELYSE                                            given son
PYCELLE                 small council grows smaller smaller
DARIO                                              entering
MELISANDRE                                  walking towards
BRONN                                            ever dorne
JAIME                                 ships sailing oldtown
TYRION                                                 wine
MISSANDEI                                             glory
WOMAN                                        filthy bastard
SAM                                     havent heard either
SHIREEN                      turns around holding something
KINGSGUARD                                             halt
MAN 3                                        youre born sin
JON                                            men sparring
BARRISTAN                liked walk amon

In [89]:
for column in episode_four.columns:
    for x in range(len(episode_four[column])):
        episode_four[column][x] = remove_stops(episode_four[column][x])

In [90]:
episode_four.index = episode_four.index.str.title()

episode_four.shape

(36, 29)

In [91]:
episode_four.head()

0   \
Stannis          lord commander nights watch   
Elaria                             nym obara   
Selyse                             given son   
Pycelle  small council grows smaller smaller   
Dario                               entering   

                                            1   \
Stannis                                  fault   
Elaria   prince doran weep father nothing else   
Selyse                                   whose   
Pycelle                                   None   
Dario                            fifty hundred   

                                     2     3             4   \
Stannis                            must  wont  walking away   
Elaria                hes come myrcella   nym          None   
Selyse                             lady  None          None   
Pycelle                            None  None          None   
Dario    think protect hizdahr zo loraq  None          None   

                                                        5   \
Stannis  father used tell boredom indicates lack inner ...   
Elaria                                                None   
Selyse                                                None   
Pycelle                                               None   
Dario                                                 None   

                                            6     7   \
Stannis  know castle black place child shireen   say   
Elaria                                    None  None   
Selyse                                    None  None   
Pycelle                                   None  None   
Dario                                     None  None   

                                                        8     9     10    11  \
Stannis  infant stands walks around desk dornish traile...  None  None  None   
Elaria                                                None  None  None  None   
Selyse                                                None  None  None  None   
Pycelle                                               None  None  None  None   
Dario                                                 None  None  None  None   

           12    13    14    15    16    17    18    19    20    21    22  \
Stannis  None  None  None  None  None  None  None  None  None  None  None   
Elaria   None  None  None  None  None  None  None  None  None  None  None   
Selyse   None  None  None  None  None  None  None  None  None  None  None   
Pycelle  None  None  None  None  None  None  None  None  None  None  None   
Dario    None  None  None  None  None  None  None  None  None  None  None   

           23    24    25    26    27    28  
Stannis  None  None  None  None  None  None  
Elaria   None  None  None  None  None  None  
Selyse   None  None  None  None  None  None  
Pycelle  None  None  None  None  None  None  
Dario    None  None  None  None  None  None

### Episode Five

In [92]:
df_s5.script_text[4]

[u'TITLE SEQUENCE',
 u'\n',
 u'\n',
 u'INT. ROOM',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'INT. THRONE ROOM',
 u'\n',
 u'\n',
 u'\n',
 u'\nHIZDAHR: I am so sorry, my queen. He was a good man.',
 u'\n',
 u'\nDAENERYS: ',
 u' they called him. ',
 u'. He was a loyal friend. And he died in an alley, ',
 u'.',
 u'\n',
 u'\nDAARIO: We could pull back to the ',
 u', secure it, and use it as a base from which to operate. Then we clean the city out, neighborhood by neighborhood, street by street, until the rats have nowhere left to hide.',
 u'\n',
 u'\n',
 u'\n',
 u'\nDAENERYS: ',
 u" Round up the leaders of each of Meereen's great families and bring them to me.",
 u'\n',
 u'\nHIZDAHR: ',
 u'\n',
 u'\n',
 u'\n',
 u'\nHIZDAHR: No, Your Grace! I had nothing to do with this. Your Grace!',
 u'\n',
 u'\n',
 u'INT. DRAGON CHAMBER',
 u'\n',
 u'\n',
 u'\n',
 u'\nDAENERYS: (',
 u') Walk forward.',
 u'\n',
 u'\n',
 u'\n',
 u'\nMAN: (Valyrian) You cannot do this.',
 u'\n',
 u'\n',
 u'\n',
 u'\nDAENERYS: (Valyr

In [93]:
script_text5_05 = df_s5.script_text[4]
print type(script_text5_05)

script_text5_05

<type 'list'>


[u'TITLE SEQUENCE',
 u'\n',
 u'\n',
 u'INT. ROOM',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'INT. THRONE ROOM',
 u'\n',
 u'\n',
 u'\n',
 u'\nHIZDAHR: I am so sorry, my queen. He was a good man.',
 u'\n',
 u'\nDAENERYS: ',
 u' they called him. ',
 u'. He was a loyal friend. And he died in an alley, ',
 u'.',
 u'\n',
 u'\nDAARIO: We could pull back to the ',
 u', secure it, and use it as a base from which to operate. Then we clean the city out, neighborhood by neighborhood, street by street, until the rats have nowhere left to hide.',
 u'\n',
 u'\n',
 u'\n',
 u'\nDAENERYS: ',
 u" Round up the leaders of each of Meereen's great families and bring them to me.",
 u'\n',
 u'\nHIZDAHR: ',
 u'\n',
 u'\n',
 u'\n',
 u'\nHIZDAHR: No, Your Grace! I had nothing to do with this. Your Grace!',
 u'\n',
 u'\n',
 u'INT. DRAGON CHAMBER',
 u'\n',
 u'\n',
 u'\n',
 u'\nDAENERYS: (',
 u') Walk forward.',
 u'\n',
 u'\n',
 u'\n',
 u'\nMAN: (Valyrian) You cannot do this.',
 u'\n',
 u'\n',
 u'\n',
 u'\nDAENERYS: (Valyr

In [94]:
script_split5 = [i.split('\n') for i in script_text5_05]
script_split5

[[u'TITLE SEQUENCE'],
 [u'', u''],
 [u'', u''],
 [u'INT. ROOM'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'INT. THRONE ROOM'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u'HIZDAHR: I am so sorry, my queen. He was a good man.'],
 [u'', u''],
 [u'', u'DAENERYS: '],
 [u' they called him. '],
 [u'. He was a loyal friend. And he died in an alley, '],
 [u'.'],
 [u'', u''],
 [u'', u'DAARIO: We could pull back to the '],
 [u', secure it, and use it as a base from which to operate. Then we clean the city out, neighborhood by neighborhood, street by street, until the rats have nowhere left to hide.'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u'DAENERYS: '],
 [u" Round up the leaders of each of Meereen's great families and bring them to me."],
 [u'', u''],
 [u'', u'HIZDAHR: '],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u'HIZDAHR: No, Your Grace! I had nothing to do with this. Your Grace!'],
 [u'', u''],
 [u'', u''],
 [u'INT. DRAGON CHAMBER'],
 [u'', u''],
 [u'', u''],
 [

In [95]:
string_script_text5 = ' '

for i in script_split5:
    for e in i:
        string_script_text5 = string_script_text5 + ' ' + e

In [96]:
string_script_text5

u'  TITLE SEQUENCE     INT. ROOM         INT. THRONE ROOM        HIZDAHR: I am so sorry, my queen. He was a good man.    DAENERYS:   they called him.  . He was a loyal friend. And he died in an alley,  .    DAARIO: We could pull back to the  , secure it, and use it as a base from which to operate. Then we clean the city out, neighborhood by neighborhood, street by street, until the rats have nowhere left to hide.        DAENERYS:   Round up the leaders of each of Meereen\'s great families and bring them to me.    HIZDAHR:         HIZDAHR: No, Your Grace! I had nothing to do with this. Your Grace!     INT. DRAGON CHAMBER        DAENERYS: ( ) Walk forward.        MAN: (Valyrian) You cannot do this.        DAENERYS: (Valyrian) Another step.        DAENERYS: (Valyrian)   Children. Some say I should give up on them. (One of the men is mumbling).   She disciplines them if she must.        DAENERYS: (Valyrian) But she does not give up on them.        DAENERYS: (Valyrian) Who is innocent? Mayb

In [97]:
words5 = word_tokenize(string_script_text5)
words5

[u'TITLE',
 u'SEQUENCE',
 u'INT',
 u'.',
 u'ROOM',
 u'INT',
 u'.',
 u'THRONE',
 u'ROOM',
 u'HIZDAHR',
 u':',
 u'I',
 u'am',
 u'so',
 u'sorry',
 u',',
 u'my',
 u'queen',
 u'.',
 u'He',
 u'was',
 u'a',
 u'good',
 u'man',
 u'.',
 u'DAENERYS',
 u':',
 u'they',
 u'called',
 u'him',
 u'.',
 u'.',
 u'He',
 u'was',
 u'a',
 u'loyal',
 u'friend',
 u'.',
 u'And',
 u'he',
 u'died',
 u'in',
 u'an',
 u'alley',
 u',',
 u'.',
 u'DAARIO',
 u':',
 u'We',
 u'could',
 u'pull',
 u'back',
 u'to',
 u'the',
 u',',
 u'secure',
 u'it',
 u',',
 u'and',
 u'use',
 u'it',
 u'as',
 u'a',
 u'base',
 u'from',
 u'which',
 u'to',
 u'operate',
 u'.',
 u'Then',
 u'we',
 u'clean',
 u'the',
 u'city',
 u'out',
 u',',
 u'neighborhood',
 u'by',
 u'neighborhood',
 u',',
 u'street',
 u'by',
 u'street',
 u',',
 u'until',
 u'the',
 u'rats',
 u'have',
 u'nowhere',
 u'left',
 u'to',
 u'hide',
 u'.',
 u'DAENERYS',
 u':',
 u'Round',
 u'up',
 u'the',
 u'leaders',
 u'of',
 u'each',
 u'of',
 u'Meereen',
 u"'s",
 u'great',
 u'families',
 

In [98]:
sentences5 = sent_tokenize(string_script_text5)
sentences5

[u'  TITLE SEQUENCE     INT.',
 u'ROOM         INT.',
 u'THRONE ROOM        HIZDAHR: I am so sorry, my queen.',
 u'He was a good man.',
 u'DAENERYS:   they called him.',
 u'.',
 u'He was a loyal friend.',
 u'And he died in an alley,  .',
 u'DAARIO: We could pull back to the  , secure it, and use it as a base from which to operate.',
 u'Then we clean the city out, neighborhood by neighborhood, street by street, until the rats have nowhere left to hide.',
 u"DAENERYS:   Round up the leaders of each of Meereen's great families and bring them to me.",
 u'HIZDAHR:         HIZDAHR: No, Your Grace!',
 u'I had nothing to do with this.',
 u'Your Grace!',
 u'INT.',
 u'DRAGON CHAMBER        DAENERYS: ( ) Walk forward.',
 u'MAN: (Valyrian) You cannot do this.',
 u'DAENERYS: (Valyrian) Another step.',
 u'DAENERYS: (Valyrian)   Children.',
 u'Some say I should give up on them.',
 u'(One of the men is mumbling).',
 u'She disciplines them if she must.',
 u'DAENERYS: (Valyrian) But she does not give up

In [99]:
dialogue5 = []

for sentence in sentences5:
    words=sentence.split(':')[0]
    if len(words.split())<=2:
        if words in (names5_05):
            dialogue5.append(sentence)

In [100]:
dialogue5

[u'DAENERYS:   they called him.',
 u'DAARIO: We could pull back to the  , secure it, and use it as a base from which to operate.',
 u"DAENERYS:   Round up the leaders of each of Meereen's great families and bring them to me.",
 u'HIZDAHR:         HIZDAHR: No, Your Grace!',
 u'MAN: (Valyrian) You cannot do this.',
 u'DAENERYS: (Valyrian) Another step.',
 u'DAENERYS: (Valyrian)   Children.',
 u'DAENERYS: (Valyrian) But she does not give up on them.',
 u'DAENERYS: (Valyrian) Who is innocent?',
 u"HIZDAHR: (Valyrian)         DAENERYS: Don't want to overfeed them.",
 u'AEMON:   Her last relation thousands of miles away, useless, dying.',
 u"SAM: Don't say that, Maester Aemon.",
 u'AEMON:     JON: Maester Aemon.',
 u'AEMON: Lord Commander.',
 u"JON: Sam, I'd like to speak to the maester alone.",
 u'JON: How are you feeling?',
 u'AEMON: Oh, like a hundred-year-old man slowly freezing to death.',
 u'JON: I need your advice.',
 u'AEMON: Half the men hate you already, Lord Commander.',
 u"JON: B

In [101]:
import pickle
with open('/Users/zoemarkovits/Metis/project_five_got/Dialogue_PKLs/s505.pkl', 'wb') as f:
    pickle.dump(dialogue5, f)

In [102]:
from collections import defaultdict

speakers5 = defaultdict(list)
for sentence in dialogue5:
    speakers5[sentence.split(':')[0]].append(sentence.split(':')[1])

speakers5

defaultdict(list,
            {u'AEMON': [u'   Her last relation thousands of miles away, useless, dying.',
              u'     JON',
              u' Lord Commander.',
              u' Oh, like a hundred-year-old man slowly freezing to death.',
              u' Half the men hate you already, Lord Commander.',
              u" That doesn't matter."],
             u'ALLISTER': [u" We've been fighting them all for thousands of years."],
             u'BRIENNE': [u' (Turns around).',
              u' Thank you.',
              u' Did you know Lord Eddard?',
              u' Not all of them.',
              u" I'm not talking about the Boltons.",
              u' Someone who swore to keep her safe.',
              u' Her mother.',
              u" That doesn't release me from an oath."],
             u'DAARIO': [u' We could pull back to the  , secure it, and use it as a base from which to operate.'],
             u'DAENERYS': [u'   they called him.',
              u"   Round up the leader

In [103]:
speakers5['AEMON']

[u'   Her last relation thousands of miles away, useless, dying.',
 u'     JON',
 u' Lord Commander.',
 u' Oh, like a hundred-year-old man slowly freezing to death.',
 u' Half the men hate you already, Lord Commander.',
 u" That doesn't matter."]

In [104]:
episode_five = pd.DataFrame.from_dict(speakers5, orient="index")
print episode_five.shape

(26, 30)


In [105]:
#from numpy import nan
#episode_five.fillna(value=str(0), inplace=True)

In [106]:
episode_five.info()

<class 'pandas.core.frame.DataFrame'>
Index: 26 entries, STANNIS to MAN
Data columns (total 30 columns):
0     26 non-null object
1     23 non-null object
2     23 non-null object
3     22 non-null object
4     19 non-null object
5     17 non-null object
6     15 non-null object
7     14 non-null object
8     12 non-null object
9     11 non-null object
10    7 non-null object
11    5 non-null object
12    4 non-null object
13    4 non-null object
14    4 non-null object
15    4 non-null object
16    3 non-null object
17    2 non-null object
18    2 non-null object
19    2 non-null object
20    2 non-null object
21    1 non-null object
22    1 non-null object
23    1 non-null object
24    1 non-null object
25    1 non-null object
26    1 non-null object
27    1 non-null object
28    1 non-null object
29    1 non-null object
dtypes: object(30)
memory usage: 6.3+ KB


In [107]:
episode_five.head()

0   \
STANNIS                                             Nothing.   
DAVOS                                                  What?   
GILLY                                          In the world.   
TYRION      What would make our time together truly enjoy...   
MISSANDEI                             (Valyrian) Three days.   

                                                   1   \
STANNIS                         You're Samwell Tarly?   
DAVOS                                 Uh, Your Grace.   
GILLY       Where you grew up, were there more books?   
TYRION                      I am a person who drinks.   
MISSANDEI               (Valyrian) You failed no one.   

                                                          2   \
STANNIS                       You don't look like a soldier.   
DAVOS       I'll choose a dozen men to stay and guard the...   
GILLY                                          Where's that?   
TYRION                    Have you sailed this route before?   
MISSANDEI                                All men fear death.   

                                                          3   \
STANNIS                                                 How?   
DAVOS                   It's a tough road ahead, Your Grace.   
GILLY                         I'm sorry I don't know things.   
TYRION      You're going to bring Daenerys a souvenir fro...   
MISSANDEI   Your Grace, I think that I am not fit to have...   

                                                          4   \
STANNIS                                         Dragonglass?   
DAVOS                                       Beg your pardon?   
GILLY                                 I can wash the linens.   
TYRION                 What about the demons and the flames?   
MISSANDEI   I can only tell you what I have seen, Your Gr...   

                                                          5   \
STANNIS     The Lady Melisandre told me that death marche...   
DAVOS       Aye, princess, but you won't be anywhere near...   
GILLY                                    Like Maester Aemon?   
TYRION                                                   Oh.   
MISSANDEI                                               None   

                          6                                         7   \
STANNIS           Seen what?   If Jon Snow returns with the wildlings.   
DAVOS         Yes, my queen.                               Well, I am.   
GILLY                   None                                      None   
TYRION      The Smoking Sea.                    And then they weren't.   
MISSANDEI               None                                      None   

                                          8   \
STANNIS     No need, they're coming with us.   
DAVOS                                   None   
GILLY                                   None   
TYRION           I suppose this is it, then.   
MISSANDEI                               None   

                                                          9   \
STANNIS     I hope you know what you're doing with these ...   
DAVOS                                                   None   
GILLY                                                   None   
TYRION                                        What was that?   
MISSANDEI                                               None   

                               10         11                   12  \
STANNIS                      None       None                 None   
DAVOS                        None       None                 None   
GILLY                        None       None                 None   
TYRION      Mormont, cut me free!   Mormont!   (Shakes his head).   
MISSANDEI                    None       None                 None   

                                                          13              14  \
STANNIS                                                 None            None   
DAVOS                                                   None            None   
GILLY           

In [108]:
test5 = episode_five[0].apply(remove_stops)
test5

STANNIS                                                nothing
DAVOS                                                         
GILLY                                                    world
TYRION       would make time together truly enjoyable would...
MISSANDEI                                  valyrian three days
SAM                                     dont say maester aemon
OLLY                                                 dont mean
SHIREEN                                             winterfell
DAENERYS                                                called
ROOSE                         trust find chamber suitable lady
JON                            sam id like speak maester alone
MYRANDA                                            saw staring
WALDA                                             thank ramsay
GREY WORM                                        valyrian long
THEON                                                 shouldnt
RAMSAY                                          im goin

In [109]:
for column in episode_five.columns:
    for x in range(len(episode_five[column])):
        episode_five[column][x] = remove_stops(episode_five[column][x])

In [110]:
episode_five.index = episode_five.index.str.title()

episode_five.shape

(26, 30)

In [111]:
episode_five.head()

0   \
Stannis                                              nothing   
Davos                                                          
Gilly                                                  world   
Tyrion     would make time together truly enjoyable would...   
Missandei                                valyrian three days   

                            1   \
Stannis    youre samwell tarly   
Davos                 uh grace   
Gilly               grew books   
Tyrion           person drinks   
Missandei  valyrian failed one   

                                                       2   \
Stannis                            dont look like soldier   
Davos      ill choose dozen men stay guard queen princess   
Gilly                                              wheres   
Tyrion                                       sailed route   
Missandei                                  men fear death   

                                                          3                4   \
Stannis                                                           dragonglass   
Davos                                 tough road ahead grace       beg pardon   
Gilly                              im sorry dont know things      wash linens   
Tyrion     youre going bring daenerys souvenir ancestral ...    demons flames   
Missandei                    grace think fit opinion matters  tell seen grace   

                                                5            6   \
Stannis    lady melisandre told death marches wall         seen   
Davos       aye princess wont anywhere near selyse    yes queen   
Gilly                           like maester aemon         None   
Tyrion                                          oh  smoking sea   
Missandei                                     None         None   

                                   7                      8   \
Stannis    jon snow returns wildlings  need theyre coming us   
Davos                            well                   None   
Gilly                            None                   None   
Tyrion                         werent                suppose   
Missandei                        None                   None   

                                  9                 10       11           12  \
Stannis    hope know youre wildlings              None     None         None   
Davos                           None              None     None         None   
Gilly                           None              None     None         None   
Tyrion                                mormont cut free  mormont  shakes head   
Missandei                       None              None     None         None   

                                           13            14  \
Stannis                                  None          None   
Davos                                    None          None   
Gilly                                    None          None   
Tyrion     itd kinder put daggers hearts done  without luck   
Missandei                                None          None   

                                  15    16    17    18    19    20    21  \
Stannis                         None  None  None  None  None  None  None   
Davos                           None  None  None  None  None  None  None   
Gilly                           None  None  None  None  None  None  None   
Tyrion     thats best idea youve day  None  None  None  None  None  None   
Missandei                       None  None  None  None  None  None  None   

             22    23    24    25    26    27    28    29  
Stannis    None  None  None  None  None  None  None  None  
Davos      None  None  None  None  None  None  None  None  
Gilly      None  None  None  None  None  None  None  None  
Tyrion     None  None  None  None  None  None  None  None  
Missandei  None  None  None  None  None  None  None  None

### Episode Six

In [112]:
df_s5.script_text[5]

[u'INT. HOUSE OF BLACK AND WHITE - CHAMBER',
 u'\n',
 u'\n',
 u'\n',
 u'\nARYA: What are they doing with the bodies?',
 u'\n',
 u'\nWAIF: Get back to work.',
 u'\n',
 u'\nARYA: No! I\u2019ve been here for weeks. I\u2019m not scrubbing one more corpse until you tell me why I\u2019m doing it.',
 u'\n',
 u'\nWAIF: You will know why.',
 u'\n',
 u'\nARYA: When?',
 u'\n',
 u'\nWAIF: When it\u2019s time. Not before. Get back to work.',
 u'\n',
 u'\nARYA: When do I get to play the game?',
 u'\n',
 u'\nWAIF: Game?',
 u'\n',
 u'\nARYA: The game. The game of faces.',
 u'\n',
 u'\nWAIF: You tried already. You failed.',
 u'\n',
 u'\nARYA: I didn\u2019t even know I was playing.',
 u'\n',
 u'\nWAIF: Who are you?',
 u'\n',
 u'\nARYA: No one.',
 u'\n',
 u'\nWAIF: Get back to work.',
 u'\n',
 u'\nARYA: Well who are you? What are you doing here? How\u2019d you get here?',
 u'\n',
 u'\nWAIF: ',
 u'\n',
 u'\n',
 u'\n',
 u'\nWAIF: Was that true or a lie?',
 u'\n',
 u'\nARYA: What?',
 u'\n',
 u'\nWAIF: Did y

In [113]:
script_text5_06 = df_s5.script_text[5]
print type(script_text5_06)

script_text5_06

<type 'list'>


[u'INT. HOUSE OF BLACK AND WHITE - CHAMBER',
 u'\n',
 u'\n',
 u'\n',
 u'\nARYA: What are they doing with the bodies?',
 u'\n',
 u'\nWAIF: Get back to work.',
 u'\n',
 u'\nARYA: No! I\u2019ve been here for weeks. I\u2019m not scrubbing one more corpse until you tell me why I\u2019m doing it.',
 u'\n',
 u'\nWAIF: You will know why.',
 u'\n',
 u'\nARYA: When?',
 u'\n',
 u'\nWAIF: When it\u2019s time. Not before. Get back to work.',
 u'\n',
 u'\nARYA: When do I get to play the game?',
 u'\n',
 u'\nWAIF: Game?',
 u'\n',
 u'\nARYA: The game. The game of faces.',
 u'\n',
 u'\nWAIF: You tried already. You failed.',
 u'\n',
 u'\nARYA: I didn\u2019t even know I was playing.',
 u'\n',
 u'\nWAIF: Who are you?',
 u'\n',
 u'\nARYA: No one.',
 u'\n',
 u'\nWAIF: Get back to work.',
 u'\n',
 u'\nARYA: Well who are you? What are you doing here? How\u2019d you get here?',
 u'\n',
 u'\nWAIF: ',
 u'\n',
 u'\n',
 u'\n',
 u'\nWAIF: Was that true or a lie?',
 u'\n',
 u'\nARYA: What?',
 u'\n',
 u'\nWAIF: Did y

In [114]:
script_split6 = [i.split('\n') for i in script_text5_06]
script_split6

[[u'INT. HOUSE OF BLACK AND WHITE - CHAMBER'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u'ARYA: What are they doing with the bodies?'],
 [u'', u''],
 [u'', u'WAIF: Get back to work.'],
 [u'', u''],
 [u'',
  u'ARYA: No! I\u2019ve been here for weeks. I\u2019m not scrubbing one more corpse until you tell me why I\u2019m doing it.'],
 [u'', u''],
 [u'', u'WAIF: You will know why.'],
 [u'', u''],
 [u'', u'ARYA: When?'],
 [u'', u''],
 [u'', u'WAIF: When it\u2019s time. Not before. Get back to work.'],
 [u'', u''],
 [u'', u'ARYA: When do I get to play the game?'],
 [u'', u''],
 [u'', u'WAIF: Game?'],
 [u'', u''],
 [u'', u'ARYA: The game. The game of faces.'],
 [u'', u''],
 [u'', u'WAIF: You tried already. You failed.'],
 [u'', u''],
 [u'', u'ARYA: I didn\u2019t even know I was playing.'],
 [u'', u''],
 [u'', u'WAIF: Who are you?'],
 [u'', u''],
 [u'', u'ARYA: No one.'],
 [u'', u''],
 [u'', u'WAIF: Get back to work.'],
 [u'', u''],
 [u'',
  u'ARYA: Well who are you? What are you doing he

In [115]:
string_script_text6 = ' '

for i in script_split6:
    for e in i:
        string_script_text6 = string_script_text6 + ' ' + e

In [116]:
string_script_text6

u"  INT. HOUSE OF BLACK AND WHITE - CHAMBER        ARYA: What are they doing with the bodies?    WAIF: Get back to work.    ARYA: No! I\u2019ve been here for weeks. I\u2019m not scrubbing one more corpse until you tell me why I\u2019m doing it.    WAIF: You will know why.    ARYA: When?    WAIF: When it\u2019s time. Not before. Get back to work.    ARYA: When do I get to play the game?    WAIF: Game?    ARYA: The game. The game of faces.    WAIF: You tried already. You failed.    ARYA: I didn\u2019t even know I was playing.    WAIF: Who are you?    ARYA: No one.    WAIF: Get back to work.    ARYA: Well who are you? What are you doing here? How\u2019d you get here?    WAIF:         WAIF: Was that true or a lie?    ARYA: What?    WAIF: Did you believe every word I said?        WAIF: Get back to work.     INT. HOUSE OF BLACK AND WHITE - CHAMBERS - NIGHT        JAQEN: Who are you?        JAQEN: Who are you?    ARYA: Arya.    JAQEN: And where did you come from?    ARYA: Westeros. My family 

In [117]:
words6 = word_tokenize(string_script_text6)
words6

[u'INT',
 u'.',
 u'HOUSE',
 u'OF',
 u'BLACK',
 u'AND',
 u'WHITE',
 u'-',
 u'CHAMBER',
 u'ARYA',
 u':',
 u'What',
 u'are',
 u'they',
 u'doing',
 u'with',
 u'the',
 u'bodies',
 u'?',
 u'WAIF',
 u':',
 u'Get',
 u'back',
 u'to',
 u'work',
 u'.',
 u'ARYA',
 u':',
 u'No',
 u'!',
 u'I\u2019ve',
 u'been',
 u'here',
 u'for',
 u'weeks',
 u'.',
 u'I\u2019m',
 u'not',
 u'scrubbing',
 u'one',
 u'more',
 u'corpse',
 u'until',
 u'you',
 u'tell',
 u'me',
 u'why',
 u'I\u2019m',
 u'doing',
 u'it',
 u'.',
 u'WAIF',
 u':',
 u'You',
 u'will',
 u'know',
 u'why',
 u'.',
 u'ARYA',
 u':',
 u'When',
 u'?',
 u'WAIF',
 u':',
 u'When',
 u'it\u2019s',
 u'time',
 u'.',
 u'Not',
 u'before',
 u'.',
 u'Get',
 u'back',
 u'to',
 u'work',
 u'.',
 u'ARYA',
 u':',
 u'When',
 u'do',
 u'I',
 u'get',
 u'to',
 u'play',
 u'the',
 u'game',
 u'?',
 u'WAIF',
 u':',
 u'Game',
 u'?',
 u'ARYA',
 u':',
 u'The',
 u'game',
 u'.',
 u'The',
 u'game',
 u'of',
 u'faces',
 u'.',
 u'WAIF',
 u':',
 u'You',
 u'tried',
 u'already',
 u'.',
 u'You'

In [118]:
sentences6 = sent_tokenize(string_script_text6)
sentences6

[u'  INT.',
 u'HOUSE OF BLACK AND WHITE - CHAMBER        ARYA: What are they doing with the bodies?',
 u'WAIF: Get back to work.',
 u'ARYA: No!',
 u'I\u2019ve been here for weeks.',
 u'I\u2019m not scrubbing one more corpse until you tell me why I\u2019m doing it.',
 u'WAIF: You will know why.',
 u'ARYA: When?',
 u'WAIF: When it\u2019s time.',
 u'Not before.',
 u'Get back to work.',
 u'ARYA: When do I get to play the game?',
 u'WAIF: Game?',
 u'ARYA: The game.',
 u'The game of faces.',
 u'WAIF: You tried already.',
 u'You failed.',
 u'ARYA: I didn\u2019t even know I was playing.',
 u'WAIF: Who are you?',
 u'ARYA: No one.',
 u'WAIF: Get back to work.',
 u'ARYA: Well who are you?',
 u'What are you doing here?',
 u'How\u2019d you get here?',
 u'WAIF:         WAIF: Was that true or a lie?',
 u'ARYA: What?',
 u'WAIF: Did you believe every word I said?',
 u'WAIF: Get back to work.',
 u'INT.',
 u'HOUSE OF BLACK AND WHITE - CHAMBERS - NIGHT        JAQEN: Who are you?',
 u'JAQEN: Who are you?',

In [119]:
dialogue6 = []

for sentence in sentences6:
    words=sentence.split(':')[0]
    if len(words.split())<=2:
        if words in (names5_06):
            dialogue6.append(sentence)

In [120]:
dialogue6

[u'WAIF: Get back to work.',
 u'ARYA: No!',
 u'WAIF: You will know why.',
 u'ARYA: When?',
 u'WAIF: When it\u2019s time.',
 u'ARYA: When do I get to play the game?',
 u'WAIF: Game?',
 u'ARYA: The game.',
 u'WAIF: You tried already.',
 u'ARYA: I didn\u2019t even know I was playing.',
 u'WAIF: Who are you?',
 u'ARYA: No one.',
 u'WAIF: Get back to work.',
 u'ARYA: Well who are you?',
 u'WAIF:         WAIF: Was that true or a lie?',
 u'ARYA: What?',
 u'WAIF: Did you believe every word I said?',
 u'WAIF: Get back to work.',
 u'JAQEN: Who are you?',
 u'ARYA: Arya.',
 u'JAQEN: And where did you come from?',
 u'ARYA: Westeros.',
 u'JAQEN: A lie.',
 u'ARYA: After he was executed I fled the capital.',
 u'JAQEN: A lie.',
 u'ARYA: I stabbed him in the gut.',
 u'JAQEN: A lie.',
 u'ARYA: A man called the Hound.',
 u'ARYA: Yes.',
 u'JAQEN: We never stop playing.',
 u'JORAH: I can.',
 u'TYRION: You\u2019re not hungry?',
 u'JORAH: Of course I\u2019m hungry.',
 u'TYRION: You\u2019re an awful travelling

In [121]:
import pickle
with open('/Users/zoemarkovits/Metis/project_five_got/Dialogue_PKLs/s506.pkl', 'wb') as f:
    pickle.dump(dialogue6, f)

In [122]:
from collections import defaultdict

speakers6 = defaultdict(list)
for sentence in dialogue6:
    speakers6[sentence.split(':')[0]].append(sentence.split(':')[1])

speakers6

defaultdict(list,
            {u'AREO': [u' Yes, my prince.',
              u' I remember how.',
              u' Drop you weapons!',
              u' Drop your weapons!',
              u' When you were whole, it would have been a good fight.'],
             u'ARYA': [u' No!',
              u' When?',
              u' When do I get to play the game?',
              u' The game.',
              u' I didn\u2019t even know I was playing.',
              u' No one.',
              u' Well who are you?',
              u' What?',
              u' Arya.',
              u' Westeros.',
              u' After he was executed I fled the capital.',
              u' I stabbed him in the gut.',
              u' A man called the Hound.',
              u' Yes.',
              u' Valar dohaeris.',
              u'          INT.'],
             u'BAELISH': [u' Yes?',
              u' That\u2019s quite a family to abandon.',
              u' Well done.',
              u' I\u2019m here on urgent business 

In [123]:
speakers6['ARYA']

[u' No!',
 u' When?',
 u' When do I get to play the game?',
 u' The game.',
 u' I didn\u2019t even know I was playing.',
 u' No one.',
 u' Well who are you?',
 u' What?',
 u' Arya.',
 u' Westeros.',
 u' After he was executed I fled the capital.',
 u' I stabbed him in the gut.',
 u' A man called the Hound.',
 u' Yes.',
 u' Valar dohaeris.',
 u'          INT.']

In [124]:
episode_six = pd.DataFrame.from_dict(speakers6, orient="index")
print episode_six.shape

(29, 24)


In [125]:
#from numpy import nan
#episode_six.fillna(value=str(0), inplace=True)

In [126]:
episode_six.info()

<class 'pandas.core.frame.DataFrame'>
Index: 29 entries, BRONN to MAN
Data columns (total 24 columns):
0     29 non-null object
1     25 non-null object
2     25 non-null object
3     22 non-null object
4     21 non-null object
5     20 non-null object
6     18 non-null object
7     13 non-null object
8     12 non-null object
9     12 non-null object
10    9 non-null object
11    7 non-null object
12    7 non-null object
13    7 non-null object
14    7 non-null object
15    6 non-null object
16    5 non-null object
17    5 non-null object
18    5 non-null object
19    4 non-null object
20    4 non-null object
21    3 non-null object
22    3 non-null object
23    3 non-null object
dtypes: object(24)
memory usage: 5.7+ KB


In [127]:
episode_six.head()

0   \
BRONN    I’m coming to the best part.   
JAIME       We’re trying to blend in.   
TYRION             You’re not hungry?   
MALKO         That or a galley slave.   
GIRL                        It hurts.   

                                                       1   \
BRONN                                               JAIME   
JAIME                           That’s the Water Gardens.   
TYRION   You’re an awful travelling companion, do you ...   
MALKO                                          Worthless.   
GIRL                                                 None   

                                           2   \
BRONN    Once we got the princess, then what?   
JAIME                    I like to improvise.   
TYRION            We are travelling together.   
MALKO             And then chop off his cock.   
GIRL                                     None   

                                                 3   \
BRONN                That explains the golden hand.   
JAIME                                     Myrcella.   
TYRION                                        JORAH   
MALKO    We’re bound to Volantis, not Slaver’s Bay.   
GIRL                                           None   

                                                       4   \
BRONN    Why don’t you let them have some time alone, ...   
JAIME                             Let’s speak in private.   
TYRION        Never occurred to you to ask why until now?   
MALKO                                                Him?   
GIRL                                                 None   

                                     5   \
BRONN    Let’s not do something stupid.   
JAIME                        Excellent.   
TYRION              I killed my father.   
MALKO                         Jousting.   
GIRL                               None   

                                                       6   \
BRONN                          That was something stupid.   
JAIME                       We have to go, Myrcella, now.   
TYRION   As miserable as you are, Mormont, at least yo...   
MALKO                                               Liar.   
GIRL                                                 None   

                                                       7   \
BRONN                                                None   
JAIME    You’ll be fine, I promise, but we have to--  ...   
TYRION     When I asked him about his men he knew all ...   
MALKO                                                None   
GIRL                                                 None   

                                                   8   \
BRONN                                            None   
JAIME                                            None   
TYRION   I only know what I heard    JORAH (stronger)   
MALKO                                            None   
GIRL                                             None   

                                                    9   \
BRONN                                             None   
JAIME                                             None   
TYRION   He was leading an expedition beyond the wall.   
MALKO                                             None   
GIRL                                              None   

                                10    11    12  \
BRONN                         None  None  None   
JAIME                         None  None  None   
TYRION   I believe in many things.   No.   No.   
MALKO                         None  None  None   
GIRL                          None  None  None   

                                                    13  \
BRONN                                             None   
JAIME                                             None   
TYRION   Doesn’t mean she’s going to be a great queen.   
MALKO                                             None   
GIRL                                              None   

                                        14    15                  16  \
BRONN                

In [128]:
test6 = episode_six[0].apply(remove_stops)
test6

BRONN                      im coming best part
JAIME                             trying blend
TYRION                            youre hungry
MALKO                             galley slave
GIRL                                     hurts
BAELISH                                    yes
SPARROW                   said despondent died
AREO                                yes prince
THEON             lord ramsay said im take arm
ROOSE                      lady sansa take man
MYRANDA        lord ramsay sent draw bath lady
SLAVER                              salt mines
WAIF                             get back work
SAND SNAKES                             oberyn
CERSEI          faith arrested heir highgarden
TRYSTANE                                  wont
MARGAERY                   everyone knew renly
RAMSAY                     ramsay house bolton
LANCEL                          brother lancel
OBARA                             youre coming
SANSA                                     want
JAQEN        

In [129]:
for column in episode_six.columns:
    for x in range(len(episode_six[column])):
        episode_six[column][x] = remove_stops(episode_six[column][x])

In [130]:
episode_six.index = episode_six.index.str.title()

episode_six.shape

(29, 24)

In [131]:
episode_six.head()

0                                      1   \
Bronn   im coming best part                                  jaime   
Jaime          trying blend                    thats water gardens   
Tyrion         youre hungry  youre awful travelling companion know   
Malko          galley slave                              worthless   
Girl                  hurts                                   None   

                         2                           3   \
Bronn          got princess        explains golden hand   
Jaime        like improvise                    myrcella   
Tyrion  travelling together                       jorah   
Malko             chop cock  bound volantis slavers bay   
Girl                   None                        None   

                             4                      5   \
Bronn   dont let time alone son  lets something stupid   
Jaime        lets speak private              excellent   
Tyrion       never occurred ask          killed father   
Malko                                         jousting   
Girl                       None                   None   

                                             6   \
Bronn                          something stupid   
Jaime                               go myrcella   
Tyrion  miserable mormont least father good man   
Malko                                      liar   
Girl                                       None   

                                      7                          8   \
Bronn                               None                       None   
Jaime           youll fine promise bronn                       None   
Tyrion  asked men knew stories every one  know heard jorah stronger   
Malko                               None                       None   
Girl                                None                       None   

                                    9                    10    11    12  \
Bronn                             None                 None  None  None   
Jaime                             None                 None  None  None   
Tyrion  leading expedition beyond wall  believe many things               
Malko                             None                 None  None  None   
Girl                              None                 None  None  None   

                                        13              14    15  \
Bronn                                 None            None  None   
Jaime                                 None            None  None   
Tyrion  doesnt mean shes going great queen  conquers world         
Malko                                 None            None  None   
Girl                                  None            None  None   

                   16                                       17         18  \
Bronn            None                                     None       None   
Jaime            None                                     None       None   
Tyrion  thats justice  father burned living men amusement king  wait wait   
Malko            None                                     None       None   
Girl             None                                     None       None   

                         19     20                    21           22      23  
Bronn                  None   None                  None         None    None  
Jaime                  None   None                  None         None    None  
Tyrion  wait wait wait wait  malko  fighting puts mereen  looks jorah  tyrion  
Malko                  None   None                  None         None    None  
Girl                   None   None                  None         None    None

### Episode Seven

In [132]:
df_s5.script_text[6]

[u'EXT. CASTLE BLACK',
 u'\n',
 u'\n',
 u'\n',
 u'\nJON: First Ranger, you have command of Castle Black.',
 u'\n',
 u'\nALLISER: Lord Commander, it is my duty to tell you I believe this mission to be reckless, foolhardy, ',
 u'\n',
 u'\nJON: As always, thank you for your honesty.',
 u'\n',
 u'\n',
 u'\n',
 u'\nSAM: Safe travels, Lord Commander.',
 u'\n',
 u'\nJON: Thank you, Sam.',
 u'\n',
 u'\nSAM: Oh, and\u2026',
 u'\n',
 u'\n',
 u'\n',
 u'\nJON: Me too.',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'INT. CASTLE BLACK - MAESTOR AEMON\u2019S ROOM',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'\nSAM: His little brother, Aegon. He became king.',
 u'\n',
 u'\nAEMON: And before that, he was a jolly fellow. Like this one.',
 u'\n',
 u'\n',
 u'\n',
 u'\nAEMON: Get him south, Gillyflower. Before it\u2019s too late.',
 u'\n',
 u'\n',
 u'INT. WINTERFELL - HALLWAY',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'INT. SANSA\u2019S ROOM',
 u'\n',
 u'\n',
 u'\n',
 u'\nSANSA: Theon, wait.',
 u'\n',
 u'\nTHEON: Not Theon, 

In [133]:
script_text5_07 = df_s5.script_text[6]
print type(script_text5_07)

script_text5_07

<type 'list'>


[u'EXT. CASTLE BLACK',
 u'\n',
 u'\n',
 u'\n',
 u'\nJON: First Ranger, you have command of Castle Black.',
 u'\n',
 u'\nALLISER: Lord Commander, it is my duty to tell you I believe this mission to be reckless, foolhardy, ',
 u'\n',
 u'\nJON: As always, thank you for your honesty.',
 u'\n',
 u'\n',
 u'\n',
 u'\nSAM: Safe travels, Lord Commander.',
 u'\n',
 u'\nJON: Thank you, Sam.',
 u'\n',
 u'\nSAM: Oh, and\u2026',
 u'\n',
 u'\n',
 u'\n',
 u'\nJON: Me too.',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'INT. CASTLE BLACK - MAESTOR AEMON\u2019S ROOM',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'\nSAM: His little brother, Aegon. He became king.',
 u'\n',
 u'\nAEMON: And before that, he was a jolly fellow. Like this one.',
 u'\n',
 u'\n',
 u'\n',
 u'\nAEMON: Get him south, Gillyflower. Before it\u2019s too late.',
 u'\n',
 u'\n',
 u'INT. WINTERFELL - HALLWAY',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'INT. SANSA\u2019S ROOM',
 u'\n',
 u'\n',
 u'\n',
 u'\nSANSA: Theon, wait.',
 u'\n',
 u'\nTHEON: Not Theon, 

In [134]:
script_split7 = [i.split('\n') for i in script_text5_07]
script_split7

[[u'EXT. CASTLE BLACK'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u'JON: First Ranger, you have command of Castle Black.'],
 [u'', u''],
 [u'',
  u'ALLISER: Lord Commander, it is my duty to tell you I believe this mission to be reckless, foolhardy, '],
 [u'', u''],
 [u'', u'JON: As always, thank you for your honesty.'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u'SAM: Safe travels, Lord Commander.'],
 [u'', u''],
 [u'', u'JON: Thank you, Sam.'],
 [u'', u''],
 [u'', u'SAM: Oh, and\u2026'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u'JON: Me too.'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'INT. CASTLE BLACK - MAESTOR AEMON\u2019S ROOM'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u'SAM: His little brother, Aegon. He became king.'],
 [u'', u''],
 [u'', u'AEMON: And before that, he was a jolly fellow. Like this one.'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u'AEMON: Get him south, Gillyflower. Before it\u2019s too late.'],
 [u

In [135]:
string_script_text7 = ' '

for i in script_split7:
    for e in i:
        string_script_text7 = string_script_text7 + ' ' + e

In [136]:
string_script_text7

u"  EXT. CASTLE BLACK        JON: First Ranger, you have command of Castle Black.    ALLISER: Lord Commander, it is my duty to tell you I believe this mission to be reckless, foolhardy,     JON: As always, thank you for your honesty.        SAM: Safe travels, Lord Commander.    JON: Thank you, Sam.    SAM: Oh, and\u2026        JON: Me too.         INT. CASTLE BLACK - MAESTOR AEMON\u2019S ROOM            SAM: His little brother, Aegon. He became king.    AEMON: And before that, he was a jolly fellow. Like this one.        AEMON: Get him south, Gillyflower. Before it\u2019s too late.     INT. WINTERFELL - HALLWAY         INT. SANSA\u2019S ROOM        SANSA: Theon, wait.    THEON: Not Theon, my lady. Reek.        SANSA: Help me.    THEON: You\u2019re his wife now.    SANSA: Theon    THEON: Do what he says. Do what he says or he\u2019ll hurt you.    SANSA: He already hurts me every night. All day I\u2019m locked in this room and every night he comes. It can\u2019t be worse.    THEON: It ca

In [137]:
words7 = word_tokenize(string_script_text7)
words7

[u'EXT',
 u'.',
 u'CASTLE',
 u'BLACK',
 u'JON',
 u':',
 u'First',
 u'Ranger',
 u',',
 u'you',
 u'have',
 u'command',
 u'of',
 u'Castle',
 u'Black',
 u'.',
 u'ALLISER',
 u':',
 u'Lord',
 u'Commander',
 u',',
 u'it',
 u'is',
 u'my',
 u'duty',
 u'to',
 u'tell',
 u'you',
 u'I',
 u'believe',
 u'this',
 u'mission',
 u'to',
 u'be',
 u'reckless',
 u',',
 u'foolhardy',
 u',',
 u'JON',
 u':',
 u'As',
 u'always',
 u',',
 u'thank',
 u'you',
 u'for',
 u'your',
 u'honesty',
 u'.',
 u'SAM',
 u':',
 u'Safe',
 u'travels',
 u',',
 u'Lord',
 u'Commander',
 u'.',
 u'JON',
 u':',
 u'Thank',
 u'you',
 u',',
 u'Sam',
 u'.',
 u'SAM',
 u':',
 u'Oh',
 u',',
 u'and\u2026',
 u'JON',
 u':',
 u'Me',
 u'too',
 u'.',
 u'INT',
 u'.',
 u'CASTLE',
 u'BLACK',
 u'-',
 u'MAESTOR',
 u'AEMON\u2019S',
 u'ROOM',
 u'SAM',
 u':',
 u'His',
 u'little',
 u'brother',
 u',',
 u'Aegon',
 u'.',
 u'He',
 u'became',
 u'king',
 u'.',
 u'AEMON',
 u':',
 u'And',
 u'before',
 u'that',
 u',',
 u'he',
 u'was',
 u'a',
 u'jolly',
 u'fellow',
 u'

In [138]:
sentences7 = sent_tokenize(string_script_text7)
sentences7

[u'  EXT.',
 u'CASTLE BLACK        JON: First Ranger, you have command of Castle Black.',
 u'ALLISER: Lord Commander, it is my duty to tell you I believe this mission to be reckless, foolhardy,     JON: As always, thank you for your honesty.',
 u'SAM: Safe travels, Lord Commander.',
 u'JON: Thank you, Sam.',
 u'SAM: Oh, and\u2026        JON: Me too.',
 u'INT.',
 u'CASTLE BLACK - MAESTOR AEMON\u2019S ROOM            SAM: His little brother, Aegon.',
 u'He became king.',
 u'AEMON: And before that, he was a jolly fellow.',
 u'Like this one.',
 u'AEMON: Get him south, Gillyflower.',
 u'Before it\u2019s too late.',
 u'INT.',
 u'WINTERFELL - HALLWAY         INT.',
 u'SANSA\u2019S ROOM        SANSA: Theon, wait.',
 u'THEON: Not Theon, my lady.',
 u'Reek.',
 u'SANSA: Help me.',
 u'THEON: You\u2019re his wife now.',
 u'SANSA: Theon    THEON: Do what he says.',
 u'Do what he says or he\u2019ll hurt you.',
 u'SANSA: He already hurts me every night.',
 u'All day I\u2019m locked in this room and ev

In [139]:
dialogue7 = []

for sentence in sentences7:
    words=sentence.split(':')[0]
    if len(words.split())<=2:
        if words in (names5_07):
            dialogue7.append(sentence)

In [140]:
dialogue7

[u'ALLISER: Lord Commander, it is my duty to tell you I believe this mission to be reckless, foolhardy,     JON: As always, thank you for your honesty.',
 u'SAM: Safe travels, Lord Commander.',
 u'JON: Thank you, Sam.',
 u'SAM: Oh, and\u2026        JON: Me too.',
 u'AEMON: And before that, he was a jolly fellow.',
 u'AEMON: Get him south, Gillyflower.',
 u'THEON: Not Theon, my lady.',
 u'SANSA: Help me.',
 u'THEON: You\u2019re his wife now.',
 u'SANSA: Theon    THEON: Do what he says.',
 u'SANSA: He already hurts me every night.',
 u'THEON: It can.',
 u'SANSA: What did he do to you?',
 u'THEON: Please\u2026        SANSA: You betrayed my family!',
 u'THEON: I\u2019m sorry.',
 u'SANSA: You have to help me!',
 u'THEON: He\u2019ll see us.',
 u'SANSA: My family still has friends in the North.',
 u'THEON: Reek, my lady, Reek!',
 u'SANSA: Your name is Theon Greyjoy.',
 u'GILLY: Get some sleep, Sam.',
 u'SAM: You don\u2019t know that.',
 u'GILLY: Get some sleep.',
 u'SAM: I\u2019ll stay too.',

In [141]:
import pickle
with open('/Users/zoemarkovits/Metis/project_five_got/Dialogue_PKLs/s507.pkl', 'wb') as f:
    pickle.dump(dialogue7, f)

In [142]:
from collections import defaultdict

speakers7 = defaultdict(list)
for sentence in dialogue7:
    speakers7[sentence.split(':')[0]].append(sentence.split(':')[1])

speakers7

defaultdict(list,
            {u'AEMON': [u' And before that, he was a jolly fellow.',
              u' Get him south, Gillyflower.'],
             u'ALLISER': [u' Lord Commander, it is my duty to tell you I believe this mission to be reckless, foolhardy,     JON',
              u' You\u2019re losing all your friends, Tarly.'],
             u'BAELISH': [u' I\u2019m sorry about the locale.',
              u' It felt like the safest place.',
              u' It was an establishment like no other.',
              u' The past is the past.',
              u' I promise you..    OLENNA',
              u' Cersei summoned me to King\u2019s Landing.',
              u' A piece of info that she know that I had.'],
             u'BRAND': [u' Where are you going, huh?',
              u' Even in White Harbor, I\u2019d want a kiss.',
              u' One little kiss.',
              u' A man gets lonely guarding the Wall.',
              u' There\u2019s no need to be rude.',
              u' Sam the S

In [143]:
speakers7['BAELISH']

[u' I\u2019m sorry about the locale.',
 u' It felt like the safest place.',
 u' It was an establishment like no other.',
 u' The past is the past.',
 u' I promise you..    OLENNA',
 u' Cersei summoned me to King\u2019s Landing.',
 u' A piece of info that she know that I had.']

In [144]:
episode_seven = pd.DataFrame.from_dict(speakers7, orient="index")
print episode_seven.shape

(36, 20)


In [145]:
#from numpy import nan
#episode_seven.fillna(value=str(0), inplace=True)

In [146]:
episode_seven.info()

<class 'pandas.core.frame.DataFrame'>
Index: 36 entries, STANNIS to MYRCELLA
Data columns (total 20 columns):
0     36 non-null object
1     29 non-null object
2     25 non-null object
3     25 non-null object
4     22 non-null object
5     18 non-null object
6     17 non-null object
7     14 non-null object
8     11 non-null object
9     10 non-null object
10    9 non-null object
11    7 non-null object
12    5 non-null object
13    5 non-null object
14    4 non-null object
15    3 non-null object
16    3 non-null object
17    2 non-null object
18    1 non-null object
19    1 non-null object
dtypes: object(20)
memory usage: 5.9+ KB


In [147]:
episode_seven.head()

0   \
STANNIS                                             What else?   
DAVOS                                                  STANNIS   
JORAH         Khaleesi, please, I just need a moment of you...   
SLAVE BUYER                                                20.   
MELISANDRE    You saw it yourself, my king, when you stared...   

                                                            1   \
STANNIS                Sell swords, loyal to nothing but gold.   
DAVOS         We still have a hard march to Wintefell and w...   
JORAH                                                     None   
SLAVE BUYER                                               None   
MELISANDRE                                        You do know.   

                                                            2   \
STANNIS                                                   And?   
DAVOS         This isn’t our time, we should head back to C...   
JORAH                                                     None   
SLAVE BUYER                                               None   
MELISANDRE                                I trust in the Lord.   

                                                            3   \
STANNIS                                                  DAVOS   
DAVOS         It’s better to wait for the right time than t...   
JORAH                                                     None   
SLAVE BUYER                                               None   
MELISANDRE    I have seen myself walk along the battlements...   

                                                            4   \
STANNIS       This is the right time, and I will risk every...   
DAVOS                                                     None   
JORAH                                                     None   
SLAVE BUYER                                               None   
MELISANDRE    But sometimes sacrifices must be made to ensu...   

                                    5                                 6   \
STANNIS       I don’t know what I saw.   And you, do you trust yourself?   
DAVOS                             None                              None   
JORAH                             None                              None   
SLAVE BUYER                       None                              None   
MELISANDRE                     STANNIS            Do you doubt me still?   

                                  7                                      8   \
STANNIS                Are you sure?   We don’t have Robert’s bastard here.   
DAVOS                           None                                   None   
JORAH                           None                                   None   
SLAVE BUYER                     None                                   None   
MELISANDRE    There is only one way.                                   None   

                                      9                    10         11  \
STANNIS       There must be another way.   She’s my daughter.   Get out.   
DAVOS                               None                 None       None   
JORAH                               None                 None       None   
SLAVE BUYER                         None                 None       None   
MELISANDRE                          None                 None       None   

               12    13    14    15    16    17    18    19  
STANNIS      None  None  None  None  None  None  None  None  
DAVOS        None  None  None  None  None  None  None  None  
JORAH        None  None  None  None  None  None  None  None  
SLAVE BUYER  None  None  None  None  None  None  None  None  
MELISANDRE   None  None  None  None  None  None  None  None

In [148]:
test7 = episode_seven[0].apply(remove_stops)
test7

STANNIS                                                      else
DAVOS                                                     stannis
JORAH                            khaleesi please need moment time
SLAVE BUYER                                                      
MELISANDRE                                 saw king stared flames
BRONN                                             code hurt woman
GILLY                                               get sleep sam
JAIME                                                       hands
TYRION                                                       wait
MALKO                                                            
BAELISH                                           im sorry locale
SAM                                   safe travels lord commander
SPARROW                                 decency kneel gods olenna
OLENNA                                                           
HIZDAHR         generations days leading great games customary...
DAENERYS  

In [149]:
for column in episode_seven.columns:
    for x in range(len(episode_seven[column])):
        episode_seven[column][x] = remove_stops(episode_seven[column][x])

In [150]:
episode_seven.index = episode_seven.index.str.title()

episode_seven.shape

(36, 20)

In [151]:
episode_seven.head()

0   \
Stannis                                  else   
Davos                                 stannis   
Jorah        khaleesi please need moment time   
Slave Buyer                                     
Melisandre             saw king stared flames   

                                                            1   \
Stannis                         sell swords loyal nothing gold   
Davos        still hard march wintefell wont marching anywh...   
Jorah                                                     None   
Slave Buyer                                               None   
Melisandre                                                know   

                                                       2   \
Stannis                                                     
Davos        isnt time head back castle black snow clears   
Jorah                                                None   
Slave Buyer                                          None   
Melisandre                                     trust lord   

                                                 3   \
Stannis                                       davos   
Davos        better wait right time risk everything   
Jorah                                          None   
Slave Buyer                                    None   
Melisandre    seen walk along battlements wintefell   

                                                        4              5   \
Stannis                         right time risk everything  dont know saw   
Davos                                                 None           None   
Jorah                                                 None           None   
Slave Buyer                                           None           None   
Melisandre   sometimes sacrifices must made ensure victory        stannis   

                      6        7                     8                 9   \
Stannis            trust     sure  dont roberts bastard  must another way   
Davos               None     None                  None              None   
Jorah               None     None                  None              None   
Slave Buyer         None     None                  None              None   
Melisandre   doubt still  one way                  None              None   

                        10    11    12    13    14    15    16    17    18  \
Stannis      shes daughter   get  None  None  None  None  None  None  None   
Davos                 None  None  None  None  None  None  None  None  None   
Jorah                 None  None  None  None  None  None  None  None  None   
Slave Buyer           None  None  None  None  None  None  None  None  None   
Melisandre            None  None  None  None  None  None  None  None  None   

               19  
Stannis      None  
Davos        None  
Jorah        None  
Slave Buyer  None  
Melisandre   None

### Episode Eight

In [152]:
df_s5.script_text[7]

[u'INT. MEEREEN - PYRAMID',
 u'\n',
 u'\nJORAH: Your Grace, I want to say--',
 u'\n',
 u'\nDAENERYS: You will not speak. How do I know you are who you say you are?',
 u'\n',
 u'\nTYRION: ',
 u'\n',
 u'\n',
 u'\n',
 u'\nTYRION: You want revenge against the Lannisters? ',
 u' I killed my father Tywin Lannister with a bow to the heart. I am the greatest Lannister killer of our time.',
 u'\n',
 u'\nDAENERYS: So I should welcome you into my service because you murdered members of your own family?',
 u'\n',
 u'\nTYRION: ',
 u'\n',
 u'\nDAENERYS: If you\u2019d rather return to the fighting pits just say the word.',
 u'\n',
 u'\nTYRION: ',
 u' She had no wealth, no lands, no army, only a name and a handful of supporters, most of whom probably thought they could use that name to benefit themselves. They kept her alive, moving her from place to place, often hours ahead of the men who had been sent to kill her. She was eventually sold off to some warlord on the edge of the world and that appeared

In [153]:
script_text5_08 = df_s5.script_text[7]
print type(script_text5_08)

script_text5_08

<type 'list'>


[u'INT. MEEREEN - PYRAMID',
 u'\n',
 u'\nJORAH: Your Grace, I want to say--',
 u'\n',
 u'\nDAENERYS: You will not speak. How do I know you are who you say you are?',
 u'\n',
 u'\nTYRION: ',
 u'\n',
 u'\n',
 u'\n',
 u'\nTYRION: You want revenge against the Lannisters? ',
 u' I killed my father Tywin Lannister with a bow to the heart. I am the greatest Lannister killer of our time.',
 u'\n',
 u'\nDAENERYS: So I should welcome you into my service because you murdered members of your own family?',
 u'\n',
 u'\nTYRION: ',
 u'\n',
 u'\nDAENERYS: If you\u2019d rather return to the fighting pits just say the word.',
 u'\n',
 u'\nTYRION: ',
 u' She had no wealth, no lands, no army, only a name and a handful of supporters, most of whom probably thought they could use that name to benefit themselves. They kept her alive, moving her from place to place, often hours ahead of the men who had been sent to kill her. She was eventually sold off to some warlord on the edge of the world and that appeared

In [154]:
script_split8 = [i.split('\n') for i in script_text5_08]
script_split8

[[u'INT. MEEREEN - PYRAMID'],
 [u'', u''],
 [u'', u'JORAH: Your Grace, I want to say--'],
 [u'', u''],
 [u'',
  u'DAENERYS: You will not speak. How do I know you are who you say you are?'],
 [u'', u''],
 [u'', u'TYRION: '],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u'TYRION: You want revenge against the Lannisters? '],
 [u' I killed my father Tywin Lannister with a bow to the heart. I am the greatest Lannister killer of our time.'],
 [u'', u''],
 [u'',
  u'DAENERYS: So I should welcome you into my service because you murdered members of your own family?'],
 [u'', u''],
 [u'', u'TYRION: '],
 [u'', u''],
 [u'',
  u'DAENERYS: If you\u2019d rather return to the fighting pits just say the word.'],
 [u'', u''],
 [u'', u'TYRION: '],
 [u' She had no wealth, no lands, no army, only a name and a handful of supporters, most of whom probably thought they could use that name to benefit themselves. They kept her alive, moving her from place to place, often hours ahead of the men who had been sen

In [155]:
string_script_text8 = ' '

for i in script_split8:
    for e in i:
        string_script_text8 = string_script_text8 + ' ' + e

In [156]:
string_script_text8

u"  INT. MEEREEN - PYRAMID    JORAH: Your Grace, I want to say--    DAENERYS: You will not speak. How do I know you are who you say you are?    TYRION:         TYRION: You want revenge against the Lannisters?   I killed my father Tywin Lannister with a bow to the heart. I am the greatest Lannister killer of our time.    DAENERYS: So I should welcome you into my service because you murdered members of your own family?    TYRION:     DAENERYS: If you\u2019d rather return to the fighting pits just say the word.    TYRION:   She had no wealth, no lands, no army, only a name and a handful of supporters, most of whom probably thought they could use that name to benefit themselves. They kept her alive, moving her from place to place, often hours ahead of the men who had been sent to kill her. She was eventually sold off to some warlord on the edge of the world and that appeared to be that. And then a few years later the most well informed person I knew told me that this girl without wealth, l

In [157]:
words8 = word_tokenize(string_script_text8)
words8

[u'INT',
 u'.',
 u'MEEREEN',
 u'-',
 u'PYRAMID',
 u'JORAH',
 u':',
 u'Your',
 u'Grace',
 u',',
 u'I',
 u'want',
 u'to',
 u'say',
 u'--',
 u'DAENERYS',
 u':',
 u'You',
 u'will',
 u'not',
 u'speak',
 u'.',
 u'How',
 u'do',
 u'I',
 u'know',
 u'you',
 u'are',
 u'who',
 u'you',
 u'say',
 u'you',
 u'are',
 u'?',
 u'TYRION',
 u':',
 u'TYRION',
 u':',
 u'You',
 u'want',
 u'revenge',
 u'against',
 u'the',
 u'Lannisters',
 u'?',
 u'I',
 u'killed',
 u'my',
 u'father',
 u'Tywin',
 u'Lannister',
 u'with',
 u'a',
 u'bow',
 u'to',
 u'the',
 u'heart',
 u'.',
 u'I',
 u'am',
 u'the',
 u'greatest',
 u'Lannister',
 u'killer',
 u'of',
 u'our',
 u'time',
 u'.',
 u'DAENERYS',
 u':',
 u'So',
 u'I',
 u'should',
 u'welcome',
 u'you',
 u'into',
 u'my',
 u'service',
 u'because',
 u'you',
 u'murdered',
 u'members',
 u'of',
 u'your',
 u'own',
 u'family',
 u'?',
 u'TYRION',
 u':',
 u'DAENERYS',
 u':',
 u'If',
 u'you\u2019d',
 u'rather',
 u'return',
 u'to',
 u'the',
 u'fighting',
 u'pits',
 u'just',
 u'say',
 u'the',

In [158]:
sentences8 = sent_tokenize(string_script_text8)
sentences8

[u'  INT.',
 u'MEEREEN - PYRAMID    JORAH: Your Grace, I want to say--    DAENERYS: You will not speak.',
 u'How do I know you are who you say you are?',
 u'TYRION:         TYRION: You want revenge against the Lannisters?',
 u'I killed my father Tywin Lannister with a bow to the heart.',
 u'I am the greatest Lannister killer of our time.',
 u'DAENERYS: So I should welcome you into my service because you murdered members of your own family?',
 u'TYRION:     DAENERYS: If you\u2019d rather return to the fighting pits just say the word.',
 u'TYRION:   She had no wealth, no lands, no army, only a name and a handful of supporters, most of whom probably thought they could use that name to benefit themselves.',
 u'They kept her alive, moving her from place to place, often hours ahead of the men who had been sent to kill her.',
 u'She was eventually sold off to some warlord on the edge of the world and that appeared to be that.',
 u'And then a few years later the most well informed person I kne

In [159]:
dialogue8 = []

for sentence in sentences8:
    words=sentence.split(':')[0]
    if len(words.split())<=2:
        if words in (names5_08):
            dialogue8.append(sentence)

/Users/zoemarkovits/anaconda/lib/python2.7/site-packages/ipykernel_launcher.py:6: UnicodeWarning: Unicode equal comparison failed to convert both arguments to Unicode - interpreting them as being unequal
  


In [160]:
dialogue8

[u'TYRION:         TYRION: You want revenge against the Lannisters?',
 u'DAENERYS: So I should welcome you into my service because you murdered members of your own family?',
 u'TYRION:     DAENERYS: If you\u2019d rather return to the fighting pits just say the word.',
 u'TYRION:   She had no wealth, no lands, no army, only a name and a handful of supporters, most of whom probably thought they could use that name to benefit themselves.',
 u'DAENERYS: And why are you worth meeting?',
 u'TYRION: Because you can not build a better world on your own.',
 u'DAENERYS:     TYRION:   When I served as Hand of the King I did quite well with the latter considering the king in question preferred torturing animals to leading his people.',
 u'DAENERYS: So you want to advise me.',
 u'TYRION: I know.',
 u'DAENERYS: Why should the people trust a queen who can\u2019t keep her promises?',
 u'TYRION: Whomever Ser Jorah was when he started informing on you, he is no longer that man.',
 u'TYRION: Did he have 

In [161]:
import pickle
with open('/Users/zoemarkovits/Metis/project_five_got/Dialogue_PKLs/s508.pkl', 'wb') as f:
    pickle.dump(dialogue8, f)

In [162]:
from collections import defaultdict

speakers8 = defaultdict(list)
for sentence in dialogue8:
    speakers8[sentence.split(':')[0]].append(sentence.split(':')[1])

speakers8

defaultdict(list,
            {u'ARYA': [u' How will she serve him?',
              u' What will she do there?',
              u' See what?',
              u'         ARYA',
              u' Best in the city.',
              u' So why would a captain make the wager in the first place?',
              u' If the captain dies, the thin man pays his family a lot of money.',
              u' The Many Faced God.',
              u' And then what?'],
             u'BROTHER': [u' But you\u2019ll never make it--    JON'],
             u'CERSEI': [u' My son.',
              u' My face will be the last thing you see before--         INT.',
              u' The charges?',
              u' All lies.',
              u' You need to talk to him, you need to talk to my son to come and see me, come and see his mother.',
              u' I can\u2019t stay here.',
              u' Confess?',
              u' I\u2019ll get out of here, you realize.'],
             u'DAENERYS': [u' So I should welcome you in

In [163]:
speakers8['ARYA']

[u' How will she serve him?',
 u' What will she do there?',
 u' See what?',
 u'         ARYA',
 u' Best in the city.',
 u' So why would a captain make the wager in the first place?',
 u' If the captain dies, the thin man pays his family a lot of money.',
 u' The Many Faced God.',
 u' And then what?']

In [164]:
episode_eight = pd.DataFrame.from_dict(speakers8, orient="index")
print episode_eight.shape

(27, 31)


In [165]:
#from numpy import nan
#episode_eight.fillna(value=str(0), inplace=True)

In [166]:
episode_eight.info()

<class 'pandas.core.frame.DataFrame'>
Index: 27 entries, KARSI to MAN
Data columns (total 31 columns):
0     27 non-null object
1     21 non-null object
2     17 non-null object
3     17 non-null object
4     14 non-null object
5     13 non-null object
6     12 non-null object
7     12 non-null object
8     10 non-null object
9     9 non-null object
10    7 non-null object
11    6 non-null object
12    6 non-null object
13    4 non-null object
14    4 non-null object
15    4 non-null object
16    4 non-null object
17    3 non-null object
18    3 non-null object
19    3 non-null object
20    3 non-null object
21    2 non-null object
22    2 non-null object
23    2 non-null object
24    2 non-null object
25    2 non-null object
26    2 non-null object
27    1 non-null object
28    1 non-null object
29    1 non-null object
30    1 non-null object
dtypes: object(31)
memory usage: 6.8+ KB


In [167]:
episode_eight.head()

0                         1   \
KARSI      You built that wall to keep us out.   Beat the white walkers?   
BROTHER      But you’ll never make it--    JON                      None   
OLLY                                     Olly.    I heard what happened.   
TYRION                                  TYRION                  DAENERYS   
DAUGHTER                  I wanna go with you.                      None   

                                                         2   \
KARSI              There are old stories about Dragonglass.   
BROTHER                                                None   
OLLY                               Figured you were hungry.   
TYRION       She had no wealth, no lands, no army, only ...   
DAUGHTER                                               None   

                                                         3   \
KARSI      And with the things we’ve seen you don’t beli...   
BROTHER                                                None   
OLLY                           Wanted to ask you something.   
TYRION     Because you can not build a better world on y...   
DAUGHTER                                               None   

                                       4   \
KARSI                Come with you where?   
BROTHER                              None   
OLLY       It’s about the Lord Commander.   
TYRION                            I know.   
DAUGHTER                             None   

                                                         5   \
KARSI                                                  If…?   
BROTHER                                                None   
OLLY       He’s going up to Hardhome to save all them wi...   
TYRION     Whomever Ser Jorah was when he started inform...   
DAUGHTER                                               None   

                                                         6   \
KARSI      I lost my father, my uncle, and 2 brothers fi...   
BROTHER                                                None   
OLLY                                   This wasn’t a fight.   
TYRION     Did he have an opportunity to confess his bet...   
DAUGHTER                                               None   

                                                         7   \
KARSI                      You vouch for this man, Tormund?   
BROTHER                                                None   
OLLY       The one he’s travelling with, the one with th...   
TYRION                                          And did he?   
DAUGHTER                                               None   

                                                         8   \
KARSI            So would mine, but fuck 'em, they’re dead.   
BROTHER                                                None   
OLLY       But what if we let the wildings through the g...   
TYRION                                     He worships you.   
DAUGHTER                                               None   

                                                         9   \
KARSI                       Johnna is gonna look after you.   
BROTHER                                                None   
OLLY                                      You believe that?   
TYRION     A ruler who kills those that are devoted to h...   
DAUGHTER                                               None   

                                                         10  \
KARSI             I need to get the old folks on the boats.   
BROTHER                                                None   
OLLY                                                   None   
TYRION     Have you decided yet whether you’re going to ...   
DAUGHTER                                               None   

                                          11  \
KARSI                        So should you !   
BROTHER                                 None   
OLLY                                    None   
TYRION     I can see why you would think so.   
DAUGHTER                                None

In [168]:
test8 = episode_eight[0].apply(remove_stops)
test8

KARSI                                  built wall keep us
BROTHER                              youll never make jon
OLLY                                                 olly
TYRION                                             tyrion
DAUGHTER                                         wanna go
SAM                                                      
MASTER                                             struck
DAENERYS          welcome service murdered members family
ROOSE                            high stannis horses jump
JON                                          hes prisoner
GIANT                                             tormund
LOBODA                        since crows give shits live
THEON                                               theon
CERSEI                                                son
WILDLING ELDER                                 im tormund
QYBURN             fornication treason murder king robert
RAMSAY                                 stannis isnt north
GILLY         

In [169]:
for column in episode_eight.columns:
    for x in range(len(episode_eight[column])):
        episode_eight[column][x] = remove_stops(episode_eight[column][x])

In [170]:
episode_eight.index = episode_eight.index.str.title()

episode_eight.shape

(27, 31)

In [171]:
episode_eight.head()

0                   1   \
Karsi       built wall keep us  beat white walkers   
Brother   youll never make jon                None   
Olly                      olly      heard happened   
Tyrion                  tyrion            daenerys   
Daughter              wanna go                None   

                                                         2   \
Karsi                               old stories dragonglass   
Brother                                                None   
Olly                                         figured hungry   
Tyrion    wealth lands army name handful supporters prob...   
Daughter                                               None   

                                     3               4   \
Karsi     things weve seen dont believe            come   
Brother                            None            None   
Olly               wanted ask something  lord commander   
Tyrion               build better world            know   
Daughter                           None            None   

                                                       5   \
Karsi                                                       
Brother                                              None   
Olly                    hes going hardhome save wildlings   
Tyrion    whomever ser jorah started informing longer man   
Daughter                                             None   

                                                      6   \
Karsi     lost father uncle brothers fighting damn crows   
Brother                                             None   
Olly                                         wasnt fight   
Tyrion                     opportunity confess betrayals   
Daughter                                            None   

                                                         7   \
Karsi                                     vouch man tormund   
Brother                                                None   
Olly      one hes travelling one red beard led raid village   
Tyrion                                                        
Daughter                                               None   

                                            8   \
Karsi           would mine fuck em theyre dead   
Brother                                   None   
Olly      let wildings gates cut throats sleep   
Tyrion                                worships   
Daughter                                  None   

                                                   9   \
Karsi                               johnna gonna look   
Brother                                          None   
Olly                                          believe   
Tyrion    ruler kills devoted ruler inspires devotion   
Daughter                                         None   

                                              10               11  \
Karsi                   need get old folks boats                    
Brother                                     None             None   
Olly                                        None             None   
Tyrion    decided yet whether youre going killed  see would think   
Daughter                                    None             None   

                                             12  \
Karsi     dont think youre gonna enforce orders   
Brother                                    None   
Olly                                       None   
Tyrion                                   father   
Daughter                                   None   

                                                 13        14       15  \
Karsi                                          None      None     None   
Brother                                        None      None     None   
Olly                                           None      None     None   
Tyrion    day decide execute ill tell killed father  daenerys  danerys   
Daughter                                       None      None     None   

                               16                  

### Episode Nine

In [172]:
df_s5.script_text[8]

[u'EXT. STANNIS\u2019 CAMP - NIGHT',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'INT. MELISANDRE\u2019S TENT',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'EXT. STANNIS\u2019 CAMP - NIGHT',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'EXT. STANNIS\u2019 CAMP - MORNING',
 u'\n',
 u'\nDAVOS: ',
 u' They were in and out before anyone spotted them, burnt our food stores to the ground, all our siege weapons were destroyed, dozens of tents were--',
 u'\n',
 u'\nSTANNIS: Horses?',
 u'\n',
 u'\nDAVOS: ',
 u'\n',
 u'\nSTANNIS: 20 men rode into our camp without a single guard sounding the alarm?',
 u'\n',
 u'\nDAVOS: The northerners know more about their land than we ever will.',
 u'\n',
 u'\nSTANNIS: Put last night\u2019s guards in chains, either they fell asleep or they were conspiring with the enemy. Find out the truth and then hang them.',
 u'\n',
 u'\nDAVOS: Unless there\u2019s a thaw, we can\u2019t press forward to Winterfell, and we don\u2019t have enough food to get us back to Castle Black.',
 u'\n',
 u'\nSTANNIS: W

In [173]:
script_text5_09 = df_s5.script_text[8]
print type(script_text5_09)

script_text5_09

<type 'list'>


[u'EXT. STANNIS\u2019 CAMP - NIGHT',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'INT. MELISANDRE\u2019S TENT',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'EXT. STANNIS\u2019 CAMP - NIGHT',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'EXT. STANNIS\u2019 CAMP - MORNING',
 u'\n',
 u'\nDAVOS: ',
 u' They were in and out before anyone spotted them, burnt our food stores to the ground, all our siege weapons were destroyed, dozens of tents were--',
 u'\n',
 u'\nSTANNIS: Horses?',
 u'\n',
 u'\nDAVOS: ',
 u'\n',
 u'\nSTANNIS: 20 men rode into our camp without a single guard sounding the alarm?',
 u'\n',
 u'\nDAVOS: The northerners know more about their land than we ever will.',
 u'\n',
 u'\nSTANNIS: Put last night\u2019s guards in chains, either they fell asleep or they were conspiring with the enemy. Find out the truth and then hang them.',
 u'\n',
 u'\nDAVOS: Unless there\u2019s a thaw, we can\u2019t press forward to Winterfell, and we don\u2019t have enough food to get us back to Castle Black.',
 u'\n',
 u'\nSTANNIS: W

In [174]:
script_split9 = [i.split('\n') for i in script_text5_09]
script_split9

[[u'EXT. STANNIS\u2019 CAMP - NIGHT'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'INT. MELISANDRE\u2019S TENT'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'EXT. STANNIS\u2019 CAMP - NIGHT'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'EXT. STANNIS\u2019 CAMP - MORNING'],
 [u'', u''],
 [u'', u'DAVOS: '],
 [u' They were in and out before anyone spotted them, burnt our food stores to the ground, all our siege weapons were destroyed, dozens of tents were--'],
 [u'', u''],
 [u'', u'STANNIS: Horses?'],
 [u'', u''],
 [u'', u'DAVOS: '],
 [u'', u''],
 [u'',
  u'STANNIS: 20 men rode into our camp without a single guard sounding the alarm?'],
 [u'', u''],
 [u'',
  u'DAVOS: The northerners know more about their land than we ever will.'],
 [u'', u''],
 [u'',
  u'STANNIS: Put last night\u2019s guards in chains, either they fell asleep or they were conspiring with the enemy. Find out the truth and then hang them.'],
 [u'', u''],
 [u'',
  u'DAVOS: Unless there\u20

In [175]:
string_script_text9 = ' '

for i in script_split9:
    for e in i:
        string_script_text9 = string_script_text9 + ' ' + e

In [176]:
string_script_text9

u"  EXT. STANNIS\u2019 CAMP - NIGHT         INT. MELISANDRE\u2019S TENT         EXT. STANNIS\u2019 CAMP - NIGHT         EXT. STANNIS\u2019 CAMP - MORNING    DAVOS:   They were in and out before anyone spotted them, burnt our food stores to the ground, all our siege weapons were destroyed, dozens of tents were--    STANNIS: Horses?    DAVOS:     STANNIS: 20 men rode into our camp without a single guard sounding the alarm?    DAVOS: The northerners know more about their land than we ever will.    STANNIS: Put last night\u2019s guards in chains, either they fell asleep or they were conspiring with the enemy. Find out the truth and then hang them.    DAVOS: Unless there\u2019s a thaw, we can\u2019t press forward to Winterfell, and we don\u2019t have enough food to get us back to Castle Black.    STANNIS: We\u2019re not returning to Castle Black.    DAVOS: Forgive me, Your Grace, I never claimed to be an expert in military matters. But if we can\u2019t march forward, and we won\u2019t march

In [177]:
words9 = word_tokenize(string_script_text9)
words9

[u'EXT',
 u'.',
 u'STANNIS\u2019',
 u'CAMP',
 u'-',
 u'NIGHT',
 u'INT',
 u'.',
 u'MELISANDRE\u2019S',
 u'TENT',
 u'EXT',
 u'.',
 u'STANNIS\u2019',
 u'CAMP',
 u'-',
 u'NIGHT',
 u'EXT',
 u'.',
 u'STANNIS\u2019',
 u'CAMP',
 u'-',
 u'MORNING',
 u'DAVOS',
 u':',
 u'They',
 u'were',
 u'in',
 u'and',
 u'out',
 u'before',
 u'anyone',
 u'spotted',
 u'them',
 u',',
 u'burnt',
 u'our',
 u'food',
 u'stores',
 u'to',
 u'the',
 u'ground',
 u',',
 u'all',
 u'our',
 u'siege',
 u'weapons',
 u'were',
 u'destroyed',
 u',',
 u'dozens',
 u'of',
 u'tents',
 u'were',
 u'--',
 u'STANNIS',
 u':',
 u'Horses',
 u'?',
 u'DAVOS',
 u':',
 u'STANNIS',
 u':',
 u'20',
 u'men',
 u'rode',
 u'into',
 u'our',
 u'camp',
 u'without',
 u'a',
 u'single',
 u'guard',
 u'sounding',
 u'the',
 u'alarm',
 u'?',
 u'DAVOS',
 u':',
 u'The',
 u'northerners',
 u'know',
 u'more',
 u'about',
 u'their',
 u'land',
 u'than',
 u'we',
 u'ever',
 u'will',
 u'.',
 u'STANNIS',
 u':',
 u'Put',
 u'last',
 u'night\u2019s',
 u'guards',
 u'in',
 u'cha

In [178]:
sentences9 = sent_tokenize(string_script_text9)
sentences9

[u'  EXT.',
 u'STANNIS\u2019 CAMP - NIGHT         INT.',
 u'MELISANDRE\u2019S TENT         EXT.',
 u'STANNIS\u2019 CAMP - NIGHT         EXT.',
 u'STANNIS\u2019 CAMP - MORNING    DAVOS:   They were in and out before anyone spotted them, burnt our food stores to the ground, all our siege weapons were destroyed, dozens of tents were--    STANNIS: Horses?',
 u'DAVOS:     STANNIS: 20 men rode into our camp without a single guard sounding the alarm?',
 u'DAVOS: The northerners know more about their land than we ever will.',
 u'STANNIS: Put last night\u2019s guards in chains, either they fell asleep or they were conspiring with the enemy.',
 u'Find out the truth and then hang them.',
 u'DAVOS: Unless there\u2019s a thaw, we can\u2019t press forward to Winterfell, and we don\u2019t have enough food to get us back to Castle Black.',
 u'STANNIS: We\u2019re not returning to Castle Black.',
 u'DAVOS: Forgive me, Your Grace, I never claimed to be an expert in military matters.',
 u'But if we can\u2

In [179]:
dialogue9 = []

for sentence in sentences9:
    words=sentence.split(':')[0]
    if len(words.split())<=2:
        if words in (names5_09):
            dialogue9.append(sentence)

In [180]:
dialogue9

[u'DAVOS:     STANNIS: 20 men rode into our camp without a single guard sounding the alarm?',
 u'DAVOS: The northerners know more about their land than we ever will.',
 u'STANNIS: Put last night\u2019s guards in chains, either they fell asleep or they were conspiring with the enemy.',
 u'DAVOS: Unless there\u2019s a thaw, we can\u2019t press forward to Winterfell, and we don\u2019t have enough food to get us back to Castle Black.',
 u'STANNIS: We\u2019re not returning to Castle Black.',
 u'DAVOS: Forgive me, Your Grace, I never claimed to be an expert in military matters.',
 u'SAM: It wasn\u2019t.',
 u'JON: I went to save them, I failed.',
 u'SAM: You didn\u2019t fail him, or him, or her.',
 u'JON: I don\u2019t think that fact\u2019s lost on them.',
 u'ALLISER:      INT.',
 u'STANNIS: Find you some healthy horses and a few good men to guard you, I\u2019m sending you back to Castle Black.',
 u'DAVOS: Your Grace, you\u2019ve named me your Hand.',
 u'STANNIS: Yes.',
 u'DAVOS: The King\u20

In [181]:
import pickle
with open('/Users/zoemarkovits/Metis/project_five_got/Dialogue_PKLs/s509.pkl', 'wb') as f:
    pickle.dump(dialogue9, f)

In [182]:
from collections import defaultdict

speakers9 = defaultdict(list)
for sentence in dialogue9:
    speakers9[sentence.split(':')[0]].append(sentence.split(':')[1])

speakers9

defaultdict(list,
            {u'ALLISER': [u'      INT.'],
             u'ANNOUNCER': [u' My queen, our first contest.',
              u' A Meereenese champion?',
              u' ...or a Westerosi Knight?!'],
             u'AREO': [u' You\u2019ll find out very soon.'],
             u'ARYA': [u' Oysters, clams, and cockels!',
              u'  .',
              u' Tomorrow.'],
             u'BANKER': [u' Lord Tyrell!',
              u' And how goes the harvest in the Reach?',
              u' I\u2019m afraid I don\u2019t partake.',
              u' Most unfortunate for the glovers.',
              u' We are not gamblers here at the Iron Bank, Lord Tyrell.',
              u" I don't have that gift."],
             u'BRONN': [u' Am I going to be happy at the end of this walk?',
              u' Prince.',
              u' I\u2019m glad to hear it.'],
             u'DAARIO': [u' That one, the smaller man, no question, that\u2019s where you should put your money.',
              u' People 

In [183]:
speakers9['ARYA']

[u' Oysters, clams, and cockels!', u'  .', u' Tomorrow.']

In [184]:
episode_nine = pd.DataFrame.from_dict(speakers9, orient="index")
print episode_nine.shape

(36, 16)


In [185]:
#from numpy import nan
#episode_nine.fillna(value=str(0), inplace=True)

In [186]:
episode_nine.info()

<class 'pandas.core.frame.DataFrame'>
Index: 36 entries, STANNIS to MAN
Data columns (total 16 columns):
0     36 non-null object
1     28 non-null object
2     22 non-null object
3     16 non-null object
4     13 non-null object
5     12 non-null object
6     10 non-null object
7     9 non-null object
8     6 non-null object
9     6 non-null object
10    5 non-null object
11    4 non-null object
12    4 non-null object
13    4 non-null object
14    3 non-null object
15    2 non-null object
dtypes: object(16)
memory usage: 4.8+ KB


In [187]:
episode_nine.head()

0   \
STANNIS     Put last night’s guards in chains, either the...   
DAVOS                                                STANNIS   
SELYSE                             It’s what the Lord wants.   
MERYN                                                  MERYN   
ANNOUNCER                       My queen, our first contest.   

                                                          1   \
STANNIS                 We’re not returning to Castle Black.   
DAVOS       The northerners know more about their land th...   
SELYSE      If we don’t act then we’ll all starve here al...   
MERYN                                        Oh, I’m buying.   
ANNOUNCER                             A Meereenese champion?   

                                                          2   \
STANNIS     Find you some healthy horses and a few good m...   
DAVOS       Unless there’s a thaw, we can’t press forward...   
SELYSE                             No...            DAENERYS   
MERYN                                               Too old.   
ANNOUNCER                         ...or a Westerosi Knight?!   

                                                          3   \
STANNIS                                                 Yes.   
DAVOS       Forgive me, Your Grace, I never claimed to be...   
SELYSE                                                  None   
MERYN                                               Too old.   
ANNOUNCER                                               None   

                                                          4   \
STANNIS     You’re not abandoning me, you’re obeying a co...   
DAVOS                 Your Grace, you’ve named me your Hand.   
SELYSE                                                  None   
MERYN                        Do you have what I want or not?   
ANNOUNCER                                               None   

                                                          5   \
STANNIS     And if Jon Snow refuses a boy with a scroll, ...   
DAVOS       The King’s Hand should never abandon the King...   
SELYSE                                                  None   
MERYN                                                  Good.   
ANNOUNCER                                               None   

                                                         6   \
STANNIS                            My family stays with me.   
DAVOS       A boy with a scroll could deliver this message.   
SELYSE                                                 None   
MERYN                        I’ll tell you when we’re done.   
ANNOUNCER                                              None   

                                                          7   \
STANNIS                                     What’s it about?   
DAVOS       Your Grace, perhaps Queen and Princess Shiree...   
SELYSE                                                  None   
MERYN               You’ll have a fresh one for me tomorrow.   
ANNOUNCER                                               None   

                                 8   \
STANNIS     “The dance of dragons”?   
DAVOS                       STANNIS   
SELYSE                         None   
MERYN                          None   
ANNOUNCER                      None   

                                                          9   \
STANNIS                             Doesn’t make much sense.   
DAVOS       Thus ending the dragonslaying career of Ser B...   
SELYSE                                                  None   
MERYN                                                   None   
ANNOUNCER                                               None   

                                                          10  \
STANNIS     If you had to choose between Rhaenyra and Aeg...   
DAVOS                                        Do you like it?   
SELYSE                                                  None   
MERYN                                                   None   
ANNOUNCER                                   

In [188]:
test9 = episode_nine[0].apply(remove_stops)
test9

STANNIS            put last nights guards chains either fell asle...
DAVOS                                                        stannis
SELYSE                                                    lord wants
MERYN                                                          meryn
ANNOUNCER                                        queen first contest
MELISANDRE                                             soon princess
BRONN                                           going happy end walk
TYENE                                               youre going miss
JAIME                                              princess myrcella
TYRION                                                        tyrion
QUICK                              fight die glory oh glorious queen
STRONG                             fight die glory oh glorious queen
PROSTITUTE                                          oh let im hungry
ELLARIA                                                        dorne
SAM                               

In [189]:
for column in episode_nine.columns:
    for x in range(len(episode_nine[column])):
        episode_nine[column][x] = remove_stops(episode_nine[column][x])

In [190]:
episode_nine.index = episode_nine.index.str.title()

episode_nine.shape

(36, 16)

In [191]:
episode_nine.head()

0   \
Stannis    put last nights guards chains either fell asle...   
Davos                                                stannis   
Selyse                                            lord wants   
Meryn                                                  meryn   
Announcer                                queen first contest   

                                                          1   \
Stannis                               returning castle black   
Davos                             northerners know land ever   
Selyse     dont act well starve us make sacrifice melisandre   
Meryn                                           oh im buying   
Announcer                                meereenese champion   

                                                          2   \
Stannis    find healthy horses good men guard im sending ...   
Davos      unless theres thaw cant press forward winterfe...   
Selyse                                              daenerys   
Meryn                                                    old   
Announcer                                   westerosi knight   

                                                          3   \
Stannis                                                  yes   
Davos      forgive grace never claimed expert military ma...   
Selyse                                                  None   
Meryn                                                    old   
Announcer                                               None   

                                               4   \
Stannis    youre abandoning youre obeying command   
Davos                      grace youve named hand   
Selyse                                       None   
Meryn                                        want   
Announcer                                    None   

                                                          5   \
Stannis                  jon snow refuses boy scroll boy say   
Davos      kings hand never abandon king especially time war   
Selyse                                                  None   
Meryn                                                   good   
Announcer                                               None   

                                         6   \
Stannis                        family stays   
Davos      boy scroll could deliver message   
Selyse                                 None   
Meryn                         ill tell done   
Announcer                              None   

                                                          7              8   \
Stannis                                                whats  dance dragons   
Davos      grace perhaps queen princess shireen could acc...        stannis   
Selyse                                                  None           None   
Meryn                               youll fresh one tomorrow           None   
Announcer                                               None           None   

                                                         9   \
Stannis                              doesnt make much sense   
Davos      thus ending dragonslaying career ser byron swann   
Selyse                                                 None   
Meryn                                                  None   
Announcer                                              None   

                                           10                         11  \
Stannis    choose rhaenyra aegon would chosen  dont even know im talking   
Davos                                    like              youre welcome   
Selyse                                   None                       None   
Meryn                                    None                       None   
Announcer                                None                       None   

               12       13          14    15  
Stannis       yes      ext  melisandre  None  
Davos      course  deserve        None  None  
Selyse       None     None        None  None  
Meryn        None     None      

### Episode Ten

In [192]:
df_s5.script_text[9]

[u'INT. STANNIS\u2019S CAMP - MELISANDRE\u2019S TENT',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'EXT. STANNIS\u2019S CAMP - DUSK',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'INT. STANNIS\u2019S CAMP - STANNIS\u2019S TENT',
 u'\n',
 u'\n',
 u'\n',
 u'\nMELISANDRE: The Lord of Light has made good on his promise, my king. His fires have melted the snows away. The way ahead is clear.',
 u'\n',
 u'\nSTANNIS: We ride for Winterfell.',
 u'\n',
 u'\nMELISANDRE: And you will take it. The Lord has shown me Bolton banners burning. You will receive what is yours by right.',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'INT. STANNIS\u2019S CAMP',
 u'\n',
 u'\n',
 u'\n',
 u'\nSOLDIER: Your Grace.',
 u'\n',
 u'\nSTANNIS: Prepare to form up.',
 u'\n',
 u'\nSOLDIER: Your Grace.',
 u'\n',
 u'\n',
 u'\n',
 u'\nSTANNIS: Tell me.',
 u'\n',
 u'\nSOLDIER: The men. Many deserted before dawn.',
 u'\n',
 u'\nSTANNIS: How many?',
 u'\n',
 u'\nSOLDIER: ',
 u'\n',
 u'\n',
 u'\n',
 u'\nSOLDIER 2: Your Grace?',
 u'\n',
 u'\nSTANNIS: Speak up

In [193]:
script_text5_10 = df_s5.script_text[9]
print type(script_text5_10)

script_text5_10

<type 'list'>


[u'INT. STANNIS\u2019S CAMP - MELISANDRE\u2019S TENT',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'EXT. STANNIS\u2019S CAMP - DUSK',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'INT. STANNIS\u2019S CAMP - STANNIS\u2019S TENT',
 u'\n',
 u'\n',
 u'\n',
 u'\nMELISANDRE: The Lord of Light has made good on his promise, my king. His fires have melted the snows away. The way ahead is clear.',
 u'\n',
 u'\nSTANNIS: We ride for Winterfell.',
 u'\n',
 u'\nMELISANDRE: And you will take it. The Lord has shown me Bolton banners burning. You will receive what is yours by right.',
 u'\n',
 u'\n',
 u'\n',
 u'\n',
 u'INT. STANNIS\u2019S CAMP',
 u'\n',
 u'\n',
 u'\n',
 u'\nSOLDIER: Your Grace.',
 u'\n',
 u'\nSTANNIS: Prepare to form up.',
 u'\n',
 u'\nSOLDIER: Your Grace.',
 u'\n',
 u'\n',
 u'\n',
 u'\nSTANNIS: Tell me.',
 u'\n',
 u'\nSOLDIER: The men. Many deserted before dawn.',
 u'\n',
 u'\nSTANNIS: How many?',
 u'\n',
 u'\nSOLDIER: ',
 u'\n',
 u'\n',
 u'\n',
 u'\nSOLDIER 2: Your Grace?',
 u'\n',
 u'\nSTANNIS: Speak up

In [194]:
script_split10 = [i.split('\n') for i in script_text5_10]
script_split10

[[u'INT. STANNIS\u2019S CAMP - MELISANDRE\u2019S TENT'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'EXT. STANNIS\u2019S CAMP - DUSK'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'INT. STANNIS\u2019S CAMP - STANNIS\u2019S TENT'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'',
  u'MELISANDRE: The Lord of Light has made good on his promise, my king. His fires have melted the snows away. The way ahead is clear.'],
 [u'', u''],
 [u'', u'STANNIS: We ride for Winterfell.'],
 [u'', u''],
 [u'',
  u'MELISANDRE: And you will take it. The Lord has shown me Bolton banners burning. You will receive what is yours by right.'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'INT. STANNIS\u2019S CAMP'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u'SOLDIER: Your Grace.'],
 [u'', u''],
 [u'', u'STANNIS: Prepare to form up.'],
 [u'', u''],
 [u'', u'SOLDIER: Your Grace.'],
 [u'', u''],
 [u'', u''],
 [u'', u''],
 [u'', u'STANNIS: Tell me.'],
 [u'', u''],
 [u'', u'SOLDIER: 

In [195]:
string_script_text10 = ' '

for i in script_split10:
    for e in i:
        string_script_text10 = string_script_text10 + ' ' + e

In [196]:
string_script_text10

u'  INT. STANNIS\u2019S CAMP - MELISANDRE\u2019S TENT         EXT. STANNIS\u2019S CAMP - DUSK         INT. STANNIS\u2019S CAMP - STANNIS\u2019S TENT        MELISANDRE: The Lord of Light has made good on his promise, my king. His fires have melted the snows away. The way ahead is clear.    STANNIS: We ride for Winterfell.    MELISANDRE: And you will take it. The Lord has shown me Bolton banners burning. You will receive what is yours by right.         INT. STANNIS\u2019S CAMP        SOLDIER: Your Grace.    STANNIS: Prepare to form up.    SOLDIER: Your Grace.        STANNIS: Tell me.    SOLDIER: The men. Many deserted before dawn.    STANNIS: How many?    SOLDIER:         SOLDIER 2: Your Grace?    STANNIS: Speak up. It can\u2019t be worse than mutiny.         EXT. WOODS OUTSIDE STANNIS\u2019S CAMP                SOLDIER: Your Grace. The Lady Melisandre was just seen riding out of camp.        STANNIS:          INT. CASTLE BLACK - LIBRARY    JON: He raised his hands. And they all stood up

In [197]:
words10 = word_tokenize(string_script_text10)
words10

[u'INT',
 u'.',
 u'STANNIS\u2019S',
 u'CAMP',
 u'-',
 u'MELISANDRE\u2019S',
 u'TENT',
 u'EXT',
 u'.',
 u'STANNIS\u2019S',
 u'CAMP',
 u'-',
 u'DUSK',
 u'INT',
 u'.',
 u'STANNIS\u2019S',
 u'CAMP',
 u'-',
 u'STANNIS\u2019S',
 u'TENT',
 u'MELISANDRE',
 u':',
 u'The',
 u'Lord',
 u'of',
 u'Light',
 u'has',
 u'made',
 u'good',
 u'on',
 u'his',
 u'promise',
 u',',
 u'my',
 u'king',
 u'.',
 u'His',
 u'fires',
 u'have',
 u'melted',
 u'the',
 u'snows',
 u'away',
 u'.',
 u'The',
 u'way',
 u'ahead',
 u'is',
 u'clear',
 u'.',
 u'STANNIS',
 u':',
 u'We',
 u'ride',
 u'for',
 u'Winterfell',
 u'.',
 u'MELISANDRE',
 u':',
 u'And',
 u'you',
 u'will',
 u'take',
 u'it',
 u'.',
 u'The',
 u'Lord',
 u'has',
 u'shown',
 u'me',
 u'Bolton',
 u'banners',
 u'burning',
 u'.',
 u'You',
 u'will',
 u'receive',
 u'what',
 u'is',
 u'yours',
 u'by',
 u'right',
 u'.',
 u'INT',
 u'.',
 u'STANNIS\u2019S',
 u'CAMP',
 u'SOLDIER',
 u':',
 u'Your',
 u'Grace',
 u'.',
 u'STANNIS',
 u':',
 u'Prepare',
 u'to',
 u'form',
 u'up',
 u'.

In [198]:
sentences10 = sent_tokenize(string_script_text10)
sentences10

[u'  INT.',
 u'STANNIS\u2019S CAMP - MELISANDRE\u2019S TENT         EXT.',
 u'STANNIS\u2019S CAMP - DUSK         INT.',
 u'STANNIS\u2019S CAMP - STANNIS\u2019S TENT        MELISANDRE: The Lord of Light has made good on his promise, my king.',
 u'His fires have melted the snows away.',
 u'The way ahead is clear.',
 u'STANNIS: We ride for Winterfell.',
 u'MELISANDRE: And you will take it.',
 u'The Lord has shown me Bolton banners burning.',
 u'You will receive what is yours by right.',
 u'INT.',
 u'STANNIS\u2019S CAMP        SOLDIER: Your Grace.',
 u'STANNIS: Prepare to form up.',
 u'SOLDIER: Your Grace.',
 u'STANNIS: Tell me.',
 u'SOLDIER: The men.',
 u'Many deserted before dawn.',
 u'STANNIS: How many?',
 u'SOLDIER:         SOLDIER 2: Your Grace?',
 u'STANNIS: Speak up.',
 u'It can\u2019t be worse than mutiny.',
 u'EXT.',
 u'WOODS OUTSIDE STANNIS\u2019S CAMP                SOLDIER: Your Grace.',
 u'The Lady Melisandre was just seen riding out of camp.',
 u'STANNIS:          INT.',
 u'C

In [199]:
dialogue10 = []

for sentence in sentences10:
    words=sentence.split(':')[0]
    if len(words.split())<=2:
        if words in (names5_10):
            dialogue10.append(sentence)

In [200]:
dialogue10

[u'STANNIS: We ride for Winterfell.',
 u'MELISANDRE: And you will take it.',
 u'STANNIS: Prepare to form up.',
 u'SOLDIER: Your Grace.',
 u'STANNIS: Tell me.',
 u'SOLDIER: The men.',
 u'STANNIS: How many?',
 u'SOLDIER:         SOLDIER 2: Your Grace?',
 u'STANNIS: Speak up.',
 u'STANNIS:          INT.',
 u'SAM: So what are you gonna do?',
 u'JON: I\u2019m gonna hope they don\u2019t learn how to climb the wall.',
 u'SAM:     SAM (confused): But\u2026 you killed a White Walker.',
 u'JON: With Longclaw.',
 u'JON: Here\u2019s to us then.',
 u'JON: What?',
 u'SAM: I wanted to ask you something.',
 u'JON: I need you here, Sam.',
 u'SAM: Well, there\u2019s Edd.',
 u'SAM:  .',
 u'SAM: If Gilly stays here then she\u2019ll die.',
 u'SAM: Thank you.',
 u'JON: You know that The Citadel will make you swear off women, too.',
 u'SAM: They\u2019ll bloody try.',
 u'SAM: I\u2019ll come back.',
 u'SAM: To my return.',
 u'BRIENNE: How do you know it\u2019s Stannis?',
 u'PODRICK:          EXT.',
 u'SOLDIER:

In [201]:
import pickle
with open('/Users/zoemarkovits/Metis/project_five_got/Dialogue_PKLs/s510.pkl', 'wb') as f:
    pickle.dump(dialogue10, f)

In [202]:
from collections import defaultdict

speakers10 = defaultdict(list)
for sentence in dialogue10:
    speakers10[sentence.split(':')[0]].append(sentence.split(':')[1])

speakers10

defaultdict(list,
            {u'ALLISER': [u' Man says he saw your uncle at Hardhome the last full moon.',
              u' Could be.',
              u' Over there.'],
             u'ARYA': [u' You were the first person on my list, you know.',
              u' I can\u2019t hear you.',
              u' You know who I am.',
              u' Do you know who you are?',
              u' You\u2019re no one.',
              u' No!',
              u' He was my friend.',
              u' But if you\u2019re\u2026 (looks to the Jaqen who drank the potion and is seemingly dead) Who\u2019s this?',
              u' What\u2019s happening?!'],
             u'BRIENNE': [u' How do you know it\u2019s Stannis?',
              u' I do not fight for the Boltons.',
              u' In the name of Renly of House Baratheon, First of his Name, Rightful King of the Andals and the First Men, Lord of the Seven Kingdoms, and Protector of the Realm, I, Brienne of Tarth, sentence you to die.'],
             u'BRONN'

In [203]:
speakers10['ARYA']

[u' You were the first person on my list, you know.',
 u' I can\u2019t hear you.',
 u' You know who I am.',
 u' Do you know who you are?',
 u' You\u2019re no one.',
 u' No!',
 u' He was my friend.',
 u' But if you\u2019re\u2026 (looks to the Jaqen who drank the potion and is seemingly dead) Who\u2019s this?',
 u' What\u2019s happening?!']

In [204]:
episode_ten = pd.DataFrame.from_dict(speakers10, orient="index")
print episode_ten.shape

(38, 16)


In [205]:
#from numpy import nan
#episode_ten.fillna(value=str(0), inplace=True)

In [206]:
episode_ten.info()

<class 'pandas.core.frame.DataFrame'>
Index: 38 entries, STANNIS to MAN
Data columns (total 16 columns):
0     38 non-null object
1     26 non-null object
2     20 non-null object
3     16 non-null object
4     14 non-null object
5     12 non-null object
6     9 non-null object
7     8 non-null object
8     7 non-null object
9     6 non-null object
10    5 non-null object
11    5 non-null object
12    3 non-null object
13    3 non-null object
14    3 non-null object
15    1 non-null object
dtypes: object(16)
memory usage: 5.0+ KB


In [207]:
episode_ten.head()

0                      1   \
STANNIS                    We ride for Winterfell.    Prepare to form up.   
DAVOS        The wildlings will make a difference!               Shireen?   
MELISANDRE                   And you will take it.                   None   
BROTHER                             For the Watch.         For the Watch.   
BRONN          Maybe I’ll come visit you sometime.   Don’t wait too long.   

                         2                3           4               5   \
STANNIS            Tell me.        How many?   Speak up.            INT.   
DAVOS                  None             None        None            None   
MELISANDRE             None             None        None            None   
BROTHER      For the Watch.   For the Watch.        None            None   
BRONN                  None             None        None            None   

                                             6     7     8     9     10    11  \
STANNIS      Bolton has women fighting for him.  None  None  None  None  None   
DAVOS                                      None  None  None  None  None  None   
MELISANDRE                                 None  None  None  None  None  None   
BROTHER                                    None  None  None  None  None  None   
BRONN                                      None  None  None  None  None  None   

              12    13    14    15  
STANNIS     None  None  None  None  
DAVOS       None  None  None  None  
MELISANDRE  None  None  None  None  
BROTHER     None  None  None  None  
BRONN       None  None  None  None

In [208]:
test10 = episode_ten[0].apply(remove_stops)
test10

STANNIS                                    ride winterfell
DAVOS                            wildlings make difference
MELISANDRE                                            take
BROTHER                                              watch
BRONN                        maybe ill come visit sometime
TYENE                                 maybe ill come visit
SOLDIER                                              grace
JAIME                                                thank
TYRION                  valyrian rusty common tongue thank
MISSANDEI                               valyrian bit rusty
WOMAN                            ive half many cocks queen
ELLARIA                                      forgive child
SURVIVOR                                         surrender
SPARROW                         grace dealt according sins
THEON                                                   go
DAENERYS                                         far carry
JON                    im gonna hope dont learn climb wa

In [209]:
for column in episode_ten.columns:
    for x in range(len(episode_ten[column])):
        episode_ten[column][x] = remove_stops(episode_ten[column][x])

In [210]:
episode_ten.index = episode_ten.index.str.title()

episode_ten.shape

(38, 16)

In [211]:
episode_ten.head()

0               1      2      3   \
Stannis                   ride winterfell    prepare form   tell   many   
Davos           wildlings make difference         shireen   None   None   
Melisandre                           take            None   None   None   
Brother                             watch           watch  watch  watch   
Bronn       maybe ill come visit sometime  dont wait long   None   None   

               4     5                      6     7     8     9     10    11  \
Stannis     speak   int  bolton women fighting  None  None  None  None  None   
Davos        None  None                   None  None  None  None  None  None   
Melisandre   None  None                   None  None  None  None  None  None   
Brother      None  None                   None  None  None  None  None  None   
Bronn        None  None                   None  None  None  None  None  None   

              12    13    14    15  
Stannis     None  None  None  None  
Davos       None  None  None  None  
Melisandre  None  None  None  None  
Brother     None  None  None  None  
Bronn       None  None  None  None

## Season Five

In [212]:
episode_one.index

Index([u'Stannis', u'Davos', u'Kevan', u'Melisandre', u'Olly', u'Jaime',
       u'Tyrion', u'Missandei', u'Mossador', u'Prostitute', u'Baelish',
       u'Mance', u'Sam', u'Grand Maester Pyrcelle', u'Daario',
       u'Kevan Lannister', u'Daenerys', u'Jon', u'Barristan', u'Hizdahr',
       u'Melara', u'Grey Worm', u'Cersei', u'Varys', u'Alliser', u'Maggy',
       u'White Rat', u'Margaery', u'Gilly', u'Podrick', u'Lancel', u'Sansa',
       u'Brienne', u'Squire', u'Olyvar', u'Yohn Royce', u'Priest', u'Loras',
       u'Royce'],
      dtype='object')

In [213]:
episode_two.index

Index([u'Stannis', u'Davos', u'Shireen', u'Meryn', u'Pycelle', u'Kevan',
       u'Old Man', u'Brother', u'Bronn', u'Gilly', u'Jaime', u'Tyrion',
       u'Lollys', u'Mossador', u'Baelish', u'Ellaria', u'Sam', u'Areo',
       u'Mace Tyrell', u'Guard', u'Selyse', u'Daenerys', u'Doran', u'Aemon',
       u'Jon', u'Barristan', u'Brothers', u'Hunters', u'Grey Worm', u'Cersei',
       u'Varys', u'Mace', u'Janos', u'Qyburn', u'Hizdahr', u'Podrick',
       u'Sansa', u'Brienne', u'Knight', u'Men', u'Jaqen', u'Daario',
       u'Alliser', u'Waitress', u'Arya', u'Knight 1', u'Man'],
      dtype='object')

In [214]:
print episode_one.shape
print episode_two.shape

(39, 22)
(47, 23)


In [215]:
episode_one = episode_one.reset_index()

In [216]:
episode_one_dict = {'Stannis':'Stannis', 
                    'Davos':'Davos', 
                    'Kevan':'Kevan', 
                    'Melisandre':'Melisandre', 
                    'Olly':'Olly', 
                    'Jaime':'Jaime',
                    'Tyrion':'Tyrion', 
                    'Missandei':'Missandei', 
                    'Mossador':'Mossador', 
                    'Prostitute':'Prostitute', 
                    'Baelish':'Baelish',
                    'Mance':'Mance', 
                    'Sam':'Sam', 
                    'Grand Maester Pyrcelle':'Pycelle', 
                    'Daario':'Daario',
                    'Kevan Lannister':'Kevan', 
                    'Daenerys':'Daenerys', 
                    'Jon':'Jon', 
                    'Barristan':'Barristan', 
                    'Hizdahr':'Hizdahr',
                    'Melara':'Melara', 
                    'Grey Worm':'Grey Worm', 
                    'Cersei':'Cersei', 
                    'Varys':'Varys', 
                    'Alliser':'Alliser', 
                    'Maggy':'Maggy',
                    'White Rat':'White Rat', 
                    'Margaery':'Margaery', 
                    'Gilly':'Gilly', 
                    'Podrick':'Podrick', 
                    'Lancel':'Lancel', 
                    'Sansa':'Sansa',
                    'Brienne':'Brienne', 
                    'Squire':'Squire', 
                    'Olyvar':'Olyvar', 
                    'Yohn Royce':'Yohn Royce', 
                    'Priest':'Priest', 
                    'Loras':'Loras',
                    'Royce':'Royce'}

episode_one['index']=episode_one['index'].replace(episode_one_dict)

In [217]:
episode_one = episode_one.set_index('index')

In [218]:
episode_one.head()

0   \
index                                    
Stannis          know rules winterfell   
Davos       ive talking sworn brothers   
Kevan                    call sparrows   
Melisandre             king wants word   
Olly                             heavy   

                                                  1   \
index                                                  
Stannis     traitor plunged dagger robb starks heart   
Davos                                      many dont   
Kevan                                         course   
Melisandre                                     never   
Olly                                            None   

                                                    2   \
index                                                    
Stannis                                         matter   
Davos       nights watch feel much affection wildlings   
Kevan                                             None   
Melisandre                                        feel   
Olly                                              None   

                                                  3   \
index                                                  
Stannis                      swear follow ill pardon   
Davos                                     fair offer   
Kevan                                           None   
Melisandre  man woman young old lord peasant choices   
Olly                                            None   

                                                           4            5   \
index                                                                        
Stannis     ill offer lives freedom mance kneels swears lo...  admire dont   
Davos                                                    None         None   
Kevan                                                    None         None   
Melisandre               free folk one true king name stannis         None   
Olly                                                     None         None   

               6          7           8     9     10    11    12    13    14  \
index                                                                          
Stannis     likes  nightfall  kneel live  None  None  None  None  None  None   
Davos        None       None        None  None  None  None  None  None  None   
Kevan        None       None        None  None  None  None  None  None  None   
Melisandre   None       None        None  None  None  None  None  None  None   
Olly         None       None        None  None  None  None  None  None  None   

              15    16    17    18    19    20    21  
index                                                 
Stannis     None  None  None  None  None  None  None  
Davos       None  None  None  None  None  None  None  
Kevan       None  None  None  None  None  None  None  
Melisandre  None  None  None  None  None  None  None  
Olly        None  None  None  None  None  None  None

In [219]:
season_five = episode_one.join(episode_two, rsuffix="_two", how='outer')
print season_five.shape

(64, 45)


In [220]:
season_five.head(65)

0  \
Aemon                                                      NaN   
Alliser                                     men need firm hand   
Areo                                                       NaN   
Arya                                                       NaN   
Baelish                                    boys develop slowly   
Barristan                                            yes grace   
Brienne                                       even know squire   
Bronn                                                      NaN   
Brother                                                    NaN   
Brothers                                                   NaN   
Cersei                                                           
Daario                                       mother whore told   
Daenerys                                   theyve never killed   
Davos                               ive talking sworn brothers   
Doran                                                      NaN   
Ellaria                                                    NaN   
Gilly                                        shouldnt training   
Grey Worm                                      white rat grace   
Guard                                                      NaN   
Hizdahr                                        ask concessions   
Hunters                                                    NaN   
Jaime        theyre waiting night make sure hes really dead...   
Janos                                                      NaN   
Jaqen                                                      NaN   
Jon                         wasnt heavy wouldnt stop sword get   
Kevan                                            call sparrows   
Kevan                                apologize sons appearance   
Knight                                                     NaN   
Knight 1                                                   NaN   
Lancel                                      deepest sympathies   
Lollys                                                     NaN   
Loras                                                     fine   
Mace                                                       NaN   
Mace Tyrell                                                NaN   
Maggy                                            listen friend   
Man                                                        NaN   
Mance                                       first met prisoner   
Margaery                                           late dinner   
Melara                                     father hears cersei   
Melisandre                                     king wants word   
Men                                                        NaN   
Meryn                                                      NaN   
Missandei         white rat unsullied heard found body brothel   
Mossador                                   see us people grace   
Old Man                                                    NaN   
Olly                                                     heavy   
Olyvar                                                      go   
Podrick                                        im youre squire   
Priest       grace many lords ladies travelled day night pr...   
Prostitute                                               habit   
Pycelle                              deepest condolences grace   
Qyburn                                                     NaN   
Royce                                            great warrior   
Sam                                 well im hardly new recruit   
Sansa                                             heading west   
Selyse                                                     NaN   
Shireen                                                    NaN   
Squire                       hands baelish note master arms os   
Stannis                                  know rules winterfell   
Tyrion              still dont see stay fucking crate set sail   
Varys                              

In [221]:
season_five.index

Index([      u'Aemon',     u'Alliser',        u'Areo',        u'Arya',
           u'Baelish',   u'Barristan',     u'Brienne',       u'Bronn',
           u'Brother',    u'Brothers',      u'Cersei',      u'Daario',
          u'Daenerys',       u'Davos',       u'Doran',     u'Ellaria',
             u'Gilly',   u'Grey Worm',       u'Guard',     u'Hizdahr',
           u'Hunters',       u'Jaime',       u'Janos',       u'Jaqen',
               u'Jon',       u'Kevan',       u'Kevan',      u'Knight',
          u'Knight 1',      u'Lancel',      u'Lollys',       u'Loras',
              u'Mace', u'Mace Tyrell',       u'Maggy',         u'Man',
             u'Mance',    u'Margaery',      u'Melara',  u'Melisandre',
               u'Men',       u'Meryn',   u'Missandei',    u'Mossador',
           u'Old Man',        u'Olly',      u'Olyvar',     u'Podrick',
            u'Priest',  u'Prostitute',     u'Pycelle',      u'Qyburn',
             u'Royce',         u'Sam',       u'Sansa',      u'Selyse',
      

In [222]:
episode_three.index

Index([u'Stannis', u'Davos', u'Meryn', u'Pycelle', u'Priestess', u'Olly',
       u'Tyrion', u'Baelish', u'Crowd', u'Janos', u'Roose', u'Jon', u'Woman 2',
       u'Man 1', u'Tommen', u'Man 2', u'Cersei', u'Varys', u'Waif', u'Mace',
       u'Woman', u'Margaery', u'Qyburn', u'Ramsay', u'Man 3', u'Podrick',
       u'Sam', u'Sansa', u'Jaqen', u'Olyvar', u'Brienne', u'Arya',
       u'High Septon', u'Man'],
      dtype='object')

In [223]:
episode_three.shape

(34, 24)

In [224]:
season_five = season_five.join(episode_three, rsuffix="_three", how='outer')
print season_five.shape

(76, 69)


In [225]:
season_five.index

Index([      u'Aemon',     u'Alliser',        u'Areo',        u'Arya',
           u'Baelish',   u'Barristan',     u'Brienne',       u'Bronn',
           u'Brother',    u'Brothers',      u'Cersei',       u'Crowd',
            u'Daario',    u'Daenerys',       u'Davos',       u'Doran',
           u'Ellaria',       u'Gilly',   u'Grey Worm',       u'Guard',
       u'High Septon',     u'Hizdahr',     u'Hunters',       u'Jaime',
             u'Janos',       u'Jaqen',         u'Jon',       u'Kevan',
             u'Kevan',      u'Knight',    u'Knight 1',      u'Lancel',
            u'Lollys',       u'Loras',        u'Mace', u'Mace Tyrell',
             u'Maggy',         u'Man',       u'Man 1',       u'Man 2',
             u'Man 3',       u'Mance',    u'Margaery',      u'Melara',
        u'Melisandre',         u'Men',       u'Meryn',   u'Missandei',
          u'Mossador',     u'Old Man',        u'Olly',      u'Olyvar',
           u'Podrick',      u'Priest',   u'Priestess',  u'Prostitute',
      

In [226]:
episode_four.index

Index([u'Stannis', u'Elaria', u'Selyse', u'Pycelle', u'Dario', u'Melisandre',
       u'Bronn', u'Jaime', u'Tyrion', u'Missandei', u'Woman', u'Sam',
       u'Shireen', u'Kingsguard', u'Man 3', u'Jon', u'Barristan', u'Man 1',
       u'Tommen', u'Man 2', u'Cersei', u'Man 4', u'Mace', u'Baelish',
       u'Daenerys', u'Margaery', u'Rider', u'Nymeria', u'Hizdahr', u'Lancel',
       u'Obara', u'Sansa', u'Jorah', u'Militant', u'High Sparrow', u'Loras'],
      dtype='object')

In [227]:
episode_four = episode_four.reset_index()

In [228]:
episode_four_dict = {'Stannis':'Stannis', 
                     'Elaria':'Ellaria', 
                     'Selyse':'Selyse', 
                     'Pycelle':'Pycelle', 
                     'Dario':'Daario', 
                     'Melisandre':'Melisandre',
                     'Bronn':'Bronn', 
                     'Jaime':'Jaime', 
                     'Tyrion':'Tyrion', 
                     'Missandei':'Missandei', 
                     'Woman':'Woman', 
                     'Sam':'Sam',
                     'Shireen':'Shireen', 
                     'Kingsguard':'Kingsguard', 
                     'Man 3':'Man 3', 
                     'Jon':'Jon', 
                     'Barristan':'Barristan', 
                     'Man 1':'Man 1',
                     'Tommen':'Tommen', 
                     'Man 2':'Man 2', 
                     'Cersei':'Cersei', 
                     'Man 4':'Man 4', 
                     'Mace':'Mace', 
                     'Baelish':'Baelish',
                     'Daenerys':'Daenerys', 
                     'Margaery':'Margaery', 
                     'Rider':'Rider', 
                     'Nymeria':'Nymeria', 
                     'Hizdahr':'Hizdahr', 
                     'Lancel':'Lancel',
                     'Obara':'Obara', 
                     'Sansa':'Sansa', 
                     'Jorah':'Jorah', 
                     'Militant':'Militant', 
                     'High Sparrow':'High Sparrow', 
                     'Loras':'Loras'}

episode_four['index'] = episode_four['index'].replace(episode_four_dict)

In [229]:
episode_four = episode_four.set_index('index')

In [230]:
episode_four.shape

(36, 29)

In [231]:
season_five = season_five.join(episode_four, rsuffix="_four", how='outer')
print season_five.shape

(84, 98)


In [232]:
season_five.index

Index([       u'Aemon',      u'Alliser',         u'Areo',         u'Arya',
            u'Baelish',    u'Barristan',      u'Brienne',        u'Bronn',
            u'Brother',     u'Brothers',       u'Cersei',        u'Crowd',
             u'Daario',     u'Daenerys',        u'Davos',        u'Doran',
            u'Ellaria',        u'Gilly',    u'Grey Worm',        u'Guard',
        u'High Septon', u'High Sparrow',      u'Hizdahr',      u'Hunters',
              u'Jaime',        u'Janos',        u'Jaqen',          u'Jon',
              u'Jorah',        u'Kevan',        u'Kevan',   u'Kingsguard',
             u'Knight',     u'Knight 1',       u'Lancel',       u'Lollys',
              u'Loras',         u'Mace',  u'Mace Tyrell',        u'Maggy',
                u'Man',        u'Man 1',        u'Man 2',        u'Man 3',
              u'Man 4',        u'Mance',     u'Margaery',       u'Melara',
         u'Melisandre',          u'Men',        u'Meryn',     u'Militant',
          u'Missandei',  

In [233]:
episode_five.index

Index([u'Stannis', u'Davos', u'Gilly', u'Tyrion', u'Missandei', u'Sam',
       u'Olly', u'Shireen', u'Daenerys', u'Roose', u'Jon', u'Myranda',
       u'Walda', u'Grey Worm', u'Theon', u'Ramsay', u'Hizdahr', u'Edd',
       u'Sansa', u'Brienne', u'Jorah', u'Allister', u'Aemon', u'Daario',
       u'Tormund', u'Man'],
      dtype='object')

In [234]:
episode_five = episode_five.reset_index()

In [235]:
episode_five_dict = {'Stannis':'Stannis', 
                     'Davos':'Davos', 
                     'Gilly':'Gilly', 
                     'Tyrion':'Tyrion', 
                     'Missandei':'Missandei', 
                     'Sam':'Sam',
                     'Olly':'Olly', 
                     'Shireen':'Shireen', 
                     'Daenerys':'Daenerys', 
                     'Roose':'Roose', 
                     'Jon':'Jon', 
                     'Myranda':'Myranda',
                     'Walda':'Walda', 
                     'Grey Worm':'Grey Worm', 
                     'Theon':'Theon', 
                     'Ramsay':'Ramsay', 
                     'Hizdahr':'Hizdahr', 
                     'Edd':'Edd',
                     'Sansa':'Sansa', 
                     'Brienne':'Brienne', 
                     'Jorah':'Jorah', 
                     'Allister':'Alliser', 
                     'Aemon':'Aemon', 
                     'Daario':'Daario',
                     'Tormund':'Tormund', 
                     'Man':'Man'}

episode_five['index'] = episode_five['index'].replace(episode_five_dict)

In [236]:
episode_five = episode_five.set_index('index')

In [237]:
episode_five.shape

(26, 30)

In [238]:
season_five = season_five.join(episode_five, rsuffix="_five", how='outer')
print season_five.shape    

(89, 128)


In [239]:
season_five.index

Index([       u'Aemon',      u'Alliser',         u'Areo',         u'Arya',
            u'Baelish',    u'Barristan',      u'Brienne',        u'Bronn',
            u'Brother',     u'Brothers',       u'Cersei',        u'Crowd',
             u'Daario',     u'Daenerys',        u'Davos',        u'Doran',
                u'Edd',      u'Ellaria',        u'Gilly',    u'Grey Worm',
              u'Guard',  u'High Septon', u'High Sparrow',      u'Hizdahr',
            u'Hunters',        u'Jaime',        u'Janos',        u'Jaqen',
                u'Jon',        u'Jorah',        u'Kevan',        u'Kevan',
         u'Kingsguard',       u'Knight',     u'Knight 1',       u'Lancel',
             u'Lollys',        u'Loras',         u'Mace',  u'Mace Tyrell',
              u'Maggy',          u'Man',        u'Man 1',        u'Man 2',
              u'Man 3',        u'Man 4',        u'Mance',     u'Margaery',
             u'Melara',   u'Melisandre',          u'Men',        u'Meryn',
           u'Militant',  

In [240]:
episode_six.index

Index([u'Bronn', u'Jaime', u'Tyrion', u'Malko', u'Girl', u'Baelish',
       u'Sparrow', u'Areo', u'Theon', u'Roose', u'Myranda', u'Slaver', u'Waif',
       u'Sand Snakes', u'Cersei', u'Trystane', u'Margaery', u'Ramsay',
       u'Lancel', u'Obara', u'Sansa', u'Jaqen', u'Jorah', u'Olyvar', u'Olenna',
       u'Arya', u'Myrcella', u'Loras', u'Man'],
      dtype='object')

In [241]:
episode_six.shape

(29, 24)

In [242]:
season_five = season_five.join(episode_six, rsuffix="_six", how='outer')
print season_five.shape 

(97, 152)


In [243]:
season_five.index

Index([       u'Aemon',      u'Alliser',         u'Areo',         u'Arya',
            u'Baelish',    u'Barristan',      u'Brienne',        u'Bronn',
            u'Brother',     u'Brothers',       u'Cersei',        u'Crowd',
             u'Daario',     u'Daenerys',        u'Davos',        u'Doran',
                u'Edd',      u'Ellaria',        u'Gilly',         u'Girl',
          u'Grey Worm',        u'Guard',  u'High Septon', u'High Sparrow',
            u'Hizdahr',      u'Hunters',        u'Jaime',        u'Janos',
              u'Jaqen',          u'Jon',        u'Jorah',        u'Kevan',
              u'Kevan',   u'Kingsguard',       u'Knight',     u'Knight 1',
             u'Lancel',       u'Lollys',        u'Loras',         u'Mace',
        u'Mace Tyrell',        u'Maggy',        u'Malko',          u'Man',
              u'Man 1',        u'Man 2',        u'Man 3',        u'Man 4',
              u'Mance',     u'Margaery',       u'Melara',   u'Melisandre',
                u'Men',  

In [244]:
episode_seven.index

Index([u'Stannis', u'Davos', u'Jorah', u'Slave Buyer', u'Melisandre', u'Bronn',
       u'Gilly', u'Jaime', u'Tyrion', u'Malko', u'Baelish', u'Sam', u'Sparrow',
       u'Olenna', u'Hizdahr', u'Daenerys', u'Aemon', u'Jon', u'Brothers',
       u'Theon', u'Tommen', u'Derryk', u'Cersei', u'Buyer', u'Alliser',
       u'Margaery', u'Ramsay', u'Tyene', u'Obara', u'Sansa', u'Brand', u'Men',
       u'Owner', u'Daario', u'High Sparrow', u'Myrcella'],
      dtype='object')

In [245]:
episode_seven.shape

(36, 20)

In [246]:
season_five = season_five.join(episode_seven, rsuffix="_seven", how='outer')
print season_five.shape 

(103, 172)


In [247]:
season_five.index

Index([     u'Aemon',    u'Alliser',       u'Areo',       u'Arya',
          u'Baelish',  u'Barristan',      u'Brand',    u'Brienne',
            u'Bronn',    u'Brother',
       ...
            u'Tyene',     u'Tyrion',      u'Varys',       u'Waif',
         u'Waitress',      u'Walda',  u'White Rat',      u'Woman',
          u'Woman 2', u'Yohn Royce'],
      dtype='object', length=103)

In [248]:
episode_eight.index

Index([u'Karsi', u'Brother', u'Olly', u'Tyrion', u'Daughter', u'Sam',
       u'Master', u'Daenerys', u'Roose', u'Jon', u'Giant', u'Loboda', u'Theon',
       u'Cersei', u'Wildling Elder', u'Qyburn', u'Ramsay', u'Gilly', u'Edd',
       u'Sansa', u'Jaqen', u'Jorah', u'Septa', u'Thin Man', u'Tormund',
       u'Arya', u'Man'],
      dtype='object')

In [249]:
episode_eight.shape

(27, 31)

In [250]:
season_five = season_five.join(episode_eight, rsuffix="_eight", how='outer')
print season_five.shape 

(111, 203)


In [251]:
episode_nine.shape

(36, 16)

In [252]:
episode_nine.index

Index([u'Stannis', u'Davos', u'Selyse', u'Meryn', u'Announcer', u'Melisandre',
       u'Bronn', u'Tyene', u'Jaime', u'Tyrion', u'Quick', u'Strong',
       u'Prostitute', u'Ellaria', u'Sam', u'Areo', u'Shireen', u'Daenerys',
       u'Doran', u'Jon', u'Head', u'Mace', u'Alliser', u'Trystane', u'Nymeria',
       u'Hizdahr', u'John', u'Jaqen', u'Jorah', u'Thin Man', u'Daario',
       u'Banker', u'Arya', u'Head Prostitute', u'Myrcella', u'Man'],
      dtype='object')

In [253]:
season_five = season_five.join(episode_nine, rsuffix="_nine", how='outer')
print season_five.shape 

(118, 219)


In [254]:
episode_ten.shape

(38, 16)

In [255]:
episode_ten.index

Index([u'Stannis', u'Davos', u'Melisandre', u'Brother', u'Bronn', u'Tyene',
       u'Soldier', u'Jaime', u'Tyrion', u'Missandei', u'Woman', u'Ellaria',
       u'Survivor', u'Sparrow', u'Theon', u'Daenerys', u'Jon', u'Myranda',
       u'Grey Worm', u'Waif', u'Varys', u'Cersei', u'Alliser', u'Qyburn',
       u'Ramsay', u'Olly', u'Podrick', u'Sam', u'Sansa', u'Brienne', u'Jorah',
       u'Septa', u'Jaqen', u'Daario', u'High Sparrow', u'Arya', u'Myrcella',
       u'Man'],
      dtype='object')

In [256]:
season_five = season_five.join(episode_ten, rsuffix="_ten", how='outer')
print season_five.shape 

(120, 235)


In [257]:
season_five.index

Index([         u'Aemon',        u'Alliser',      u'Announcer',
                 u'Areo',           u'Arya',        u'Baelish',
               u'Banker',      u'Barristan',          u'Brand',
              u'Brienne',
       ...
               u'Tyrion',          u'Varys',           u'Waif',
             u'Waitress',          u'Walda',      u'White Rat',
       u'Wildling Elder',          u'Woman',        u'Woman 2',
           u'Yohn Royce'],
      dtype='object', length=120)

In [258]:
from numpy import nan
season_five.fillna(value=str(0), inplace=True)

In [259]:
season_five.head(125)

0  \
Aemon                                                            0   
Alliser                                         men need firm hand   
Announcer                                                        0   
Areo                                                             0   
Arya                                                             0   
Baelish                                        boys develop slowly   
Banker                                                           0   
Barristan                                                yes grace   
Brand                                                            0   
Brienne                                           even know squire   
Bronn                                                            0   
Brother                                                          0   
Brothers                                                         0   
Buyer                                                            0   
Cersei                                                               
Crowd                                                            0   
Daario                                           mother whore told   
Daenerys                                       theyve never killed   
Daughter                                                         0   
Davos                                   ive talking sworn brothers   
Derryk                                                           0   
Doran                                                            0   
Edd                                                              0   
Ellaria                                                          0   
Giant                                                            0   
Gilly                                            shouldnt training   
Girl                                                             0   
Grey Worm                                          white rat grace   
Guard                                                            0   
Head                                                             0   
Head Prostitute                                                  0   
High Septon                                                      0   
High Sparrow                                                     0   
Hizdahr                                            ask concessions   
Hunters                                                          0   
Jaime            theyre waiting night make sure hes really dead...   
Janos                                                            0   
Jaqen                                                            0   
John                                                             0   
Jon                             wasnt heavy wouldnt stop sword get   
Jorah                                                            0   
Karsi                                                            0   
Kevan                                                call sparrows   
Kevan                                    apologize sons appearance   
Kingsguard                                                       0   
Knight                                                           0   
Knight 1                                                         0   
Lancel                                          deepest sympathies   
Loboda                                                           0   
Lollys                                                           0   
Loras                                                         fine   
Mace                                                             0   
Mace Tyrell                                                      0   
Maggy                                                listen friend   
Malko                                                            0   
Man                                                              0   
Man 1                                                            0   
Man 2

In [260]:
season_five.info()

<class 'pandas.core.frame.DataFrame'>
Index: 120 entries, Aemon to Yohn Royce
Columns: 235 entries, 0 to 15_ten
dtypes: object(235)
memory usage: 221.2+ KB


In [261]:
season_five.to_pickle('/Users/zoemarkovits/Metis/project_five_got/PKLs/season_five.pkl')

## Character Breakdown

### Arya Stark

In [262]:
Arya = season_five.loc['Arya']
print Arya

0                                                           0
1                                                           0
2                                                           0
3                                                           0
4                                                           0
5                                                           0
6                                                           0
7                                                           0
8                                                           0
9                                                           0
10                                                          0
11                                                          0
12                                                          0
13                                                          0
14                                                          0
15                                                          0
16      

In [263]:
Arya_Text = Arya.values.tolist()
Arya_Text

['0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'hes statue',
 u'thank bringing',
 u'valar dohaeris',
 u'hello',
 u'jaqen hghar gave',
 u'please',
 u'wait',
 u'said jaqen hghar',
 u'well',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'ive sweeping floor days',
 u'didnt come sweep floors',
 u'said could apprentice',
 u'want serve',
 u'one manyfaced god',
 u'taking',
 '',
 u'moment perks',
 u'ow',
 u'told im gets hit',
 u'youre find',
 u'stands',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0'

In [264]:
Arya_Words = []

for word in Arya_Text:
    if len(word)>=1:
        if word != '0':
            Arya_Words.append(word)
        
Arya_Words 

[u'hes statue',
 u'thank bringing',
 u'valar dohaeris',
 u'hello',
 u'jaqen hghar gave',
 u'please',
 u'wait',
 u'said jaqen hghar',
 u'well',
 u'ive sweeping floor days',
 u'didnt come sweep floors',
 u'said could apprentice',
 u'want serve',
 u'one manyfaced god',
 u'taking',
 u'moment perks',
 u'ow',
 u'told im gets hit',
 u'youre find',
 u'stands',
 u'get play game',
 u'game',
 u'didnt even know playing',
 u'one',
 u'well',
 u'arya',
 u'westeros',
 u'executed fled capital',
 u'stabbed gut',
 u'man called hound',
 u'yes',
 u'valar dohaeris',
 u'int',
 u'serve',
 u'see',
 u'arya',
 u'best city',
 u'would captain make wager first place',
 u'captain dies thin man pays family lot money',
 u'many faced god',
 u'oysters clams cockels',
 u'tomorrow',
 u'first person list know',
 u'cant hear',
 u'know',
 u'know',
 u'youre one',
 u'friend',
 u'youre looks jaqen drank potion seemingly dead whos',
 u'whats happening']

In [265]:
Arya_Words_String = ' '.join(Arya_Words)
Arya_Words_String

u'hes statue thank bringing valar dohaeris hello jaqen hghar gave please wait said jaqen hghar well ive sweeping floor days didnt come sweep floors said could apprentice want serve one manyfaced god taking moment perks ow told im gets hit youre find stands get play game game didnt even know playing one well arya westeros executed fled capital stabbed gut man called hound yes valar dohaeris int serve see arya best city would captain make wager first place captain dies thin man pays family lot money many faced god oysters clams cockels tomorrow first person list know cant hear know know youre one friend youre looks jaqen drank potion seemingly dead whos whats happening'

In [266]:
Arya_String_Length = len(Arya_Words_String)
Arya_String_Length

673

In [267]:
Arya_Sentiment = TextBlob(Arya_Words_String).sentiment
Arya_Sentiment

Sentiment(polarity=0.07499999999999998, subjectivity=0.4395833333333333)

### Petyr Baelish/Littlefinger

In [268]:
Littlefinger = season_five.loc['Baelish']
print Littlefinger

0                                        boys develop slowly
1                                                      gifts
2                                                      sansa
3                   doubt upon return robins skills improved
4                                                           
5                                                           
6           lord royce may honorable thinks hes alone castle
7                                                           
8              land far even cersei lannister cant get hands
9                                                          0
10                                                         0
11                                                         0
12                                                         0
13                                                         0
14                                                         0
15                                                         0
16                      

In [269]:
Littlefinger_Text = Littlefinger.values.tolist()
Littlefinger_Text

[u'boys develop slowly',
 u'gifts',
 u'sansa',
 u'doubt upon return robins skills improved',
 '',
 '',
 u'lord royce may honorable thinks hes alone castle',
 '',
 u'land far even cersei lannister cant get hands',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'becoming observant young lady',
 u'old saying',
 u'marriage proposal accepted',
 u'like taste',
 u'gives men courage',
 u'weve met',
 u'please lady brienne',
 u'strange',
 u'ah yes',
 u'accused',
 u'happen',
 u'shadow',
 u'uncle',
 u'dont want new friend wandering countryside alone',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'yes',
 u'home',
 u'shakes head',
 '',
 '',
 u'winterfell home',
 u'always',
 u'youre marrying roose bolton',
 u'sansa sansa',
 u'grabbing',
 u'hope',
 u'ramsay',
 u'seems pleased',
 u'begin walking',
 u'delivered everything ive promised',
 u'queen margaery adores sansa',
 u'message say',
 u'every ambitious move gamble',
 u'eyrie mine',
 '0',
 '0',
 '0',
 '0',
 '

In [270]:
Littlefinger_Words = []

for word in Littlefinger_Text:
    if len(word)>=1:
        if word != '0':
            Littlefinger_Words.append(word)
        
Littlefinger_Words 

[u'boys develop slowly',
 u'gifts',
 u'sansa',
 u'doubt upon return robins skills improved',
 u'lord royce may honorable thinks hes alone castle',
 u'land far even cersei lannister cant get hands',
 u'becoming observant young lady',
 u'old saying',
 u'marriage proposal accepted',
 u'like taste',
 u'gives men courage',
 u'weve met',
 u'please lady brienne',
 u'strange',
 u'ah yes',
 u'accused',
 u'happen',
 u'shadow',
 u'uncle',
 u'dont want new friend wandering countryside alone',
 u'yes',
 u'home',
 u'shakes head',
 u'winterfell home',
 u'always',
 u'youre marrying roose bolton',
 u'sansa sansa',
 u'grabbing',
 u'hope',
 u'ramsay',
 u'seems pleased',
 u'begin walking',
 u'delivered everything ive promised',
 u'queen margaery adores sansa',
 u'message say',
 u'every ambitious move gamble',
 u'eyrie mine',
 u'saw',
 u'come',
 u'kings landing',
 u'cersei sent',
 u'know hard live believe',
 u'begin walking',
 u'larger army',
 u'stannis takes winterfell rescues despised family north',
 u't

In [271]:
Littlefinger_Words_String = ' '.join(Littlefinger_Words)
Littlefinger_Words_String

u'boys develop slowly gifts sansa doubt upon return robins skills improved lord royce may honorable thinks hes alone castle land far even cersei lannister cant get hands becoming observant young lady old saying marriage proposal accepted like taste gives men courage weve met please lady brienne strange ah yes accused happen shadow uncle dont want new friend wandering countryside alone yes home shakes head winterfell home always youre marrying roose bolton sansa sansa grabbing hope ramsay seems pleased begin walking delivered everything ive promised queen margaery adores sansa message say every ambitious move gamble eyrie mine saw come kings landing cersei sent know hard live believe begin walking larger army stannis takes winterfell rescues despised family north take bolton boy ramsay make course hes dangerous man yes thats quite family abandon well done im urgent business queen mother baelish course house tyrell wont tolerate insults cersei lysa good woman know hard lose parents young

In [272]:
Littlefinger_String_Length = len(Littlefinger_Words_String)
Littlefinger_String_Length

1456

In [273]:
Littlefinger_Sentiment = TextBlob(Littlefinger_Words_String).sentiment
Littlefinger_Sentiment

Sentiment(polarity=-0.02623753058535667, subjectivity=0.5615847920195747)

### Brienne of Tarth

In [274]:
Brienne = season_five.loc['Brienne']
print Brienne

0                                            even know squire
1                                                   im knight
2                                         dont care im mother
3                                                  found arya
4                                                  shut mouth
5                                                           0
6                                                           0
7                                                           0
8                                                           0
9                                                           0
10                                                          0
11                                                          0
12                                                          0
13                                                          0
14                                                          0
15                                                          0
16      

In [275]:
Brienne_Text = Brienne.values.tolist()
Brienne_Text

[u'even know squire',
 u'im knight',
 u'dont care im mother',
 u'found arya',
 u'shut mouth',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '',
 u'sure',
 u'littlefinger',
 u'find',
 u'lord baelish lady sansa name brienne tarth',
 u'lady sansa mothers death sworn sword',
 '',
 u'renlys murder',
 u'tried',
 u'men didnt see happened',
 u'murdered shadow',
 u'say affairs',
 u'lady sansa word alone sansa',
 u'please lady',
 u'neither us wanted',
 u'podrick',
 u'podrick',
 u'stand',
 u'wary strangers',
 u'swore mother id protect girls',
 u'get horse',
 '0',
 '0',
 u'dont',
 u'doesnt matter',
 u'well hes complain',
 u'borrowed',
 u'walks away get firewood',
 u'im sorry im always snapping',
 u'want knight pod',
 u'starting tomorrow well train sword twice day ride morning camp evening',
 u'cant knight teach fight',
 '',
 '',
 u'shadow face stannis baratheon',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 

In [276]:
Brienne_Words = []

for word in Brienne_Text:
    if len(word)>=1:
        if word != '0':
            Brienne_Words.append(word)
        
Brienne_Words 

[u'even know squire',
 u'im knight',
 u'dont care im mother',
 u'found arya',
 u'shut mouth',
 u'sure',
 u'littlefinger',
 u'find',
 u'lord baelish lady sansa name brienne tarth',
 u'lady sansa mothers death sworn sword',
 u'renlys murder',
 u'tried',
 u'men didnt see happened',
 u'murdered shadow',
 u'say affairs',
 u'lady sansa word alone sansa',
 u'please lady',
 u'neither us wanted',
 u'podrick',
 u'podrick',
 u'stand',
 u'wary strangers',
 u'swore mother id protect girls',
 u'get horse',
 u'dont',
 u'doesnt matter',
 u'well hes complain',
 u'borrowed',
 u'walks away get firewood',
 u'im sorry im always snapping',
 u'want knight pod',
 u'starting tomorrow well train sword twice day ride morning camp evening',
 u'cant knight teach fight',
 u'shadow face stannis baratheon',
 u'turns around',
 u'thank',
 u'know lord eddard',
 u'im talking boltons',
 u'someone swore keep safe',
 u'mother',
 u'doesnt release oath',
 u'know stannis',
 u'fight boltons',
 u'name renly house baratheon first

In [277]:
Brienne_Words_String = ' '.join(Brienne_Words)
Brienne_Words_String

u'even know squire im knight dont care im mother found arya shut mouth sure littlefinger find lord baelish lady sansa name brienne tarth lady sansa mothers death sworn sword renlys murder tried men didnt see happened murdered shadow say affairs lady sansa word alone sansa please lady neither us wanted podrick podrick stand wary strangers swore mother id protect girls get horse dont doesnt matter well hes complain borrowed walks away get firewood im sorry im always snapping want knight pod starting tomorrow well train sword twice day ride morning camp evening cant knight teach fight shadow face stannis baratheon turns around thank know lord eddard im talking boltons someone swore keep safe mother doesnt release oath know stannis fight boltons name renly house baratheon first name rightful king andals first men lord seven kingdoms protector realm brienne tarth sentence die'

In [278]:
Brienne_String_Length = len(Brienne_Words_String)
Brienne_String_Length

881

In [279]:
Brienne_Sentiment = TextBlob(Brienne_Words_String).sentiment
Brienne_Sentiment

Sentiment(polarity=0.07142857142857142, subjectivity=0.5507936507936508)

### Cersei Lannister

In [280]:
Cersei = season_five.loc['Cersei']
print Cersei

0                                                            
1                                     dont need afraid father
2                                                         yes
3                                                      course
4                                             said terrifying
5                                 know youre witch see future
6                 tell future ill two boring eyes gouged head
7                                                       queen
8                                                keep waiting
9                                                            
10                                                    nothing
11                                                father dead
12             tyrion may monster least killed father purpose
13                                              cousin lancel
14                                        uncle quite alright
15                                          im sure hell grow
16      

In [281]:
Cersei_Text = Cersei.values.tolist()
Cersei_Text

['',
 u'dont need afraid father',
 u'yes',
 u'course',
 u'said terrifying',
 u'know youre witch see future',
 u'tell future ill two boring eyes gouged head',
 u'queen',
 u'keep waiting',
 '',
 u'nothing',
 u'father dead',
 u'tyrion may monster least killed father purpose',
 u'cousin lancel',
 u'uncle quite alright',
 u'im sure hell grow',
 u'wounds blackwater seem healed',
 '',
 u'could possibly done warrant forgiveness',
 u'doubt youve ever led anyone anywhere',
 u'dont know youre talking',
 u'day tywin lannisters soul needs help cut',
 u'two like world',
 u'course threat',
 u'blame us death oberyn sister every tragedy thats befallen cursed country',
 '',
 u'daughters danger youre worried im speaking loudly',
 u'dont call daughter',
 u'caution brought',
 u'never made anything better',
 u'cant ask prince doran give back',
 u'go army act war',
 u'oberyn mentioned water gardens',
 u'scoffs youre going dorne',
 u'wont necessary ser meryn',
 u'take head',
 u'good',
 u'uncle',
 u'called',
 

In [282]:
Cersei_Words = []

for word in Cersei_Text:
    if len(word)>=1:
        if word != '0':
            Cersei_Words.append(word)
        
Cersei_Words 

[u'dont need afraid father',
 u'yes',
 u'course',
 u'said terrifying',
 u'know youre witch see future',
 u'tell future ill two boring eyes gouged head',
 u'queen',
 u'keep waiting',
 u'nothing',
 u'father dead',
 u'tyrion may monster least killed father purpose',
 u'cousin lancel',
 u'uncle quite alright',
 u'im sure hell grow',
 u'wounds blackwater seem healed',
 u'could possibly done warrant forgiveness',
 u'doubt youve ever led anyone anywhere',
 u'dont know youre talking',
 u'day tywin lannisters soul needs help cut',
 u'two like world',
 u'course threat',
 u'blame us death oberyn sister every tragedy thats befallen cursed country',
 u'daughters danger youre worried im speaking loudly',
 u'dont call daughter',
 u'caution brought',
 u'never made anything better',
 u'cant ask prince doran give back',
 u'go army act war',
 u'oberyn mentioned water gardens',
 u'scoffs youre going dorne',
 u'wont necessary ser meryn',
 u'take head',
 u'good',
 u'uncle',
 u'called',
 u'king named qyburn 

In [283]:
Cersei_Words_String = ' '.join(Cersei_Words)
Cersei_Words_String

u'dont need afraid father yes course said terrifying know youre witch see future tell future ill two boring eyes gouged head queen keep waiting nothing father dead tyrion may monster least killed father purpose cousin lancel uncle quite alright im sure hell grow wounds blackwater seem healed could possibly done warrant forgiveness doubt youve ever led anyone anywhere dont know youre talking day tywin lannisters soul needs help cut two like world course threat blame us death oberyn sister every tragedy thats befallen cursed country daughters danger youre worried im speaking loudly dont call daughter caution brought never made anything better cant ask prince doran give back go army act war oberyn mentioned water gardens scoffs youre going dorne wont necessary ser meryn take head good uncle called king named qyburn new master whisperers qualification loyalty grand maester king busy moment learning concern master war would abandon king time need theres nothing casterly rock chuckles real h

In [284]:
Cersei_String_Length = len(Cersei_Words_String)
Cersei_String_Length

3292

In [285]:
Cersei_Sentiment = TextBlob(Cersei_Words_String).sentiment
Cersei_Sentiment

Sentiment(polarity=0.033030303030303035, subjectivity=0.6062218678008151)

### Daenerys Targaryan

In [286]:
Daenerys = season_five.loc['Daenerys']
print Daenerys

0                                         theyve never killed
1                                               didnt conquer
2                       learn see things differently mossador
3                                           want buried honor
4                                           angry snakes lash
5                                                        good
6                                                 concessions
7                                               im politician
8                              dont expect wise masters happy
9                                               fighting pits
10                                              fighting pits
11                       respect tradition human cockfighting
12                                                           
13                                                           
14          sold slavery forced fight death amusement mast...
15                         thats unsullied patrolling streets
16      

In [287]:
Dany_Text = Daenerys.values.tolist()
Dany_Text

[u'theyve never killed',
 u'didnt conquer',
 u'learn see things differently mossador',
 u'want buried honor',
 u'angry snakes lash',
 u'good',
 u'concessions',
 u'im politician',
 u'dont expect wise masters happy',
 u'fighting pits',
 u'fighting pits',
 u'respect tradition human cockfighting',
 '',
 '',
 u'sold slavery forced fight death amusement masters youre defending fighting pits',
 u'thats unsullied patrolling streets',
 u'dont want another childs bones dropped feet',
 u'easy',
 '0',
 '0',
 '0',
 '0',
 u'would send message',
 '',
 u'perhaps thing gave pride knowing someone lower',
 u'thank counsel',
 '',
 u'mad king',
 u'im father',
 u'son harpy executed without fair trial',
 u'prisoner awaiting trial',
 u'slaves',
 u'harpys life take',
 u'law law',
 u'leave',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '',
 u'sang',
 '',

In [288]:
Dany_Words = []

for word in Dany_Text:
    if len(word)>=1:
        if word != '0':
            Dany_Words.append(word)
        
Dany_Words 

[u'theyve never killed',
 u'didnt conquer',
 u'learn see things differently mossador',
 u'want buried honor',
 u'angry snakes lash',
 u'good',
 u'concessions',
 u'im politician',
 u'dont expect wise masters happy',
 u'fighting pits',
 u'fighting pits',
 u'respect tradition human cockfighting',
 u'sold slavery forced fight death amusement masters youre defending fighting pits',
 u'thats unsullied patrolling streets',
 u'dont want another childs bones dropped feet',
 u'easy',
 u'would send message',
 u'perhaps thing gave pride knowing someone lower',
 u'thank counsel',
 u'mad king',
 u'im father',
 u'son harpy executed without fair trial',
 u'prisoner awaiting trial',
 u'slaves',
 u'harpys life take',
 u'law law',
 u'leave',
 u'sang',
 u'good',
 u'told rhaegar good killing people',
 u'money',
 u'many others',
 u'joining us ser barristan',
 u'think protect hizdahr zo loraq',
 u'used tell men set butchering sport',
 u'recognize tradition',
 u'called',
 u'round leaders meereens great famili

In [289]:
Dany_Words_String = ' '.join(Dany_Words)
Dany_Words_String

u'theyve never killed didnt conquer learn see things differently mossador want buried honor angry snakes lash good concessions im politician dont expect wise masters happy fighting pits fighting pits respect tradition human cockfighting sold slavery forced fight death amusement masters youre defending fighting pits thats unsullied patrolling streets dont want another childs bones dropped feet easy would send message perhaps thing gave pride knowing someone lower thank counsel mad king im father son harpy executed without fair trial prisoner awaiting trial slaves harpys life take law law leave sang good told rhaegar good killing people money many others joining us ser barristan think protect hizdahr zo loraq used tell men set butchering sport recognize tradition called round leaders meereens great families bring valyrian another step valyrian children valyrian give valyrian innocent give everyone deserve ill one left rule sitting valar morghulis takes courage admit fear cut dont ridicul

In [290]:
Dany_String_Length = len(Dany_Words_String)
Dany_String_Length

1839

In [291]:
Dany_Sentiment = TextBlob(Dany_Words_String).sentiment
Dany_Sentiment

Sentiment(polarity=0.1770833333333333, subjectivity=0.5620370370370371)

### Davos Seaworth

In [292]:
Davos = season_five.loc['Davos']
print Davos

0                                  ive talking sworn brothers
1                                                   many dont
2                  nights watch feel much affection wildlings
3                                                  fair offer
4                                                           0
5                                                           0
6                                                           0
7                                                           0
8                                                           0
9                                                           0
10                                                          0
11                                                          0
12                                                          0
13                                                          0
14                                                          0
15                                                          0
16      

In [293]:
Davos_Text = Davos.values.tolist()
Davos_Text

[u'ive talking sworn brothers',
 u'many dont',
 u'nights watch feel much affection wildlings',
 u'fair offer',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'tonight nights watch elect new lord commander',
 u'unpleasant man',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'sees something',
 u'king complicated man',
 u'hes one true king',
 '',
 u'long boltons rule north stands north suffer',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '',
 u'uh grace',
 u'ill choose dozen men stay guard queen princess',
 u'tough road ahead grace',
 u'beg pardon',
 u'aye princess wont anywhere near selyse',
 u'yes queen',

In [294]:
Davos_Words = []

for word in Davos_Text:
    if len(word)>=1:
        if word != '0':
            Davos_Words.append(word)
        
Davos_Words 

[u'ive talking sworn brothers',
 u'many dont',
 u'nights watch feel much affection wildlings',
 u'fair offer',
 u'tonight nights watch elect new lord commander',
 u'unpleasant man',
 u'sees something',
 u'king complicated man',
 u'hes one true king',
 u'long boltons rule north stands north suffer',
 u'uh grace',
 u'ill choose dozen men stay guard queen princess',
 u'tough road ahead grace',
 u'beg pardon',
 u'aye princess wont anywhere near selyse',
 u'yes queen',
 u'well',
 u'stannis',
 u'still hard march wintefell wont marching anywhere weather',
 u'isnt time head back castle black snow clears',
 u'better wait right time risk everything',
 u'stannis',
 u'northerners know land ever',
 u'unless theres thaw cant press forward winterfell dont enough food get us back castle black',
 u'forgive grace never claimed expert military matters',
 u'grace youve named hand',
 u'kings hand never abandon king especially time war',
 u'boy scroll could deliver message',
 u'grace perhaps queen princess 

In [295]:
Davos_Words_String = ' '.join(Davos_Words)
Davos_Words_String

u'ive talking sworn brothers many dont nights watch feel much affection wildlings fair offer tonight nights watch elect new lord commander unpleasant man sees something king complicated man hes one true king long boltons rule north stands north suffer uh grace ill choose dozen men stay guard queen princess tough road ahead grace beg pardon aye princess wont anywhere near selyse yes queen well stannis still hard march wintefell wont marching anywhere weather isnt time head back castle black snow clears better wait right time risk everything stannis northerners know land ever unless theres thaw cant press forward winterfell dont enough food get us back castle black forgive grace never claimed expert military matters grace youve named hand kings hand never abandon king especially time war boy scroll could deliver message grace perhaps queen princess shireen could accompany stannis thus ending dragonslaying career ser byron swann like youre welcome course deserve wildlings make difference 

In [296]:
Davos_String_Length = len(Davos_Words_String)
Davos_String_Length

1005

In [297]:
Davos_Sentiment = TextBlob(Davos_Words_String).sentiment
Davos_Sentiment

Sentiment(polarity=0.06774734926908842, subjectivity=0.5709533220402786)

### Gilly

In [298]:
Gilly = season_five.loc['Gilly']
print Gilly

0                        shouldnt training
1                                one hates
2                    dont let send us away
3                cant leave theyll execute
4                                        0
5                                        0
6                                        0
7                                        0
8                                        0
9                                        0
10                                       0
11                                       0
12                                       0
13                                       0
14                                       0
15                                       0
16                                       0
17                                       0
18                                       0
19                                       0
20                                       0
21                                       0
0_two                                snake
1_two      

In [299]:
Gilly_Text = Gilly.values.tolist()
Gilly_Text

[u'shouldnt training',
 u'one hates',
 u'dont let send us away',
 u'cant leave theyll execute',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'snake',
 u'know',
 u'well youre wonderful teacher',
 u'thats alright',
 u'dont know',
 u'sam',
 u'shireen',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'world',
 u'grew books',
 u'wheres',
 u'im sorry dont know things',
 u'wash linens',
 u'like maester aemon',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0'

In [300]:
Gilly_Words = []

for word in Gilly_Text:
    if len(word)>=1:
        if word != '0':
            Gilly_Words.append(word)
        
Gilly_Words 

[u'shouldnt training',
 u'one hates',
 u'dont let send us away',
 u'cant leave theyll execute',
 u'snake',
 u'know',
 u'well youre wonderful teacher',
 u'thats alright',
 u'dont know',
 u'sam',
 u'shireen',
 u'world',
 u'grew books',
 u'wheres',
 u'im sorry dont know things',
 u'wash linens',
 u'like maester aemon',
 u'get sleep sam',
 u'get sleep',
 u'leave alone',
 u'leave alone',
 u'sam',
 u'sam',
 u'youre',
 u'dont stupid sam youre fighter',
 u'promise whatever happens youll take care little sam',
 u'need water',
 u'hurting',
 u'good',
 u'im one got punched kicked face',
 u'im good',
 u'little',
 u'need check baby sam']

In [301]:
Gilly_Words_String = ' '.join(Gilly_Words)
Gilly_Words_String

u'shouldnt training one hates dont let send us away cant leave theyll execute snake know well youre wonderful teacher thats alright dont know sam shireen world grew books wheres im sorry dont know things wash linens like maester aemon get sleep sam get sleep leave alone leave alone sam sam youre dont stupid sam youre fighter promise whatever happens youll take care little sam need water hurting good im one got punched kicked face im good little need check baby sam'

In [302]:
Gilly_String_Length = len(Gilly_Words_String)
Gilly_String_Length

466

In [303]:
Gilly_Sentiment = TextBlob(Gilly_Words_String).sentiment
Gilly_Sentiment

Sentiment(polarity=0.10357142857142856, subjectivity=0.7428571428571428)

### Jaime Lannister

In [304]:
Jaime = season_five.loc['Jaime']
print Jaime

0           theyre waiting night make sure hes really dead...
1                                                           0
2                                                           0
3                                                           0
4                                                           0
5                                                           0
6                                                           0
7                                                           0
8                                                           0
9                                                           0
10                                                          0
11                                                          0
12                                                          0
13                                                          0
14                                                          0
15                                                          0
16      

In [305]:
Jaime_Text = Jaime.values.tolist()
Jaime_Text

[u'theyre waiting night make sure hes really dead soon see stones eyes theyll set work tearing us apart',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'threat',
 u'note',
 u'softer',
 u'loud',
 u'world cant know knows shes daughter',
 u'father children theyd stoned streets',
 u'ill make things better',
 u'im going dorne',
 u'im going ask anything',
 u'army',
 u'ill find',
 u'never said going alone',
 u'ser bronn blackwater',
 u'thank',
 u'pleasure',
 u'beautiful bride youve chosen',
 '',
 u'good',
 u'mmm',
 u'cause youre going come help something important',
 u'far south south goes',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'ships sailing oldtown',
 '',
 u'happy go back',
 u'kidnapping princess',
 u'thats youre',
 u'dont want start war',
 '',
 u'quietly varys set free',
 u'murdered father'

In [306]:
Jaime_Words = []

for word in Jaime_Text:
    if len(word)>=1:
        if word != '0':
            Jaime_Words.append(word)
        
Jaime_Words 

[u'theyre waiting night make sure hes really dead soon see stones eyes theyll set work tearing us apart',
 u'threat',
 u'note',
 u'softer',
 u'loud',
 u'world cant know knows shes daughter',
 u'father children theyd stoned streets',
 u'ill make things better',
 u'im going dorne',
 u'im going ask anything',
 u'army',
 u'ill find',
 u'never said going alone',
 u'ser bronn blackwater',
 u'thank',
 u'pleasure',
 u'beautiful bride youve chosen',
 u'good',
 u'mmm',
 u'cause youre going come help something important',
 u'far south south goes',
 u'ships sailing oldtown',
 u'happy go back',
 u'kidnapping princess',
 u'thats youre',
 u'dont want start war',
 u'quietly varys set free',
 u'murdered father',
 u'far ive seen theyre shit ways die',
 u'dont care whats sung im dead',
 u'sounds like rest',
 u'lets go',
 u'pentoshi',
 u'said',
 u'bag gold',
 u'heavy bag',
 u'four',
 u'one hes slow',
 u'thought sharks would get us',
 u'could sworn shark fins',
 u'luck',
 u'corpses raise questions question

In [307]:
Jaime_Words_String = ' '.join(Jaime_Words)
Jaime_Words_String

u'theyre waiting night make sure hes really dead soon see stones eyes theyll set work tearing us apart threat note softer loud world cant know knows shes daughter father children theyd stoned streets ill make things better im going dorne im going ask anything army ill find never said going alone ser bronn blackwater thank pleasure beautiful bride youve chosen good mmm cause youre going come help something important far south south goes ships sailing oldtown happy go back kidnapping princess thats youre dont want start war quietly varys set free murdered father far ive seen theyre shit ways die dont care whats sung im dead sounds like rest lets go pentoshi said bag gold heavy bag four one hes slow thought sharks would get us could sworn shark fins luck corpses raise questions questions raise armies holding hand trying blend thats water gardens like improvise myrcella lets speak private excellent go myrcella youll fine promise bronn hands im sorry mothers worried good dont understand pri

In [308]:
Jaime_String_Length = len(Jaime_Words_String)
Jaime_String_Length

1379

In [309]:
Jaime_Sentiment = TextBlob(Jaime_Words_String).sentiment
Jaime_Sentiment

Sentiment(polarity=0.22473118279569887, subjectivity=0.7362903225806453)

### Jon Snow

In [310]:
Jon = season_five.loc['Jon']
print Jon

0                          wasnt heavy wouldnt stop sword get
1                                                        come
2                                             good good pivot
3                                                roose bolton
4                                want great many things grace
5                                             theyre good men
6                                                    belonged
7                                        born wrong side wall
8                    men nights watch sworn play part stannis
9                             grace want wildlings march army
10                                    dont think thats likely
11                                                    respect
12                                                  much time
13                                                           
14                                         know stannis wants
15                                         shouldnt king bold
16      

In [311]:
Jon_Text = Jon.values.tolist()
Jon_Text

[u'wasnt heavy wouldnt stop sword get',
 u'come',
 u'good good pivot',
 u'roose bolton',
 u'want great many things grace',
 u'theyre good men',
 u'belonged',
 u'born wrong side wall',
 u'men nights watch sworn play part stannis',
 u'grace want wildlings march army',
 u'dont think thats likely',
 u'respect',
 u'much time',
 '',
 u'know stannis wants',
 u'shouldnt king bold',
 u'told werent conquer',
 u'spent life convincing clans come together first time history',
 u'bend knee save people',
 u'many tens thousands right',
 u'theyll burn alive',
 u'think youre making terrible mistake',
 u'respect grace free folk never follow matter',
 '',
 u'bear island knows king king north whose name stark',
 u'apologize grace',
 u'likely',
 u'unpleasant expect',
 u'dont doubt grace',
 u'cant',
 u'first thing ever remember wanting',
 u'im going refuse',
 u'swore vow nights watch',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'stands',
 u'olly steward lord commander mormonts'

In [312]:
Jon_Words = []

for word in Jon_Text:
    if len(word)>=1:
        if word != '0':
            Jon_Words.append(word)
        
Jon_Words 

[u'wasnt heavy wouldnt stop sword get',
 u'come',
 u'good good pivot',
 u'roose bolton',
 u'want great many things grace',
 u'theyre good men',
 u'belonged',
 u'born wrong side wall',
 u'men nights watch sworn play part stannis',
 u'grace want wildlings march army',
 u'dont think thats likely',
 u'respect',
 u'much time',
 u'know stannis wants',
 u'shouldnt king bold',
 u'told werent conquer',
 u'spent life convincing clans come together first time history',
 u'bend knee save people',
 u'many tens thousands right',
 u'theyll burn alive',
 u'think youre making terrible mistake',
 u'respect grace free folk never follow matter',
 u'bear island knows king king north whose name stark',
 u'apologize grace',
 u'likely',
 u'unpleasant expect',
 u'dont doubt grace',
 u'cant',
 u'first thing ever remember wanting',
 u'im going refuse',
 u'swore vow nights watch',
 u'stands',
 u'olly steward lord commander mormonts',
 u'refuse',
 u'wish could fight beside',
 u'may ask grace long plan stay castle 

In [313]:
Jon_Words_String = ' '.join(Jon_Words)
Jon_Words_String

u'wasnt heavy wouldnt stop sword get come good good pivot roose bolton want great many things grace theyre good men belonged born wrong side wall men nights watch sworn play part stannis grace want wildlings march army dont think thats likely respect much time know stannis wants shouldnt king bold told werent conquer spent life convincing clans come together first time history bend knee save people many tens thousands right theyll burn alive think youre making terrible mistake respect grace free folk never follow matter bear island knows king king north whose name stark apologize grace likely unpleasant expect dont doubt grace cant first thing ever remember wanting im going refuse swore vow nights watch stands olly steward lord commander mormonts refuse wish could fight beside may ask grace long plan stay castle black saved us mance rayders army wildlings brothers yes heard best keep enemies close im sorry disappointed long hes ruling ive sworn stay clear politics seven kingdoms needs 

In [314]:
Jon_String_Length = len(Jon_Words_String)
Jon_String_Length

2145

In [315]:
Jon_Sentiment = TextBlob(Jon_Words_String).sentiment
Jon_Sentiment

Sentiment(polarity=0.10729564553093966, subjectivity=0.5183473389355743)

### Jorah Mormont

In [316]:
Jorah = season_five.loc['Jorah']
print Jorah

0                                                  0
1                                                  0
2                                                  0
3                                                  0
4                                                  0
5                                                  0
6                                                  0
7                                                  0
8                                                  0
9                                                  0
10                                                 0
11                                                 0
12                                                 0
13                                                 0
14                                                 0
15                                                 0
16                                                 0
17                                                 0
18                                            

In [317]:
Jorah_Text = Jorah.values.tolist()
Jorah_Text

['0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'captor',
 '',
 u'stay awake',
 u'im taking sister',
 '',
 u'business would queen',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '',
 u'wine',
 '',
 '',
 u'think youll plenty',
 '',
 u'jorah',
 u'youre heavier look',
 u'suppose thats send',
 u'walk coast',
 u'weve got long walk ahead us',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '',
 u'course im hungry',
 u'travelling companion',
 u'im sure youve visited many bro

In [318]:
Jorah_Words = []

for word in Jorah_Text:
    if len(word)>=1:
        if word != '0':
            Jorah_Words.append(word)
        
Jorah_Words 

[u'captor',
 u'stay awake',
 u'im taking sister',
 u'business would queen',
 u'wine',
 u'think youll plenty',
 u'jorah',
 u'youre heavier look',
 u'suppose thats send',
 u'walk coast',
 u'weve got long walk ahead us',
 u'course im hungry',
 u'travelling companion',
 u'im sure youve visited many brothels many cities',
 u'know father',
 u'int',
 u'believe anything',
 u'something greater mean',
 u'neither cynic like',
 u'hard cynic',
 u'doesnt',
 u'first conquer world',
 u'rules',
 u'rightful heir',
 u'shh',
 u'probably came ashore water',
 u'queen daenerys outlawed slavery',
 u'killed dothraki blood rider single combat',
 u'take slavers bay put sword hand ill prove worth',
 u'khaleesi please need moment time',
 u'ive flogged makes happy',
 u'int',
 u'way',
 u'torgo nudho',
 u'none matters',
 u'youve many days',
 u'careful',
 u'second time thanks',
 u'ever kill eyes wide open',
 u'hes foreign dwarf barely speaks language']

In [319]:
Jorah_Words_String = ' '.join(Jorah_Words)
Jorah_Words_String

u'captor stay awake im taking sister business would queen wine think youll plenty jorah youre heavier look suppose thats send walk coast weve got long walk ahead us course im hungry travelling companion im sure youve visited many brothels many cities know father int believe anything something greater mean neither cynic like hard cynic doesnt first conquer world rules rightful heir shh probably came ashore water queen daenerys outlawed slavery killed dothraki blood rider single combat take slavers bay put sword hand ill prove worth khaleesi please need moment time ive flogged makes happy int way torgo nudho none matters youve many days careful second time thanks ever kill eyes wide open hes foreign dwarf barely speaks language'

In [320]:
Jorah_String_Length = len(Jorah_Words_String)
Jorah_String_Length

733

In [321]:
Jorah_Sentiment = TextBlob(Jorah_Words_String).sentiment
Jorah_Sentiment

Sentiment(polarity=0.11187641723356008, subjectivity=0.4519368858654572)

### Margaery Tyrell

In [322]:
Margaery = season_five.loc['Margaery']
print Margaery

0                                                 late dinner
1                                                   im hungry
2                                                  whats name
3               im afraid brother keeping king waiting olyvar
4                         perhaps might consider bit discreet
5           event throws loras clothes shouldnt keep inten...
6                                                       lucky
7                            think want woman married brother
8                                                     perhaps
9                                                           0
10                                                          0
11                                                          0
12                                                          0
13                                                          0
14                                                          0
15                                                          0
16      

In [323]:
Margaery_Text = Margaery.values.tolist()
Margaery_Text

[u'late dinner',
 u'im hungry',
 u'whats name',
 u'im afraid brother keeping king waiting olyvar',
 u'perhaps might consider bit discreet',
 u'event throws loras clothes shouldnt keep intended waiting',
 u'lucky',
 u'think want woman married brother',
 u'perhaps',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '',
 u'yes',
 u'wouldnt glorious',
 u'im fine',
 u'sits',
 u'think going happy tommen',
 u'living tower high touches clouds',
 u'wonderful watching',
 '',
 u'adore always generous kind',
 u'mother',
 u'bring anything eat drink',
 u'sweet',
 u'absolutely adore',
 u'ecstatic',
 u'oh forgive havent court long get confused',
 u'cersei',
 u'imagine celebrations',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'know',
 u'shes jealous youre anymore',
 u'scoffs',
 u'cant bear think brother locked away grimy cell',
 u'promise',
 u

In [324]:
Margaery_Words = []

for word in Margaery_Text:
    if len(word)>=1:
        if word != '0':
            Margaery_Words.append(word)
        
Margaery_Words 

[u'late dinner',
 u'im hungry',
 u'whats name',
 u'im afraid brother keeping king waiting olyvar',
 u'perhaps might consider bit discreet',
 u'event throws loras clothes shouldnt keep intended waiting',
 u'lucky',
 u'think want woman married brother',
 u'perhaps',
 u'yes',
 u'wouldnt glorious',
 u'im fine',
 u'sits',
 u'think going happy tommen',
 u'living tower high touches clouds',
 u'wonderful watching',
 u'adore always generous kind',
 u'mother',
 u'bring anything eat drink',
 u'sweet',
 u'absolutely adore',
 u'ecstatic',
 u'oh forgive havent court long get confused',
 u'cersei',
 u'imagine celebrations',
 u'know',
 u'shes jealous youre anymore',
 u'scoffs',
 u'cant bear think brother locked away grimy cell',
 u'promise',
 u'youre king andals lord seven kingdoms protector realm',
 u'dont know',
 u'walking',
 u'need family grace',
 u'everyone knew renly',
 u'kings brother',
 u'cersei behind',
 u'call forward',
 u'queen',
 u'lies',
 u'yes swear',
 u'tommen',
 u'cant queen',
 u'know',

In [325]:
Margaery_Words_String = ' '.join(Margaery_Words)
Margaery_Words_String

u'late dinner im hungry whats name im afraid brother keeping king waiting olyvar perhaps might consider bit discreet event throws loras clothes shouldnt keep intended waiting lucky think want woman married brother perhaps yes wouldnt glorious im fine sits think going happy tommen living tower high touches clouds wonderful watching adore always generous kind mother bring anything eat drink sweet absolutely adore ecstatic oh forgive havent court long get confused cersei imagine celebrations know shes jealous youre anymore scoffs cant bear think brother locked away grimy cell promise youre king andals lord seven kingdoms protector realm dont know walking need family grace everyone knew renly kings brother cersei behind call forward queen lies yes swear tommen cant queen know lies come easily dont want see leave get hateful bitch'

In [326]:
Margaery_String_Length = len(Margaery_Words_String)
Margaery_String_Length

835

In [327]:
Margaery_Sentiment = TextBlob(Margaery_Words_String).sentiment
Margaery_Sentiment

Sentiment(polarity=0.18622222222222226, subjectivity=0.7137777777777778)

### Melisandre

In [328]:
Melisandre = season_five.loc['Melisandre']
print Melisandre

0                                    king wants word
1                                              never
2                                               feel
3           man woman young old lord peasant choices
4               free folk one true king name stannis
5                                                  0
6                                                  0
7                                                  0
8                                                  0
9                                                  0
10                                                 0
11                                                 0
12                                                 0
13                                                 0
14                                                 0
15                                                 0
16                                                 0
17                                                 0
18                                            

In [329]:
Melisandre_Text = Melisandre.values.tolist()
Melisandre_Text

[u'king wants word',
 u'never',
 u'feel',
 u'man woman young old lord peasant choices',
 u'free folk one true king name stannis',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'walking towards',
 u'father lords chosen king',
 u'march winterfell soon',
 u'put faith ser davos left behind',
 u'need faith king',
 u'serve lord',
 u'lord commander',
 u'come us ride south',
 u'visions',
 u'feel heart beating',
 u'lord light made us male female',
 u'shouldnt tell',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',


In [330]:
Melisandre_Words = []

for word in Melisandre_Text:
    if len(word)>=1:
        if word != '0':
            Melisandre_Words.append(word)
        
Melisandre_Words 

[u'king wants word',
 u'never',
 u'feel',
 u'man woman young old lord peasant choices',
 u'free folk one true king name stannis',
 u'walking towards',
 u'father lords chosen king',
 u'march winterfell soon',
 u'put faith ser davos left behind',
 u'need faith king',
 u'serve lord',
 u'lord commander',
 u'come us ride south',
 u'visions',
 u'feel heart beating',
 u'lord light made us male female',
 u'shouldnt tell',
 u'saw king stared flames',
 u'know',
 u'trust lord',
 u'seen walk along battlements wintefell',
 u'sometimes sacrifices must made ensure victory',
 u'stannis',
 u'doubt still',
 u'one way',
 u'soon princess',
 u'year lord',
 u'take']

In [331]:
Melisandre_Words_String = ' '.join(Melisandre_Words)
Melisandre_Words_String

u'king wants word never feel man woman young old lord peasant choices free folk one true king name stannis walking towards father lords chosen king march winterfell soon put faith ser davos left behind need faith king serve lord lord commander come us ride south visions feel heart beating lord light made us male female shouldnt tell saw king stared flames know trust lord seen walk along battlements wintefell sometimes sacrifices must made ensure victory stannis doubt still one way soon princess year lord take'

In [332]:
Melisandre_String_Length = len(Melisandre_Words_String)
Melisandre_String_Length

512

In [333]:
Melisandre_Sentiment = TextBlob(Melisandre_Words_String).sentiment
Melisandre_Sentiment

Sentiment(polarity=0.11499999999999999, subjectivity=0.38166666666666665)

### Missandei

In [334]:
Missandei = season_five.loc['Missandei']
print Missandei

0           white rat unsullied heard found body brothel
1                                                      0
2                                                      0
3                                                      0
4                                                      0
5                                                      0
6                                                      0
7                                                      0
8                                                      0
9                                                      0
10                                                     0
11                                                     0
12                                                     0
13                                                     0
14                                                     0
15                                                     0
16                                                     0
17                             

In [335]:
Missandei_Text = Missandei.values.tolist()
Missandei_Text

[u'white rat unsullied heard found body brothel',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'glory',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'valyrian three days',
 u'valyrian failed one',
 u'men fear death',
 u'grace think fit opinion matters',
 u'tell seen grace',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 

In [336]:
Missandei_Words = []

for word in Missandei_Text:
    if len(word)>=1:
        if word != '0':
            Missandei_Words.append(word)
        
Missandei_Words 

[u'white rat unsullied heard found body brothel',
 u'glory',
 u'valyrian three days',
 u'valyrian failed one',
 u'men fear death',
 u'grace think fit opinion matters',
 u'tell seen grace',
 u'valyrian bit rusty',
 u'strong enough go anywhere',
 u'true']

In [337]:
Missandei_Words_String = ' '.join(Missandei_Words)
Missandei_Words_String

u'white rat unsullied heard found body brothel glory valyrian three days valyrian failed one men fear death grace think fit opinion matters tell seen grace valyrian bit rusty strong enough go anywhere true'

In [338]:
Missandei_String_Length = len(Missandei_Words_String)
Missandei_String_Length

203

In [339]:
Missandei_Sentiment = TextBlob(Missandei_Words_String).sentiment
Missandei_Sentiment

Sentiment(polarity=0.11388888888888889, subjectivity=0.4305555555555555)

### Olenna Tyrell

In [340]:
Olenna = season_five.loc['Olenna']
print Olenna

0           0
1           0
2           0
3           0
4           0
5           0
6           0
7           0
8           0
9           0
10          0
11          0
12          0
13          0
14          0
15          0
16          0
17          0
18          0
19          0
20          0
21          0
0_two       0
1_two       0
2_two       0
3_two       0
4_two       0
5_two       0
6_two       0
7_two       0
8_two       0
9_two       0
10_two      0
11_two      0
12_two      0
13_two      0
14_two      0
15_two      0
16_two      0
17_two      0
18_two      0
19_two      0
20_two      0
21_two      0
22          0
0           0
1           0
2           0
3           0
4           0
5           0
6           0
7           0
8           0
9           0
10          0
11          0
12          0
13          0
14          0
15          0
16          0
           ..
1_eight     0
2_eight     0
3_eight     0
4_eight     0
5_eight     0
6_eight     0
7_eight     0
8_eight     0
9_eigh

In [341]:
Olenna_Text = Olenna.values.tolist()
Olenna_Text

['0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'oh',
 u'renly baratheon shagged half stable boys seven kingdoms',
 u'loras queens brother',
 u'course',
 u'put pen dear know arent writing anything',
 u'famous tart queen cersei',
 u'know youre behind absurd incarceration grandso

In [342]:
Olenna_Words = []

for word in Olenna_Text:
    if len(word)>=1:
        if word != '0':
            Olenna_Words.append(word)
        
Olenna_Words 

[u'oh',
 u'renly baratheon shagged half stable boys seven kingdoms',
 u'loras queens brother',
 u'course',
 u'put pen dear know arent writing anything',
 u'famous tart queen cersei',
 u'know youre behind absurd incarceration grandson',
 u'crown suddenly stopped needing troops gold wheat house supplies',
 u'didnt trust father',
 u'well think thats quite enough',
 u'decency stand talk lady',
 u'hips',
 u'man people game',
 u'spare homilies sparrow',
 u'im grandson granddaughter',
 u'dont walk away',
 u'want',
 u'communicate demands',
 u'half men women children foul city break sacred laws',
 u'equality want',
 u'youre',
 u'clientele clearly',
 u'youve always rather impressed havent',
 u'dont pretend concern house grandchildren',
 u'want']

In [343]:
Olenna_Words_String = ' '.join(Olenna_Words)
Olenna_Words_String

u'oh renly baratheon shagged half stable boys seven kingdoms loras queens brother course put pen dear know arent writing anything famous tart queen cersei know youre behind absurd incarceration grandson crown suddenly stopped needing troops gold wheat house supplies didnt trust father well think thats quite enough decency stand talk lady hips man people game spare homilies sparrow im grandson granddaughter dont walk away want communicate demands half men women children foul city break sacred laws equality want youre clientele clearly youve always rather impressed havent dont pretend concern house grandchildren want'

In [344]:
Olenna_String_Length = len(Olenna_Words_String)
Olenna_String_Length

620

In [345]:
Olenna_Sentiment = TextBlob(Olenna_Words_String).sentiment
Olenna_Sentiment

Sentiment(polarity=-0.0033333333333333214, subjectivity=0.5816666666666667)

### Ramsay Bolton

In [346]:
Ramsay = season_five.loc['Ramsay']
print Ramsay

0                                                      0
1                                                      0
2                                                      0
3                                                      0
4                                                      0
5                                                      0
6                                                      0
7                                                      0
8                                                      0
9                                                      0
10                                                     0
11                                                     0
12                                                     0
13                                                     0
14                                                     0
15                                                     0
16                                                     0
17                             

In [347]:
Ramsay_Text = Ramsay.values.tolist()
Ramsay_Text

['0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'cant hold north let lesser lords insult us',
 u'roose',
 u'flayed living along wife brother',
 u'new lord cerwyn paid taxes',
 u'pact lannisters protects roose',
 u'honor meet lady',
 u'ill never hurt',
 u'yes father',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'im going marry',
 u'meant',
 u'course',
 u'think shes pretty',
 u'laughs',
 u'something tell',
 u'reek',
 '',
 u'saw',
 u'mustnt keep secrets reek',
 u'give hand',
 u'forgive',
 u'allow',
 u'mother',
 u'lady family northerners',
 u'you

In [348]:
Ramsay_Words = []

for word in Ramsay_Text:
    if len(word)>=1:
        if word != '0':
            Ramsay_Words.append(word)
        
Ramsay_Words 

[u'cant hold north let lesser lords insult us',
 u'roose',
 u'flayed living along wife brother',
 u'new lord cerwyn paid taxes',
 u'pact lannisters protects roose',
 u'honor meet lady',
 u'ill never hurt',
 u'yes father',
 u'im going marry',
 u'meant',
 u'course',
 u'think shes pretty',
 u'laughs',
 u'something tell',
 u'reek',
 u'saw',
 u'mustnt keep secrets reek',
 u'give hand',
 u'forgive',
 u'allow',
 u'mother',
 u'lady family northerners',
 u'youre right',
 u'heard two reunited',
 u'thats new name reek',
 u'reek something say',
 u'look reek',
 u'sorry',
 u'done',
 u'wonderful',
 u'shes pregnant',
 u'manage',
 u'getting pregnant',
 u'course find',
 u'boy',
 u'position quite clear',
 u'yes',
 u'ramsay house bolton',
 u'pleased lady',
 u'good',
 u'youre lying',
 u'lying husband wedding night would bad way start marriage',
 u'good',
 u'oh',
 u'reek',
 u'youve known sansa since girl',
 u'father told marrying half expected fat bearded beast',
 u'scouts report stannis baratheon rides win

In [349]:
Ramsay_Words_String = ' '.join(Ramsay_Words)
Ramsay_Words_String

u'cant hold north let lesser lords insult us roose flayed living along wife brother new lord cerwyn paid taxes pact lannisters protects roose honor meet lady ill never hurt yes father im going marry meant course think shes pretty laughs something tell reek saw mustnt keep secrets reek give hand forgive allow mother lady family northerners youre right heard two reunited thats new name reek reek something say look reek sorry done wonderful shes pregnant manage getting pregnant course find boy position quite clear yes ramsay house bolton pleased lady good youre lying lying husband wedding night would bad way start marriage good oh reek youve known sansa since girl father told marrying half expected fat bearded beast scouts report stannis baratheon rides winterfell ill baby brother ive naturalized royal decree sansa tough old bird stannis isnt north sit wait let stannis decide type fight going looks like done accept surrender'

In [350]:
Ramsay_String_Length = len(Ramsay_Words_String)
Ramsay_String_Length

933

In [351]:
Ramsay_Sentiment = TextBlob(Ramsay_Words_String).sentiment
Ramsay_Sentiment

Sentiment(polarity=0.08597763347763347, subjectivity=0.6397402597402596)

### Samwell Tarly

In [352]:
Sam = season_five.loc['Sam']
print Sam

0                                  well im hardly new recruit
1           ser alliser chosen new lord commander hates wi...
2                                                   wildlings
3                                                  sure thing
4                                                        told
5                                                           0
6                                                           0
7                                                           0
8                                                           0
9                                                           0
10                                                          0
11                                                          0
12                                                          0
13                                                          0
14                                                          0
15                                                          0
16      

In [353]:
Sam_Text = Sam.values.tolist()
Sam_Text

[u'well im hardly new recruit',
 u'ser alliser chosen new lord commander hates wildlings',
 u'wildlings',
 u'sure thing',
 u'told',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'hmm',
 u'deserve',
 u'name gilly',
 u'wildling girl baby lord janos',
 u'whilst lord janos hiding women children jon snow leading',
 u'ser alliser fought bravely true',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'apologizes',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'havent heard either',
 u'chuckles looking next letter',
 u'know im sorry need men supplies',
 u'swore watchers wall',
 u'apologies lady',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'dont say maester aemon',
 u'standing laughter',
 u

In [354]:
Sam_Words = []

for word in Sam_Text:
    if len(word)>=1:
        if word != '0':
            Sam_Words.append(word)
        
Sam_Words 

[u'well im hardly new recruit',
 u'ser alliser chosen new lord commander hates wildlings',
 u'wildlings',
 u'sure thing',
 u'told',
 u'hmm',
 u'deserve',
 u'name gilly',
 u'wildling girl baby lord janos',
 u'whilst lord janos hiding women children jon snow leading',
 u'ser alliser fought bravely true',
 u'apologizes',
 u'havent heard either',
 u'chuckles looking next letter',
 u'know im sorry need men supplies',
 u'swore watchers wall',
 u'apologies lady',
 u'dont say maester aemon',
 u'standing laughter',
 u'every book',
 u'well',
 u'fathers literate man',
 u'citadel',
 u'gilly look',
 u'well gilly',
 u'train maesters',
 u'wanted one young',
 u'ah grace',
 u'grace',
 u'grace',
 u'dagger made dragonglass',
 u'maesters call obsidian stannis',
 u'dont know',
 u'ive seen grace',
 u'safe travels lord commander',
 u'oh jon',
 u'dont know',
 u'ill stay',
 u'get hands',
 u'gilly go get back room lock door',
 u'im warning',
 u'said get hands',
 u'killed white walker',
 u'im alright',
 u'kind m

In [355]:
Sam_Words_String = ' '.join(Sam_Words)
Sam_Words_String

u'well im hardly new recruit ser alliser chosen new lord commander hates wildlings wildlings sure thing told hmm deserve name gilly wildling girl baby lord janos whilst lord janos hiding women children jon snow leading ser alliser fought bravely true apologizes havent heard either chuckles looking next letter know im sorry need men supplies swore watchers wall apologies lady dont say maester aemon standing laughter every book well fathers literate man citadel gilly look well gilly train maesters wanted one young ah grace grace grace dagger made dragonglass maesters call obsidian stannis dont know ive seen grace safe travels lord commander oh jon dont know ill stay get hands gilly go get back room lock door im warning said get hands killed white walker im alright kind man would ran away saw someone hurting course stay know mean scared whos come worry youre good lad yes weve fighting years wildlings people like us olly olly ive seen army dead jons taking risk heart try worry olly wasnt d

In [356]:
Sam_String_Length = len(Sam_Words_String)
Sam_String_Length

1130

In [357]:
Sam_Sentiment = TextBlob(Sam_Words_String).sentiment
Sam_Sentiment

Sentiment(polarity=-0.04237012987012988, subjectivity=0.5159752284752285)

### Sansa Stark

In [358]:
Sansa = season_five.loc['Sansa']
print Sansa

0                                          heading west
1                        wanted betray us already would
2                                                      
3                                                 going
4                                                     0
5                                                     0
6                                                     0
7                                                     0
8                                                     0
9                                                     0
10                                                    0
11                                                    0
12                                                    0
13                                                    0
14                                                    0
15                                                    0
16                                                    0
17                                              

In [359]:
Sansa_Text = Sansa.values.tolist()
Sansa_Text

[u'heading west',
 u'wanted betray us already would',
 '',
 u'going',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'left maester gave raven scroll',
 u'mother used say dark wings dark words',
 u'good news',
 u'thought still mourn death beloved aunt lysa',
 u'ill',
 u'dont see fuss',
 u'give courage',
 u'sometimes',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'way kings landing father arya taking',
 u'boltons winterfell',
 u'roose bolton murdered brother',
 u'serves lannisters',
 u'wont go',
 u'anymore',
 u'cant marry',
 u'smiles',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'father never talked',
 u'yes chose kidnapped raped',
 u'dressed riding',
 u'going',
 u'kings landing',
 u'cant leave',
 u'know',
 u'dont know',
 u'think hell defeat boltons',
 u'youre right',
 u'wouldnt wardeness north baelish',
 u'youre wrong',
 u'do

In [360]:
Sansa_Words = []

for word in Sansa_Text:
    if len(word)>=1:
        if word != '0':
            Sansa_Words.append(word)
        
Sansa_Words 

[u'heading west',
 u'wanted betray us already would',
 u'going',
 u'left maester gave raven scroll',
 u'mother used say dark wings dark words',
 u'good news',
 u'thought still mourn death beloved aunt lysa',
 u'ill',
 u'dont see fuss',
 u'give courage',
 u'sometimes',
 u'way kings landing father arya taking',
 u'boltons winterfell',
 u'roose bolton murdered brother',
 u'serves lannisters',
 u'wont go',
 u'anymore',
 u'cant marry',
 u'smiles',
 u'father never talked',
 u'yes chose kidnapped raped',
 u'dressed riding',
 u'going',
 u'kings landing',
 u'cant leave',
 u'know',
 u'dont know',
 u'think hell defeat boltons',
 u'youre right',
 u'wouldnt wardeness north baelish',
 u'youre wrong',
 u'dont know',
 u'frightens',
 u'expect ill married woman time return',
 u'oh dont need woman',
 u'woman',
 u'mother',
 u'thank',
 u'id rather mother',
 u'theon',
 u'yes thank lord',
 u'isnt strange place',
 u'im happy',
 u'want',
 u'others',
 u'others',
 u'hunt',
 u'name',
 u'long loved myranda',
 u'go

In [361]:
Sansa_Words_String = ' '.join(Sansa_Words)
Sansa_Words_String

u'heading west wanted betray us already would going left maester gave raven scroll mother used say dark wings dark words good news thought still mourn death beloved aunt lysa ill dont see fuss give courage sometimes way kings landing father arya taking boltons winterfell roose bolton murdered brother serves lannisters wont go anymore cant marry smiles father never talked yes chose kidnapped raped dressed riding going kings landing cant leave know dont know think hell defeat boltons youre right wouldnt wardeness north baelish youre wrong dont know frightens expect ill married woman time return oh dont need woman woman mother thank id rather mother theon yes thank lord isnt strange place im happy want others others hunt name long loved myranda go im touching think care take man yes lord tyrion kind gentle never touched lord yes sir help theon theon already hurts every night help family still friends north name theon greyjoy isnt step mother pregnant happens boy reek good know went bran r

In [362]:
Sansa_String_Length = len(Sansa_Words_String)
Sansa_String_Length

1045

In [363]:
Sansa_Sentiment = TextBlob(Sansa_Words_String).sentiment
Sansa_Sentiment

Sentiment(polarity=0.2036340852130326, subjectivity=0.6176691729323309)

### Shireen Baratheon

In [364]:
Shireen = season_five.loc['Shireen']
print Shireen

0                                                           0
1                                                           0
2                                                           0
3                                                           0
4                                                           0
5                                                           0
6                                                           0
7                                                           0
8                                                           0
9                                                           0
10                                                          0
11                                                          0
12                                                          0
13                                                          0
14                                                          0
15                                                          0
16      

In [365]:
Shireen_Text = Shireen.values.tolist()
Shireen_Text

['0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'right good',
 u'youll learn promise',
 u'three',
 u'lot time practice',
 u'greyscale',
 u'dont remember',
 u'mother',
 '',
 u'names gilly',
 u'gilly wouldnt',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'turns around holding something',
 u'looks',
 u'told stannis',
 u'ashamed father',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'winterfell',
 u'going battle',
 u'im scared',
 u'smiling',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 

In [366]:
Shireen_Words = []

for word in Shireen_Text:
    if len(word)>=1:
        if word != '0':
            Shireen_Words.append(word)
        
Shireen_Words 

[u'right good',
 u'youll learn promise',
 u'three',
 u'lot time practice',
 u'greyscale',
 u'dont remember',
 u'mother',
 u'names gilly',
 u'gilly wouldnt',
 u'turns around holding something',
 u'looks',
 u'told stannis',
 u'ashamed father',
 u'winterfell',
 u'going battle',
 u'im scared',
 u'smiling',
 u'hes beautiful',
 u'thank',
 u'make doe company',
 u'getting present',
 u'youll read',
 u'dance dragons',
 u'story fight rhaenyra targaryen halfbrother aegon control seven kingdoms',
 u'thats call',
 u'think poetic',
 u'stannis',
 u'alright father',
 u'doesnt matter',
 u'good want',
 u'wheres father',
 u'let see father',
 u'mother dont please']

In [367]:
Shireen_Words_String = ' '.join(Shireen_Words)
Shireen_Words_String

u'right good youll learn promise three lot time practice greyscale dont remember mother names gilly gilly wouldnt turns around holding something looks told stannis ashamed father winterfell going battle im scared smiling hes beautiful thank make doe company getting present youll read dance dragons story fight rhaenyra targaryen halfbrother aegon control seven kingdoms thats call think poetic stannis alright father doesnt matter good want wheres father let see father mother dont please'

In [368]:
Shireen_String_Length = len(Shireen_Words_String)
Shireen_String_Length

487

In [369]:
Shireen_Sentiment = TextBlob(Shireen_Words_String).sentiment
Shireen_Sentiment

Sentiment(polarity=0.4851190476190476, subjectivity=0.580952380952381)

### Stannis Baratheon¶

In [370]:
Stannis = season_five.loc['Stannis']
print Stannis

0                                       know rules winterfell
1                    traitor plunged dagger robb starks heart
2                                                      matter
3                                     swear follow ill pardon
4           ill offer lives freedom mance kneels swears lo...
5                                                 admire dont
6                                                       likes
7                                                   nightfall
8                                                  kneel live
9                                                           0
10                                                          0
11                                                          0
12                                                          0
13                                                          0
14                                                          0
15                                                          0
16      

In [371]:
Stannis_Text = Stannis.values.tolist()
Stannis_Text

[u'know rules winterfell',
 u'traitor plunged dagger robb starks heart',
 u'matter',
 u'swear follow ill pardon',
 u'ill offer lives freedom mance kneels swears loyalty',
 u'admire dont',
 u'likes',
 u'nightfall',
 u'kneel live',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '',
 u'jon',
 u'lady bear island child',
 u'know',
 u'bravery made look weak',
 u'give north',
 u'kneel',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'olly closes door',
 u'well',
 u'say word',
 u'im giving chance avenge family',
 u'bored us already',
 u'know',
 u'theyd rather burn fight',
 u'youre lord commander',
 u'many enemies castle black',
 u'whoever said didnt many enemies',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'lord commander nights watch',
 u'fault',
 u'must',
 u'wont',
 u'walking away',
 u'father used tell boredom indicates lack inner resources',
 u'know castle black plac

In [372]:
Stannis_Words = []

for word in Stannis_Text:
    if len(word)>=1:
        if word != '0':
            Stannis_Words.append(word)
        
Stannis_Words 

[u'know rules winterfell',
 u'traitor plunged dagger robb starks heart',
 u'matter',
 u'swear follow ill pardon',
 u'ill offer lives freedom mance kneels swears loyalty',
 u'admire dont',
 u'likes',
 u'nightfall',
 u'kneel live',
 u'jon',
 u'lady bear island child',
 u'know',
 u'bravery made look weak',
 u'give north',
 u'kneel',
 u'olly closes door',
 u'well',
 u'say word',
 u'im giving chance avenge family',
 u'bored us already',
 u'know',
 u'theyd rather burn fight',
 u'youre lord commander',
 u'many enemies castle black',
 u'whoever said didnt many enemies',
 u'lord commander nights watch',
 u'fault',
 u'must',
 u'wont',
 u'walking away',
 u'father used tell boredom indicates lack inner resources',
 u'know castle black place child shireen',
 u'say',
 u'infant stands walks around desk dornish trailer landed dragonstone',
 u'nothing',
 u'youre samwell tarly',
 u'dont look like soldier',
 u'dragonglass',
 u'lady melisandre told death marches wall',
 u'seen',
 u'jon snow returns wildli

In [373]:
Stannis_Words_String = ' '.join(Stannis_Words)
Stannis_Words_String

u'know rules winterfell traitor plunged dagger robb starks heart matter swear follow ill pardon ill offer lives freedom mance kneels swears loyalty admire dont likes nightfall kneel live jon lady bear island child know bravery made look weak give north kneel olly closes door well say word im giving chance avenge family bored us already know theyd rather burn fight youre lord commander many enemies castle black whoever said didnt many enemies lord commander nights watch fault must wont walking away father used tell boredom indicates lack inner resources know castle black place child shireen say infant stands walks around desk dornish trailer landed dragonstone nothing youre samwell tarly dont look like soldier dragonglass lady melisandre told death marches wall seen jon snow returns wildlings need theyre coming us hope know youre wildlings else sell swords loyal nothing gold davos right time risk everything dont know saw trust sure dont roberts bastard must another way shes daughter get

In [374]:
Stannis_String_Length = len(Stannis_Words_String)
Stannis_String_Length

1437

In [375]:
Stannis_Sentiment = TextBlob(Stannis_Words_String).sentiment
Stannis_Sentiment

Sentiment(polarity=0.07684498041640897, subjectivity=0.5309334845049131)

### Theon Greyjoy

In [376]:
Theon = season_five.loc['Theon']
print Theon

0                                                           0
1                                                           0
2                                                           0
3                                                           0
4                                                           0
5                                                           0
6                                                           0
7                                                           0
8                                                           0
9                                                           0
10                                                          0
11                                                          0
12                                                          0
13                                                          0
14                                                          0
15                                                          0
16      

In [377]:
Theon_Text = Theon.values.tolist()
Theon_Text

['0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'shouldnt',
 u'lord',
 u'stuttering',
 u'sansa',
 u'yes',
 u'turns around',
 u'moment stuttering',
 u'im sorry',
 u'killing brothers',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'lord ramsay said im take arm',
 u'please',
 u'sansa house stark comes wed woman grown trueborn noble',
 u'theon house greyjoy',
 '0',
 '0',
 '0',


In [378]:
Theon_Words = []

for word in Theon_Text:
    if len(word)>=1:
        if word != '0':
            Theon_Words.append(word)
        
Theon_Words 

[u'shouldnt',
 u'lord',
 u'stuttering',
 u'sansa',
 u'yes',
 u'turns around',
 u'moment stuttering',
 u'im sorry',
 u'killing brothers',
 u'lord ramsay said im take arm',
 u'please',
 u'sansa house stark comes wed woman grown trueborn noble',
 u'theon house greyjoy',
 u'theon lady',
 u'youre wife',
 u'please sansa',
 u'im sorry',
 u'hell see us',
 u'reek lady reek',
 u'theon',
 u'hunted caught strapped cross cut away piece piece theon left',
 u'deserved everything',
 u'werent boys bran rickon',
 u'werent',
 u'cant sansa',
 u'cant unless master says sansa',
 u'werent sansa tell bran rickon dead still breathe air',
 u'werent bran rickon',
 u'cant talk anymore',
 u'go',
 u'hes coming back']

In [379]:
Theon_Words_String = ' '.join(Theon_Words)
Theon_Words_String

u'shouldnt lord stuttering sansa yes turns around moment stuttering im sorry killing brothers lord ramsay said im take arm please sansa house stark comes wed woman grown trueborn noble theon house greyjoy theon lady youre wife please sansa im sorry hell see us reek lady reek theon hunted caught strapped cross cut away piece piece theon left deserved everything werent boys bran rickon werent cant sansa cant unless master says sansa werent sansa tell bran rickon dead still breathe air werent bran rickon cant talk anymore go hes coming back'

In [380]:
Theon_String_Length = len(Theon_Words_String)
Theon_String_Length

541

In [381]:
Theon_Sentiment = TextBlob(Theon_Words_String).sentiment
Theon_Sentiment

Sentiment(polarity=-0.1, subjectivity=0.4875)

### Tyrion Lannister

In [382]:
Tyrion = season_five.loc['Tyrion']
print Tyrion

0                  still dont see stay fucking crate set sail
1                          know like stuff shit one air holes
2                                                      pentos
3                                                 much better
4                                          dont think anymore
5                                                         box
6                                                         cut
7                             eunuch spider master whisperers
8                                                      coward
9                                         never told set free
10                                                 could said
11                                        dangerous releasing
12                  drunken dwarf never savior seven kingdoms
13                           youre going find another soldier
14                                         im wellsuited work
15                                                 compassion
16      

In [383]:
Tyrion_Text = Tyrion.values.tolist()
Tyrion_Text

[u'still dont see stay fucking crate set sail',
 u'know like stuff shit one air holes',
 u'pentos',
 u'much better',
 u'dont think anymore',
 u'box',
 u'cut',
 u'eunuch spider master whisperers',
 u'coward',
 u'never told set free',
 u'could said',
 u'dangerous releasing',
 u'drunken dwarf never savior seven kingdoms',
 u'youre going find another soldier',
 u'im wellsuited work',
 u'compassion',
 u'want exactly',
 u'castles made gingerbread moats filled blackberry wine',
 u'never sit iron throne',
 u'good luck finding',
 u'drink death road meereen',
 '0',
 u'agreed come misrepresent intentions',
 u'want take walk',
 u'ought offer cunt',
 u'youre right',
 u'hope find end road meereen',
 u'weve already got ruler',
 u'didnt rule',
 u'managed kill lot people',
 u'find us repulsive',
 u'youre right',
 u'many dwarves world',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'get wheelhouse',
 u'mm get wheelhouse',
 u'walks',
 u'im losing mind',
 u'look thousands miles

In [384]:
Tyrion_Words = []

for word in Tyrion_Text:
    if len(word)>=1:
        if word != '0':
            Tyrion_Words.append(word)
        
Tyrion_Words 

[u'still dont see stay fucking crate set sail',
 u'know like stuff shit one air holes',
 u'pentos',
 u'much better',
 u'dont think anymore',
 u'box',
 u'cut',
 u'eunuch spider master whisperers',
 u'coward',
 u'never told set free',
 u'could said',
 u'dangerous releasing',
 u'drunken dwarf never savior seven kingdoms',
 u'youre going find another soldier',
 u'im wellsuited work',
 u'compassion',
 u'want exactly',
 u'castles made gingerbread moats filled blackberry wine',
 u'never sit iron throne',
 u'good luck finding',
 u'drink death road meereen',
 u'agreed come misrepresent intentions',
 u'want take walk',
 u'ought offer cunt',
 u'youre right',
 u'hope find end road meereen',
 u'weve already got ruler',
 u'didnt rule',
 u'managed kill lot people',
 u'find us repulsive',
 u'youre right',
 u'many dwarves world',
 u'get wheelhouse',
 u'mm get wheelhouse',
 u'walks',
 u'im losing mind',
 u'look thousands miles westeros',
 u'slaves',
 u'tyrion',
 u'even better luck suck dwarfs cock',
 u'

In [385]:
Tyrion_Words_String = ' '.join(Tyrion_Words)
Tyrion_Words_String

u'still dont see stay fucking crate set sail know like stuff shit one air holes pentos much better dont think anymore box cut eunuch spider master whisperers coward never told set free could said dangerous releasing drunken dwarf never savior seven kingdoms youre going find another soldier im wellsuited work compassion want exactly castles made gingerbread moats filled blackberry wine never sit iron throne good luck finding drink death road meereen agreed come misrepresent intentions want take walk ought offer cunt youre right hope find end road meereen weve already got ruler didnt rule managed kill lot people find us repulsive youre right many dwarves world get wheelhouse mm get wheelhouse walks im losing mind look thousands miles westeros slaves tyrion even better luck suck dwarfs cock curious hair appears youre targaryen supporter well watches kiss man shes taken need speak someone hair hello youve got drink look like man without money thats theyve never met queen know spot liar ske

In [386]:
Tyrion_String_Length = len(Dany_Words_String)
Tyrion_String_Length

1839

In [387]:
Tyrion_Sentiment = TextBlob(Dany_Words_String).sentiment
Tyrion_Sentiment

Sentiment(polarity=0.1770833333333333, subjectivity=0.5620370370370371)

### Varys

In [388]:
Varys = season_five.loc['Varys']
print Varys

0                                                  saved life
1                                                            
2                                              home colleague
3                                                        lord
4                             already drank across narrow sea
5                                      talking future country
6                                                 imp halfman
7                                            faster ways kill
8                                   many things friend coward
9                                               brother asked
10                                          refuse kingslayer
11                                                      didnt
12                                       dont believe saviors
13                      many admirable qualities selfpity one
14                                                      think
15                                         never said perfect
16      

In [389]:
Varys_Text = Varys.values.tolist()
Varys_Text

[u'saved life',
 '',
 u'home colleague',
 u'lord',
 u'already drank across narrow sea',
 u'talking future country',
 u'imp halfman',
 u'faster ways kill',
 u'many things friend coward',
 u'brother asked',
 u'refuse kingslayer',
 u'didnt',
 u'dont believe saviors',
 u'many admirable qualities selfpity one',
 u'think',
 u'never said perfect',
 u'peace',
 u'perhaps',
 u'wont',
 u'said anything',
 '0',
 '0',
 u'yes best careful',
 u'dont like',
 u'cant',
 u'really going spend entire road volantis talking futility everything',
 u'road meereen',
 u'told',
 u'quite good know',
 u'still man talent',
 u'yes showed great promise areas well',
 u'people follow leaders',
 u'find repulsive surround large comfortable boxes keep away',
 '',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 u'volantis large city',
 u'likelihood spotted increases hundredfold',
 u'im sure many new ways find saying',
 u'perfectly good face',
 u'anyone recognizes youll lose',
 u'yes',
 u'aside keep moving'

In [390]:
Varys_Words = []

for word in Varys_Text:
    if len(word)>=1:
        if word != '0':
            Varys_Words.append(word)
        
Varys_Words 

[u'saved life',
 u'home colleague',
 u'lord',
 u'already drank across narrow sea',
 u'talking future country',
 u'imp halfman',
 u'faster ways kill',
 u'many things friend coward',
 u'brother asked',
 u'refuse kingslayer',
 u'didnt',
 u'dont believe saviors',
 u'many admirable qualities selfpity one',
 u'think',
 u'never said perfect',
 u'peace',
 u'perhaps',
 u'wont',
 u'said anything',
 u'yes best careful',
 u'dont like',
 u'cant',
 u'really going spend entire road volantis talking futility everything',
 u'road meereen',
 u'told',
 u'quite good know',
 u'still man talent',
 u'yes showed great promise areas well',
 u'people follow leaders',
 u'find repulsive surround large comfortable boxes keep away',
 u'volantis large city',
 u'likelihood spotted increases hundredfold',
 u'im sure many new ways find saying',
 u'perfectly good face',
 u'anyone recognizes youll lose',
 u'yes',
 u'aside keep moving',
 u'thank',
 u'someone inspires priests whores worth taking seriously',
 u'wherere goin

In [391]:
Varys_Words_String = ' '.join(Varys_Words)
Varys_Words_String

u'saved life home colleague lord already drank across narrow sea talking future country imp halfman faster ways kill many things friend coward brother asked refuse kingslayer didnt dont believe saviors many admirable qualities selfpity one think never said perfect peace perhaps wont said anything yes best careful dont like cant really going spend entire road volantis talking futility everything road meereen told quite good know still man talent yes showed great promise areas well people follow leaders find repulsive surround large comfortable boxes keep away volantis large city likelihood spotted increases hundredfold im sure many new ways find saying perfectly good face anyone recognizes youll lose yes aside keep moving thank someone inspires priests whores worth taking seriously wherere going thought happy together abandoned birds sing west birds sing east information key oh know'

In [392]:
Varys_String_Length = len(Varys_Words_String)
Varys_String_Length

892

In [393]:
Varys_Sentiment = TextBlob(Varys_Words_String).sentiment
Varys_Sentiment

Sentiment(polarity=0.3559818968909878, subjectivity=0.5848747212383576)